# Watershed metrics for all Huc12 subwatersheds that intersect AWC recorded streams
Iterate over AKSSF regions and identify all HUC12 sub-watersheds that intersect an AWC recorded stream. Identify the downstream-most/outlet catchment for each Huc12 from this pool and convert the polygon to INSIDE centroid point.  Calculate the distance to coastline as the straight line distance in Km from centroid point to NHD recorded coastline and export this as a feature class/table.  Next use the outlet catchments unique identifier to query the appropriate dataset and build watersheds for each outlet catchment.  Calculate watershed metrics listed in the covariate section and export final merged csv using the catchment unique identifier field "cat_ID_con" to link the metric back to the source catchment/HUC12.  Merge watersheds together and use to calculate covariates.
## Covariates
Covariates needed for prediction on AWC-HUC12 outlets are as follows:
### Summer Precipitation
To be calculated in R using the outlet catchment centroid point feature class exported during outlet identification process.
### Watershed Slope Metrics
Regional Slope grids created in AKSSF_merge_grids.ipynb script.
Run zonal statistics on slope grid using merged watershed as zone feature.
Field names and descriptions:
* **awc_huc12s_wtd_slope_mn = mean watershed slope**
* **awc_huc12s_wtd_slope_min = min watershed slope**
* **awc_huc12s_wtd_slope_max = max watershed slope**
* **awc_huc12s_wtd_slope_sd (or cv) = standard deviation of watershed slope**
### Watershed Percent North Aspect
Regional North grids created in AKSSF_merge_grids.ipynb scripts.
North = aspects from 315-45 degrees and calculate the percentage of land area facing north for each watershed. Run tabulate area on north grid using merged watershed as zone feature and calculate percentage from area.
Field names and descriptions:
* **awc_huc12s_north_wtd = percent watershed with north aspect**
### Watershed Percent Lake Cover
Updated the Lakes/Ponds with newest version of Base NHD April 28 2023
Lakes feature classes for each network datatype (NHDPlus vs TauDEM) stored in AKSSF hydrography database on the T:
Calculate percentage of watershed that is covered by lakes/ponds using tabulate interesection between lake features and watersheds.
Field names and descriptions:
* **awc_huc12s_wtd_lake_per = percent watershed covered by lakes**
### Watershed Percent Glacier Cover
Use input glacier fc (from previous covariate calculations) stored in regional gdbs an calculate percent of watershed with glacial coverage using tabulate intersection between lake features and watersheds.
Field names and descriptions:
* **awc_huc12s_wtd_glac_per = percent watershed covered by glaciers**
### Watershed LCLD
LCLD rasters created in AKSSF_MODIS_lcld_ipynb.
Iterate over LCLD input rasters to produce yearly means for watersheds using zonal statistics.
Field names and descriptions:
* **awc_huc12s_wtd_lcld_mn_YYYY = mean lcld**


## Import modules
Set initial environments and import modules
Print system paths

In [5]:
import os, arcpy, sys,datetime, traceback

arcpy.env.overwriteOutput = True
sr = arcpy.SpatialReference(3338)  #'NAD_1983_Alaska_Albers'
arcpy.env.outputCoordinateSystem = sr
print(f'Date: {datetime.datetime.now()}')
print('imports complete')
print(f'{("-"*100)}')
print(f'sys paths {sys.path}')
print(f'{("-"*100)}')
print(f'Python Environment set to - {sys.base_exec_prefix}')
print(f'{("-"*100)}')
print (datetime.datetime.now())
outdir = os.path.dirname(os.getcwd())
print(f'CSV table output directory set to {outdir}')

Date: 2023-05-18 14:36:49.879126
imports complete
----------------------------------------------------------------------------------------------------
sys paths ['C:\\Program Files\\JetBrains\\PyCharm 2020.2.3\\plugins\\python\\helpers-pro\\jupyter_debug', 'C:\\Program Files\\JetBrains\\PyCharm 2020.2.3\\plugins\\python\\helpers\\pydev', 'C:\\Users\\dwmerrigan\\Documents\\GitHub\\AKSSF\\data_preparation\\sensitivity_drivers\\landcover', 'C:\\Program Files\\ArcGIS\\Pro\\Resources\\ArcPy', 'C:\\Users\\dwmerrigan\\Documents\\GitHub\\AKSSF', 'C:\\Program Files\\ArcGIS\\Pro\\bin\\Python\\envs\\arcgispro-py3\\python39.zip', 'C:\\Program Files\\ArcGIS\\Pro\\bin\\Python\\envs\\arcgispro-py3\\DLLs', 'C:\\Program Files\\ArcGIS\\Pro\\bin\\Python\\envs\\arcgispro-py3\\lib', 'C:\\Program Files\\ArcGIS\\Pro\\bin\\Python\\envs\\arcgispro-py3', '', 'C:\\Users\\dwmerrigan\\AppData\\Roaming\\Python\\Python39\\site-packages', 'C:\\Program Files\\ArcGIS\\Pro\\bin\\Python\\envs\\arcgispro-py3\\lib\\site-pa

## Functions
Define any functions that will be used

In [6]:
# Function to add key, value pairs to dictionary
def append_value(dict_obj, key, value):
    # Check if key exist in dict or not
    if key in dict_obj:
        # Key exist in dict.
        # Check if type of value of key is list or not
        if not isinstance(dict_obj[key], list):
            # If type is not list then make it list
            dict_obj[key] = [dict_obj[key]]
        # Append the value in list
        dict_obj[key].append(value)
    else:
        # As key is not in dict,
        # so, add key-value pair
        dict_obj[key] = value
# Function to remove parenthesis from user inputs
def replace_all(userinput, dic):
    for i, j in dic.items():
        userinput = userinput.replace(i, j)
    return userinput

# Getnull rows from numpy array
def getnull(cat_ID_con):
    nullRows = []
    nullRows.append(cat_ID_con)
    return True

#Generate unique column names
def uniquify(df_final):
    seen = set()
    for item in df_final:
        fudge = 1
        newitem = item
        while newitem in seen:
            fudge += 1
            newitem = "{}_{}".format(item, fudge)
        yield newitem
        seen.add(newitem)

# Section 1 -Set input datasets, output locations, and scratch workspaces
User to input paths for necessary input data and output locations
Scratch workspaces and output workspaces will be automatically created if they do not already exist.

In [7]:
# Get user inputs
# Used to format user inputs
inputDict = {"'":"",'"':""}

# Specify path to nhdPlus lakes
while True:
    try:
        nhdlakesinput = replace_all((input('Input path to NHDPlus lakes feature class.\nHydrography database on T: has copy\nLeave blank and hit enter to use the default location.\nDefault = D:\\Basedata\\AKSSF_Basedata\\AKSSF_Basedata.gdb\\AKSSF_NHDPlus_LakePond_alb') or 'D:\\Basedata\\AKSSF_Basedata\\AKSSF_Basedata.gdb\\AKSSF_NHDPlus_LakePond_alb'),inputDict)
        if not arcpy.Exists(nhdlakesinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            nhd_lakes_fc = nhdlakesinput
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()

print(f'NHDPlus lakes set to {nhd_lakes_fc}\n {"-"*100}')

# Specify path to nhd lakes for tau regions
while True:
    try:
        taulakesinput = replace_all((input('Input path to NHD_H_Alaska_State_GDB lakes feature class.\nHydrography database on T: has copy\nLeave blank and hit enter to use the default location.\nDefault = D:\\Basedata\\AKSSF_Basedata\\AKSSF_Basedata.gdb\\AKSSF_NHD_LakesPonds_alb') or 'D:\\Basedata\\AKSSF_Basedata\\AKSSF_Basedata.gdb\\AKSSF_NHD_LakesPonds_alb'),inputDict)
        if not arcpy.Exists(taulakesinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            tau_lakes_fc = taulakesinput
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()
print(f'NHD_H_Alaska lakes for TauDEM regions set to {nhd_lakes_fc}\n {"-"*100}')

# Specify path to coastline fc
while True:
    try:
        coastinput = replace_all((input('Input path to coastline fc.\nHydrography database on T: has copy\nLeave blank and hit enter to use the default location.\nDefault = D:\\Basedata\\AKSSF_Basedata\\AKSSF_Basedata.gdb\\NHD_H_Alaska_Coastline_alb') or 'D:\\Basedata\\AKSSF_Basedata\\AKSSF_Basedata.gdb\\NHD_H_Alaska_Coastline_alb'),inputDict)
        if not arcpy.Exists(coastinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            coast = coastinput
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()
print(f'Coastline for all regions set to {coast}\n {"-"*100}')

# Specify path to AKSSF parent directory
while True:
    try:
        datadirinput = replace_all((input('Input AKSSF parent directory containing regional sub-folders.\nLeave blank and hit enter to use the default location.\nDefault = D:\\GIS\\AKSSF\\') or 'D:\\GIS\\AKSSF'),inputDict)
        if not arcpy.Exists(datadirinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            data_dir = datadirinput
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()

print(f'AKSSF parent directory set to {data_dir}\n {"-"*100}')

# Specify path to AWC events fc
while True:
    try:
        awceventsinput = replace_all((input('Input path to awc events feature class or shapefile.\nLeave blank and hit enter to use the default location.\nDefault = D:\\GIS\\AKSSF_land_met\\AKSSF_land_met.gdb\\awcEventArcs_Intersect_H12sDiss') or "D:\\GIS\\AKSSF_land_met\\AKSSF_land_met.gdb\\awcEventArcs_Intersect_H12sDiss"), inputDict)
        if not arcpy.Exists(awceventsinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            awc_events = awceventsinput
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()
print(f'AWC events feature class set to {awc_events}\n {"-"*100}')

# Enter output destination  - to create working folders and gdbs
while True:
    try:
        temppathinput = replace_all((input('Input path to create working folders.\nLeave blank and hit enter to use the default location.\nDefault = D:\\GIS\\') or 'D:\\GIS\\'),inputDict)
        if not arcpy.Exists(temppathinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            temp_path = temppathinput
            print(f'Output locations will be created at {temp_path}\n {"-"*100}')
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()


# Path to lcld rasters
# Enter output destination  - to create working folders and gdbs
while True:
    try:
        lcldfolinput = replace_all((input('Input path to LCLD raster parent folder.\nLeave blank and hit enter to use the default location.\nDefault = D:\\Basedata\\LCLD_rasters_archive\\') or 'D:\\Basedata\\LCLD_rasters_archive'),inputDict)
        if not arcpy.Exists(lcldfolinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            lcld_folder = lcldfolinput
            print(f'LCLD subfolders located at {lcld_folder}\n {"-"*100}')
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()

# Threshold in meters to use as cutoff for selecting awcEvents polylines
while True:
    try:
        awcthreshinput = (input('Input minimum awc stream length in meters to use as threshold for selection.\nLeave blank and hit enter to use the default value of 500 meters.\nDefault = 500') or 500)
        if not type(awcthreshinput) == int or type(awcthreshinput) == float:
            print('Please enter a valid number')
            continue
        else:
            awcthresh = awcthreshinput
            print(f'Only stream segments greater than {awcthresh} meters will be used for selection\n {"-"*100}')
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()

# Output Directory
while True:
    try:
        dirname = (input('Input name of directory being created for outputs'))
        if not dirname:
            print(f'Must not be blank\n {"-"*100}')
            break
        else:
            dirname = dirname
            tempgdbname = dirname + '.gdb'
            temp_dir = os.path.join(temp_path, dirname)
            outdir = temp_dir
            outcheck = os.path.join(temp_dir, tempgdbname)
            print(f'output directory set to {temp_dir} output gdb = {outcheck}' )
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()

# Create temporary working gdb
if not arcpy.Exists(temp_dir):
    os.makedirs(temp_dir)
else:
    print(f'Working Folder already created {temp_dir}\n {"-"*100}')

if arcpy.Exists(outcheck):
    print (f'Output location already exists {outcheck}\n {"-"*100}')
    outgdb = outcheck
if not arcpy.Exists(outcheck):
    print(f'Creating output GDB\n {"-"*100}')
    tempgdb = arcpy.CreateFileGDB_management(temp_dir,tempgdbname)
    print (f'Output geodatabase created at {outcheck}\n {"-"*100}')
    outgdb = tempgdb.getOutput(0)


NHDPlus lakes set to D:\Basedata\AKSSF_Basedata\AKSSF_Basedata.gdb\AKSSF_NHDPlus_LakePond_alb
 ----------------------------------------------------------------------------------------------------
NHD_H_Alaska lakes for TauDEM regions set to D:\Basedata\AKSSF_Basedata\AKSSF_Basedata.gdb\AKSSF_NHDPlus_LakePond_alb
 ----------------------------------------------------------------------------------------------------
Coastline for all regions set to D:\Basedata\AKSSF_Basedata\AKSSF_Basedata.gdb\NHD_H_Alaska_Coastline_alb
 ----------------------------------------------------------------------------------------------------
AKSSF parent directory set to D:\GIS\AKSSF
 ----------------------------------------------------------------------------------------------------
AWC events feature class set to D:\GIS\AKSSF_land_met\AKSSF_land_met.gdb\awcEventArcs_Intersect_H12sDiss
 ----------------------------------------------------------------------------------------------------
Output locations will be

## Set and create local copies of additional input data


In [8]:

import arcpy
arcpy.env.overwriteOutput = True
sr = arcpy.SpatialReference(3338)  #'NAD_1983_Alaska_Albers'
arcpy.env.outputCoordinateSystem = sr

nhdplusfol = []
tahuc12=[]

# Create and set HUC12 data if it does not already exist
nhdplushucs = os.path.join(outgdb, 'NHDPlusHUC12')
tauhucs = os.path.join(outgdb, 'NHD_H_HUC12')

if not arcpy.Exists(tauhucs):
    print(f'Huc12 data for Tau Regions not yet created')
    #Enter path to WBDHU12 from NHD_H gdb
    while True:
        try:
            tauhuc12input = replace_all((input('Input path to source WBDHU12 for state of Alaska.\nLeave blank and hit enter to use the default location.\nDefault = D:\\Basedata\\2023\\NHD_H_Alaska_State_GDB.gdb\\WBD\\WBDHU12') or 'D:\\Basedata\\2023\\NHD_H_Alaska_State_GDB.gdb\\WBD\\WBDHU12'),inputDict)
            if not arcpy.Exists(tauhuc12input):
                print('Path specified does not exist!\nPlease re-enter a valid path')
                continue
            else:
                tauhuc12 = tauhuc12input
                arcpy.CopyFeatures_management(tauhuc12,tauhucs)
                print(f'WBD Huc12  copied to {tauhucs}\n {"-"*100}')
                break
        except KeyboardInterrupt:
            print('interrupted!')
            sys.exit()

else:
    print(f'Tau Region Hucs {tauhucs} located and exists = {arcpy.Exists(tauhucs)}')
    tauhucs = os.path.join(outgdb, 'NHD_H_HUC12')

if not arcpy.Exists(nhdplushucs):
    print(f'Huc12 data for NHDPlus Regions not yet created')
    #Enter NHDplus data folder
    while True:
        try:
            nhdplusfolinput = replace_all((input('Input path to source NHDPlus parent folder.\nLeave blank and hit enter to use the default location.\nDefault = D:\\Basedata\\NHDPlus') or 'D:\\Basedata\\NHDPlus'),inputDict)
            if not arcpy.Exists(nhdplusfolinput):
                print('Path specified does not exist!\nPlease re-enter a valid path')
                continue
            else:
                nhdplusfol = nhdplusfolinput
                print(f'NHD HUC12 will be copied to {nhdplushucs}\n {"-"*100}')
                hucs = []
                walk = arcpy.da.Walk(nhdplusfol, datatype="FeatureClass", type="Polygon")

                for dirpath, dirnames, filenames in walk:
                    for filename in filenames:
                        if filename == 'WBDHU12':
                            hucs.append(os.path.join(dirpath, filename))
                arcpy.Merge_management(hucs,nhdplushucs,'','ADD_SOURCE_INFO')
                break
        except KeyboardInterrupt:
            print('interrupted!')
            sys.exit()
else:
    print(f'NHDPlus Hucs {nhdplushucs} located and exists = {arcpy.Exists(nhdplushucs)}')
    nhdplushucs = os.path.join(outgdb, 'NHDPlusHUC12')

print(f'process complete {datetime.datetime.now()}')

Tau Region Hucs D:\GIS\outputs_20230518\outputs_20230518.gdb\NHD_H_HUC12 located and exists = True
Huc12 data for NHDPlus Regions not yet created
NHD HUC12 will be copied to D:\GIS\outputs_20230518\outputs_20230518.gdb\NHDPlusHUC12
 ----------------------------------------------------------------------------------------------------
process complete 2023-05-18 14:38:19.843882


# Section 2 - Identify outlet catchments by region
Identify downstream-most catchment for each Huc 12
 * Select by location and select catchment with most us contributing area
    * NHDPlus
        * Use update cursor to join TotalDrainageAreaSqKm from vaa table to catchment
        * Find max value from selection and save as outlet catchment for that HUC12
    * TauDEM
        * DSContArea - Drainage area at the downstream end of the link. Generally this is one grid cell upstream of the downstream end because the drainage area at the downstream end grid cell includes the area of the stream being joined.
 * Generate Centroid point and append to centroid dataset
    * Retain cat_id and Huc12-id
 * Append to HUC12 catchment dataset
 * **NOTE- Since the HUC12 Boundaries do not align perfectly with TauDEM (and at least one NHDPlus copper river: 190201040109) catchments, the outlet catchment that is identified may be further upstream than we would like.**


## Set Qc dictionaries and lists if necessary
Initially flagged for review if length of awc in HUC12 was < threshold of 500 meters to identify HUCS that may have been chosen in error due to differences between AWC streams and NHDPlus/Tau Streams and Catchments

Drop the following HUCs completely as they are large Coastal HUCs:
Red River-Frontal Pacific Ocean	190207011108
Fort Island-Gulf of Alaska	190207011206
Uyak Bay-Frontal Shelikof Strait	190207010708
Sacramento River-Frontal Pacific Ocean	190207011905
Cape Uganik-Shelikof Strait	190207010502
Sevenmile Beach-Frontal Shelikof Strait	190207010814
Tonki Cape Peninsula-Frontal Marmot Bay	190207011410
Chiniak Bay	190207011506
Steep Cape-Frontal Shelikof Strait	190207010208
Nushagak Bay-Frontal Bristol Bay	190303060803
Norseman Lake-Frontal Bristol Bay	190303051505
Togiak Bay-Frontal Bristol Bay	190303051103
Right Hand Point-Frontal Bristol Bay	190303051907
Hagemeister Island-Frontal Bristol Bay	190303052002
Kvichack Bay-Frontal Bristol Bay	190302062311



In [9]:
# Change outdir to temp_dir if QC otherwise comment out
#outdir = temp_dir
print(f'CSV table output directory set to {outdir}')

# key = cat_ID_con:vals [new cat_ID_con (may stay the same or pick a new catchment that best represents the HUC12), AWCCODE,HUC12, ReviewCode(1 - Keep but change awc relation, 2 - choose new catchment and re-run watersheds, 3 - drop, 4 - Additional Review), 0 - leave as is]
awcQcDict = {}
# Update reviewDict to match qcDict from sp_ls script after initial/subsequent reviews (Only wrong catchments and drops)
reviewDict = {'Kodiak_74624': ['Kodiak_75104', '252-35-10020', '190207010501', 2],
'Prince_William_Sound_33396':['Prince_William_Sound_32806','226-20-16174','190202012505',2],
'Bristol_Bay_4063777': ['Bristol_Bay_4062777', '325-20-10030', '190303060206', 2],
'Prince_William_Sound_42595':['Prince_William_Sound_41025','224-40-14900','190202012310',2],
'Prince_William_Sound_46513': ['Prince_William_Sound_29994', '221-10-10020', '190202010200', 2],
'Prince_William_Sound_43535': ['Prince_William_Sound_685', '224-40-14920', '190202012307', 2],
'Prince_William_Sound_34455': ['Prince_William_Sound_28465', '226-20-16862', '190202030208', 2],
'Prince_William_Sound_30344': ['Prince_William_Sound_45273', '224-10-14496', '190202012003', 2],
'Prince_William_Sound_23854': ['Prince_William_Sound_24654', '222-40-12960', '190202030202', 2],
'Prince_William_Sound_22134': ['Prince_William_Sound_23574', '222-30-12933', '190202030201', 2],
'Prince_William_Sound_31916': ['Prince_William_Sound_33036', '226-20-16170', '190202012506', 2],
'Prince_William_Sound_76692': ['Prince_William_Sound_71142', '221-50-11170', '190202011109', 2],
'Prince_William_Sound_18747': ['Prince_William_Sound_18967', '227-30-17780', '190202030702', 2],
'Prince_William_Sound_27856': ['Prince_William_Sound_19416', '226-40-16851', '190202030209', 2],
'Prince_William_Sound_30084': ['Prince_William_Sound_29704', '224-10-14540', '190202012104', 2],
'Prince_William_Sound_30546': ['Prince_William_Sound_16467', '226-50-16154', '190202030503', 2],
'Prince_William_Sound_43775': ['Prince_William_Sound_39255', '224-40-14904', '190202012306', 2],
'Prince_William_Sound_43255': ['Prince_William_Sound_37935', '226-20-16010', '190202012508', 2],
'Prince_William_Sound_44273': ['Prince_William_Sound_35343', '223-40-13390', '190202011605', 2],
'Prince_William_Sound_44605': ['Prince_William_Sound_37955', '226-20-16950', '190202030207', 2],
'Prince_William_Sound_45925': ['Prince_William_Sound_28734', '224-40-14860', '190202012304', 2],
'Prince_William_Sound_46623': ['Prince_William_Sound_36553', '224-10-14510', '190202012001', 2],
'Prince_William_Sound_70762': ['Prince_William_Sound_61812', '222-10-12030', '190202011308', 2],
'Prince_William_Sound_60732': ['Prince_William_Sound_75002', '223-30-13140', '190202011805', 2],
'Prince_William_Sound_77992': ['Prince_William_Sound_75842', '224-10-14020', '190202011906', 2],
'Prince_William_Sound_80112': ['Prince_William_Sound_78912', '222-10-12040', '190202011307', 2],
'Prince_William_Sound_81631': ['Prince_William_Sound_72242', '222-20-12640', '190202011505', 2],
'Prince_William_Sound_89681': ['Prince_William_Sound_75151', '221-60-11520', '190202011103', 2],
'Prince_William_Sound_43933': ['Prince_William_Sound_44113', '221-20-10350', '190202010402', 2],
'Kodiak_79862': ['Kodiak_78362', '252-33-10020', '190207011404', 2],
'Kodiak_79034': ['Kodiak_75664', '253-11-10040', '190207010407', 2],
'Kodiak_77952': ['Kodiak_75052', '251-82-10029', '190207011202', 2],
'Kodiak_79842': ['Kodiak_79852', '252-33-10010', '190207011403', 2],
'Kodiak_47797': ['Kodiak_47317', '258-54-10012', '190207011805', 2],
'Kodiak_49837': ['Kodiak_46347', '257-50-10030', '190207011002', 2],
'Kodiak_103116': ['Kodiak_99996', '254-20-10010', '190207010708', 2],
'Bristol_Bay_5029122': ['Bristol_Bay_5029102', '326-00-10400-2091-3201', '190303050503', 2],
'Bristol_Bay_5028612': ['Bristol_Bay_5028672', '326-00-10400-2163', '190303050402', 2],
'Bristol_Bay_5026052': ['Bristol_Bay_5026192', '326-00-10400-2178', '190303050401', 2],
'Bristol_Bay_4120132': ['Bristol_Bay_4120152', '325-30-10100-2202', '190303021003', 2],
'Bristol_Bay_4116442': ['Bristol_Bay_4116432', '325-30-10100-2249-3142-4163', '190303011304', 2],
'Bristol_Bay_4107454': ['Bristol_Bay_4105234', '325-30-10100-2202-3044', '190303021609', 2],
'Bristol_Bay_4105964': ['Bristol_Bay_4099714', '325-30-10100-2202-3080', '190303021102', 2],
'Bristol_Bay_4102223': ['Bristol_Bay_4093963', '325-30-10100-2202-3125', '190303020903', 2],
'Bristol_Bay_4100083': ['Bristol_Bay_4068633', '325-30-10100-2202-3076', '190303021501', 2],
'Bristol_Bay_4099023': ['Bristol_Bay_4093813', '325-30-10100-2202-3080-4029-5039-6045', '190303021203', 2],
'Bristol_Bay_4098664': ['Bristol_Bay_4098614', '325-30-10100-2202-3080', '190303021101', 2],
'Bristol_Bay_4098081': ['Bristol_Bay_4091891', '325-30-10100-2202-3420', '190303020708', 2],
'Bristol_Bay_4097981': ['Bristol_Bay_4095631', '325-30-10100-2202-3446', '190303020605', 2],
'Bristol_Bay_4097911': ['Bristol_Bay_4097941', '325-30-10100-2202', '190303020705', 2],
'Kodiak_125845': ['Kodiak_126005', '253-12-10020', '190207010403', 2],
'Bristol_Bay_4119952': ['Bristol_Bay_4119972', '325-30-10100-2202', '190303020710', 2],
'Bristol_Bay_4096891': ['Bristol_Bay_4096991', '325-30-10100-2202-3510', '190303020503', 2],
'Bristol_Bay_4095641': ['Bristol_Bay_4055540', '325-30-10100-2202', '190303020209', 2],
'Bristol_Bay_4094233': ['Bristol_Bay_4090253', '325-30-10100-2202-3080-4058', '190303021303', 2],
'Bristol_Bay_4093891': ['Bristol_Bay_4093871', '325-30-10100', '190303010304', 2],
'Bristol_Bay_4090071': ['Bristol_Bay_4088891', '325-30-10100-2202-3510-4089', '190303020401', 2],
'Bristol_Bay_4090011': ['Bristol_Bay_4089921', '325-30-10100', '190303010101', 2],
'Bristol_Bay_4108222': ['Bristol_Bay_4108242', '325-30-10100-2299', '190303010802', 2],
'Bristol_Bay_4107994': ['Bristol_Bay_4108014', '325-30-10100', '190303012008', 2],
'Bristol_Bay_4107732': ['Bristol_Bay_4090833', '325-30-10100-2311', '190303010907', 2],
'Bristol_Bay_4083715': ['Bristol_Bay_4083725', '325-30-10100-2129-3040', '190303030406', 2],
'Bristol_Bay_4076065': ['Bristol_Bay_4076505', '325-30-10100-2031-3118-4006', '190303040304', 2],
'Bristol_Bay_4073646': ['Bristol_Bay_4073516', '325-30-10100-2031-3028', '190303040405', 2],
'Bristol_Bay_4071596': ['Bristol_Bay_4071606', '325-20-10030-2009', '190303060102', 2],
'Bristol_Bay_4068006': ['Bristol_Bay_4068046', '325-30-10100-2112', '190303030702', 2],
'Bristol_Bay_4066027': ['Bristol_Bay_4066047', '325-30-10100', '190303031007', 2],
'Bristol_Bay_4065827': ['Bristol_Bay_4065837', '325-30-10100', '190303030906', 2],
'Bristol_Bay_4065317': ['Bristol_Bay_4032098', '325-10-10010-2023', '190303060404', 2],
'Bristol_Bay_4063637': ['Bristol_Bay_4063647', '325-20-10030', '190303060204', 2],
'Bristol_Bay_4059867': ['Bristol_Bay_4071786', '325-30-10100-2110-3115-4403', '190303030602', 2],
'Bristol_Bay_4055510': ['Bristol_Bay_4055500', '325-30-10100-2202-3545', '190303020208', 2],
'Bristol_Bay_4054660': ['Bristol_Bay_4084501', '325-30-10100-2497-3226-4080', '190303010404', 2],
'Bristol_Bay_3033946': ['Bristol_Bay_3033956', '324-20-10140-2200', '190302040803', 2],
'Bristol_Bay_3033656': ['Bristol_Bay_3033806', '324-20-10140-2194-3039', '190302040906', 2],
'Bristol_Bay_3031465': ['Bristol_Bay_3031545', '324-20-10140-2245', '190302040605', 2],
'Bristol_Bay_3024543': ['Bristol_Bay_3024533', '324-20-10140', '190302041502', 2],
'Bristol_Bay_3019031': ['Bristol_Bay_3018051', '324-20-10140-2245-3029-4113-5011', '190302040206', 2],
'Bristol_Bay_2089766': ['Bristol_Bay_2088336', '324-10-10150-2053', '190302061505', 2],
'Bristol_Bay_2088346': ['Bristol_Bay_2069835', '324-10-10150-2097', '190302061301', 2],
'Bristol_Bay_2085482': ['Bristol_Bay_2084502', '324-10-10150-2207-3173-4050', '190302051012', 2],
'Bristol_Bay_2085476': ['Bristol_Bay_2068087', '324-10-10150-2010-3035', '190302062001', 2],
'Bristol_Bay_2084722': ['Bristol_Bay_2083292', '324-10-10150-2207-3301', '190302050304', 2],
'Bristol_Bay_2081566': ['Bristol_Bay_2081546', '324-10-10150-2136', '190302061001', 2],
'Bristol_Bay_2079192': ['Bristol_Bay_2079202', '324-10-10150-2207-3214', '190302050505', 2],
'Bristol_Bay_2074484': ['Bristol_Bay_2072044', '324-10-10150-2267', '190302060302', 2],
'Bristol_Bay_2074434': ['Bristol_Bay_2074294', '324-10-10150-2273', '190302060902', 2],
'Bristol_Bay_2073204': ['Bristol_Bay_2073174', '324-10-10150-2402-3025', '190302060203', 2],
'Bristol_Bay_2070037': ['Bristol_Bay_2064327', '324-10-10150-2010-3030', '190302062005', 2],
'Bristol_Bay_2070227': ['Bristol_Bay_2070217', '324-10-10150', '190302062204', 2],
'Bristol_Bay_2040601': ['Bristol_Bay_2040341', '324-10-10150-2207-3301', '190302050301', 2],
'Bristol_Bay_1030062': ['Bristol_Bay_1030072', '322-10-10080-2016', '190302030402', 2],
'Bristol_Bay_1022284': ['Bristol_Bay_1022264', '322-10-10080-2058', '190302031103', 2],
'Bristol_Bay_1006858': ['Bristol_Bay_1006868', '322-10-10080-2292', '190302030205', 2],
'Kodiak_80022': ['Kodiak_80022', '251-40-10030', '190207010202', 1],
'Bristol_Bay_4051420': ['Bristol_Bay_4051420', '325-30-10100-2202-3901', '190303020106', 1],
'Kodiak_77372': ['Kodiak_77372', '251-30-10020', '190207010204', 1],
'Kodiak_79642': ['Kodiak_79642', '251-30-10010', '190207010203', 1],
'Kodiak_63963': ['Kodiak_63963', '251-20-10020', '190207010205', 1],
'Kodiak_49617': ['Kodiak_49617', '257-40-10030', '190207010906', 1],
'Kodiak_47207': ['Kodiak_47207', '258-51-10010', '190207011806', 1],
'Kodiak_46167': ['Kodiak_46167', '258-55-10040', '190207011804', 1],
'Kodiak_14958': ['Kodiak_14958', '258-60-10020', '190207011903', 1],
'Kodiak_14858': ['Kodiak_14858', '257-60-10050', '190207011004', 1],
'Kodiak_131775': ['Kodiak_131775', '254-30-10010', '190207010705', 1],
'Kodiak_130995': ['Kodiak_130995', '255-10-10010', '190207010808', 1],
'Kodiak_125235': ['Kodiak_125235', '254-30-10020', '190207010706', 1],
'Kodiak_124215': ['Kodiak_124215', '259-41-10020', '190207011608', 1],
'Kodiak_122785': ['Kodiak_122785', '259-25-10040', '190207011505', 1],
'Kodiak_122415': ['Kodiak_122415', '253-12-10010', '190207010401', 1],
'Kodiak_104296': ['Kodiak_104296', '258-52-10010', '190207011705', 1],
'Kodiak_103266': ['Kodiak_103266', '254-20-10020', '190207010701', 1],
'Kodiak_101826': ['Kodiak_101826', '258-20-10040', '190207011704', 1],
'Kodiak_75624': ['Kodiak_75624', '259-10-10015', '190207011409', 1],
'Kodiak_75194': ['Kodiak_75194', '252-38-10020', '190207011304', 1],
'Kodiak_63943': ['Kodiak_63943', '252-34-10020-2019-3009', '190207011407', 1],
'Kodiak_48997': ['Kodiak_48997', '257-40-10030-2002', '190207010908', 1],
'Kodiak_47187': ['Kodiak_47187', '258-40-10012', '190207011902', 1],
'Kodiak_13958': ['Kodiak_13958', '258-80-10140-2006', '190207011904', 1],
'Kodiak_125115': ['Kodiak_125115', '259-41-10050', '190207011605', 1],
'Kodiak_124945': ['Kodiak_124945', '259-23-10010', '190207011503', 1],
'Kodiak_124065': ['Kodiak_124065', '259-24-10020', '190207011504', 1],
'Kodiak_123415': ['Kodiak_123415', '259-41-10040', '190207011606', 1],
'Kodiak_108606': ['Kodiak_108606', '256-40-10010', '190207010810', 1],
'Kodiak_107376': ['Kodiak_107376', '256-20-10010', '190207011101', 1],
'Kodiak_105086': ['Kodiak_105086', '256-20-10010-2034', '190207011102', 1],
'Kodiak_103196': ['Kodiak_103196', '256-20-10010-2016', '190207011104', 1],
'Kodiak_103016': ['Kodiak_103016', '258-52-10040', '190207011801', 1],
'Kodiak_102106': ['Kodiak_102106', '256-30-10010', '190207011106', 1],
'Kodiak_101146': ['Kodiak_101146', '258-20-10069', '190207011702', 1],
'Kodiak_100826': ['Kodiak_100826', '255-10-10010-2059', '190207010802', 1],
'Bristol_Bay_5038685': ['Bristol_Bay_5038685', '326-00-10400', '190303050904', 1],
'Bristol_Bay_5021956': ['Bristol_Bay_5021956', '326-30-10500', '190303051305', 1],
'Bristol_Bay_4112382': ['Bristol_Bay_4112382', '325-30-10100-2202-3281-4011', '190303020807', 1],
'Bristol_Bay_5034833': ['Bristol_Bay_5034833', '326-00-10400-2108', '190303050305', 1],
'Bristol_Bay_5034423': ['Bristol_Bay_5034423', '326-00-10400-2081', '190303050605', 1],
'Bristol_Bay_5033295': ['Bristol_Bay_5033295', '326-30-10500', '190303051301', 1],
'Bristol_Bay_5033213': ['Bristol_Bay_5033213', '326-00-10400-2091', '190303050506', 1],
'Bristol_Bay_5033104': ['Bristol_Bay_5033104', '326-00-10400-2058', '190303050703', 1],
'Bristol_Bay_5033043': ['Bristol_Bay_5033043', '326-00-10400-2108-3028', '190303050304', 1],
'Bristol_Bay_5030574': ['Bristol_Bay_5030574', '326-10-10020', '190303051701', 1],
'Bristol_Bay_5030514': ['Bristol_Bay_5030514', '326-00-10400-2047-3021', '190303050802', 1],
'Bristol_Bay_5021406': ['Bristol_Bay_5021406', '326-10-10600-2006', '190303051602', 1],
'Bristol_Bay_5019001': ['Bristol_Bay_5019001', '326-00-10400-2189-3012', '190303050202', 1],
'Bristol_Bay_4114362': ['Bristol_Bay_4114362', '325-30-10100-2481', '190303010902', 1],
'Bristol_Bay_4114302': ['Bristol_Bay_4114302', '325-30-10100-2202-3281', '190303020808', 1],
'Bristol_Bay_4111042': ['Bristol_Bay_4111042', '325-30-10100-2435-3230', '190303010504', 1],
'Bristol_Bay_4110612': ['Bristol_Bay_4110612', '325-30-10100-2435-3238', '190303010502', 1],
'Bristol_Bay_4110112': ['Bristol_Bay_4110112', '325-30-10100-2481-3020', '190303010901', 1],
'Bristol_Bay_4107154': ['Bristol_Bay_4107154', '325-30-10100-2249', '190303011804', 1],
'Bristol_Bay_4106774': ['Bristol_Bay_4106774', '325-30-10100-2202-3043', '190303021703', 1],
'Bristol_Bay_4106762': ['Bristol_Bay_4106762', '325-30-10100-2350', '190303010701', 1],
'Bristol_Bay_4105772': ['Bristol_Bay_4105772', '325-30-10100-2580-3016', '190303010202', 1],
'Bristol_Bay_4103902': ['Bristol_Bay_4103902', '325-30-10100-2350-3301', '190303010702', 1],
'Bristol_Bay_4101893': ['Bristol_Bay_4101893', '325-30-10100-2202', '190303021005', 1],
'Bristol_Bay_4099614': ['Bristol_Bay_4099614', '325-30-10100-2241', '190303012003', 1],
'Bristol_Bay_4099464': ['Bristol_Bay_4099464', '325-30-10100-2249-3025', '190303011801', 1],
'Bristol_Bay_4099444': ['Bristol_Bay_4099444', '325-30-10100-2241-3015', '190303012002', 1],
'Bristol_Bay_4098683': ['Bristol_Bay_4098683', '325-30-10100-2249-3111', '190303011702', 1],
'Bristol_Bay_4098534': ['Bristol_Bay_4098534', '325-30-10100-2202-3044', '190303021601', 1],
'Bristol_Bay_4098514': ['Bristol_Bay_4098514', '325-30-10100-2129-3140', '190303030403', 1],
'Bristol_Bay_4097764': ['Bristol_Bay_4097764', '325-30-10100-2202-3044-4065', '190303021603', 1],
'Bristol_Bay_4097543': ['Bristol_Bay_4097543', '325-30-10100-2202-3080-4083', '190303021103', 1],
'Bristol_Bay_4097174': ['Bristol_Bay_4097174', '325-30-10100-2243', '190303012001', 1],
'Bristol_Bay_4097073': ['Bristol_Bay_4097073', '325-30-10100-2202-3080-4071', '190303021301', 1],
'Bristol_Bay_4096733': ['Bristol_Bay_4096733', '325-30-10100-2249-3048', '190303011603', 1],
'Bristol_Bay_4095964': ['Bristol_Bay_4095964', '325-30-10100-2202-3044-4053', '190303021607', 1],
'Bristol_Bay_4094641': ['Bristol_Bay_4094641', '325-30-10100-2202-3446-4052', '190303020603', 1],
'Bristol_Bay_4093591': ['Bristol_Bay_4093591', '325-30-10100-2555', '190303010303', 1],
'Bristol_Bay_4092891': ['Bristol_Bay_4092891', '325-30-10100', '190303010109', 1],
'Bristol_Bay_4092121': ['Bristol_Bay_4092121', '325-30-10100-2620', '190303010108', 1],
'Bristol_Bay_4091781': ['Bristol_Bay_4091781', '325-30-10100-2497-3226', '190303010405', 1],
'Bristol_Bay_4089713': ['Bristol_Bay_4089713', '325-30-10100-2280', '190303011007', 1],
'Bristol_Bay_4089671': ['Bristol_Bay_4089671', '325-30-10100-2202-3281-4020-5510', '190303020805', 1],
'Bristol_Bay_4088865': ['Bristol_Bay_4088865', '325-30-10100-2202', '190303021708', 1],
'Bristol_Bay_4118552': ['Bristol_Bay_4118552', '325-30-10100-2435', '190303010603', 1],
'Bristol_Bay_4106152': ['Bristol_Bay_4106152', '325-30-10100-2311-3102', '190303010906', 1],
'Bristol_Bay_4087083': ['Bristol_Bay_4087083', '325-30-10100-2259-3312', '190303011008', 1],
'Bristol_Bay_4087071': ['Bristol_Bay_4087071', '325-30-10100-2202-3510-4164', '190303020307', 1],
'Bristol_Bay_4086803': ['Bristol_Bay_4086803', '325-30-10100-2202-3080-4029-5050', '190303021201', 1],
'Bristol_Bay_4086795': ['Bristol_Bay_4086795', '325-30-10100-2129', '190303030503', 1],
'Bristol_Bay_4086751': ['Bristol_Bay_4086751', '325-30-10100-2202-3446-4021', '190303020604', 1],
'Bristol_Bay_4085381': ['Bristol_Bay_4085381', '325-30-10100-2202-3281', '190303020801', 1],
'Bristol_Bay_4085325': ['Bristol_Bay_4085325', '325-30-10100-2129-3050', '190303030404', 1],
'Bristol_Bay_4084971': ['Bristol_Bay_4084971', '325-30-10100-2575', '190303010301', 1],
'Bristol_Bay_4084941': ['Bristol_Bay_4084941', '325-30-10100-2497-3019', '190303010408', 1],
'Bristol_Bay_4084581': ['Bristol_Bay_4084581', '325-30-10100-2702', '190303010105', 1],
'Bristol_Bay_4084315': ['Bristol_Bay_4084315', '325-30-10100-2129-3040', '190303030407', 1],
'Bristol_Bay_4083471': ['Bristol_Bay_4083471', '325-30-10100-2497-3031', '190303010406', 1],
'Bristol_Bay_4082741': ['Bristol_Bay_4082741', '325-30-10100-2202-3281-4101', '190303020802', 1],
'Bristol_Bay_4080805': ['Bristol_Bay_4080805', '325-30-10100-2129-3020', '190303030506', 1],
'Bristol_Bay_4080635': ['Bristol_Bay_4080635', '325-30-10100-2190-3301', '190303030102', 1],
'Bristol_Bay_4080545': ['Bristol_Bay_4080545', '325-30-10100-2141-3111', '190303030304', 1],
'Bristol_Bay_4075046': ['Bristol_Bay_4075046', '325-10-10010-2071', '190303060301', 1],
'Bristol_Bay_4072656': ['Bristol_Bay_4072656', '325-10-10010-2071-3019', '190303060304', 1],
'Bristol_Bay_4067386': ['Bristol_Bay_4067386', '325-30-10100-2031-3028-4012', '190303040404', 1],
'Bristol_Bay_4066846': ['Bristol_Bay_4066846', '325-10-10010-2087', '190303060306', 1],
'Bristol_Bay_4066507': ['Bristol_Bay_4066507', '325-30-10100', '190303031106', 1],
'Bristol_Bay_4065337': ['Bristol_Bay_4065337', '325-10-10010', '190303060604', 1],
'Bristol_Bay_4063687': ['Bristol_Bay_4063687', '325-30-10100-2080-3010', '190303030905', 1],
'Bristol_Bay_4063447': ['Bristol_Bay_4063447', '325-30-10100-2101', '190303030805', 1],
'Bristol_Bay_4062937': ['Bristol_Bay_4062937', '325-30-10100-2060-3038', '190303031003', 1],
'Bristol_Bay_4051080': ['Bristol_Bay_4051080', '325-30-10100-2202', '190303020102', 1],
'Bristol_Bay_4050550': ['Bristol_Bay_4050550', '325-30-10100-2202-3590-4021', '190303020205', 1],
'Bristol_Bay_4050230': ['Bristol_Bay_4050230', '325-30-10100-2202-3571', '190303020207', 1],
'Bristol_Bay_4034378': ['Bristol_Bay_4034378', '325-10-10010', '190303060606', 1],
'Bristol_Bay_4033648': ['Bristol_Bay_4033648', '325-10-10010-2015', '190303060504', 1],
'Bristol_Bay_3034116': ['Bristol_Bay_3034116', '324-20-10140-2232', '190302040705', 1],
'Bristol_Bay_3032286': ['Bristol_Bay_3032286', '324-20-10140-2076-3051', '190302041108', 1],
'Bristol_Bay_3024783': ['Bristol_Bay_3024783', '324-20-10140', '190302041503', 1],
'Bristol_Bay_3024213': ['Bristol_Bay_3024213', '324-20-10140-2050', '190302041307', 1],
'Bristol_Bay_3023733': ['Bristol_Bay_3023733', '324-20-10140-2039', '190302041403', 1],
'Bristol_Bay_3021962': ['Bristol_Bay_3021962', '324-20-10140-2055', '190302041201', 1],
'Bristol_Bay_3021744': ['Bristol_Bay_3021744', '324-20-10140-2245-3029-4006-5015', '190302040304', 1],
'Bristol_Bay_3016301': ['Bristol_Bay_3016301', '324-20-10140-2039-3038', '190302041401', 1],
'Bristol_Bay_3006179': ['Bristol_Bay_3006179', '324-20-10140-2076-3124', '190302041102', 1],
'Bristol_Bay_2088616': ['Bristol_Bay_2088616', '324-10-10150-2097', '190302061303', 1],
'Bristol_Bay_2087446': ['Bristol_Bay_2087446', '324-10-10150-2053-3029', '190302061503', 1],
'Bristol_Bay_2086386': ['Bristol_Bay_2086386', '324-10-10150-2010-3115', '190302061604', 1],
'Bristol_Bay_2083946': ['Bristol_Bay_2083946', '324-10-10150-2131-3015', '190302061207', 1],
'Bristol_Bay_2082873': ['Bristol_Bay_2082873', '324-10-10150-2267-3020', '190302060301', 1],
'Bristol_Bay_2082862': ['Bristol_Bay_2082862', '324-10-10150-2207-3203', '190302050608', 1],
'Bristol_Bay_2082856': ['Bristol_Bay_2082856', '324-10-10150-2136', '190302061003', 1],
'Bristol_Bay_2082586': ['Bristol_Bay_2082586', '324-10-10150-2132', '190302061103', 1],
'Bristol_Bay_2081436': ['Bristol_Bay_2081436', '324-10-10150-2010-3115-4021', '190302061603', 1],
'Bristol_Bay_2080866': ['Bristol_Bay_2080866', '324-10-10150-2053-3011', '190302061504', 1],
'Bristol_Bay_2076254': ['Bristol_Bay_2076254', '324-10-10150-2261', '190302060904', 1],
'Bristol_Bay_2075404': ['Bristol_Bay_2075404', '324-10-10150-2341', '190302060104', 1],
'Bristol_Bay_2074724': ['Bristol_Bay_2074724', '324-10-10150-2183-3010', '190302060703', 1],
'Bristol_Bay_2070527': ['Bristol_Bay_2070527', '324-10-10150', '190302062208', 1],
'Bristol_Bay_2070127': ['Bristol_Bay_2070127', '324-10-10150-2010', '190302062008', 1],
'Bristol_Bay_2069504': ['Bristol_Bay_2069504', '324-10-10150-2131', '190302061201', 1],
'Bristol_Bay_2069334': ['Bristol_Bay_2069334', '324-10-10150-2167', '190302060913', 1],
'Bristol_Bay_2069144': ['Bristol_Bay_2069144', '324-10-10150-2402-3014', '190302060206', 1],
'Bristol_Bay_2068895': ['Bristol_Bay_2068895', '324-10-10150-2131', '190302061205', 1],
'Bristol_Bay_2068715': ['Bristol_Bay_2068715', '324-10-10150-2131-3133', '190302061203', 1],
'Bristol_Bay_2068474': ['Bristol_Bay_2068474', '324-10-10150-2167', '190302060912', 1],
'Bristol_Bay_2067465': ['Bristol_Bay_2067465', '324-10-10150-2131', '190302061202', 1],
'Bristol_Bay_2066734': ['Bristol_Bay_2066734', '324-10-10150-2402-3040', '190302060202', 1],
'Bristol_Bay_2064385': ['Bristol_Bay_2064385', '324-10-10150-2097-3076', '190302061302', 1],
'Bristol_Bay_2064245': ['Bristol_Bay_2064245', '324-10-10150-2196-3008', '190302060604', 1],
'Bristol_Bay_2063257': ['Bristol_Bay_2063257', '324-10-10150-2010-3070-4035', '190302061805', 1],
'Bristol_Bay_2042341': ['Bristol_Bay_2042341', '324-10-10150-2207-3351', '190302050405', 1],
'Bristol_Bay_1026613': ['Bristol_Bay_1026613', '322-10-10080-2011-3156', '190302030605', 1],
'Bristol_Bay_1026463': ['Bristol_Bay_1026463', '322-10-10080-2058', '190302031104', 1],
'Bristol_Bay_1025783': ['Bristol_Bay_1025783', '322-10-10080-2016', '190302030401', 1],
'Bristol_Bay_1025113': ['Bristol_Bay_1025113', '322-10-10080-2011-3154', '190302030604', 1],
'Bristol_Bay_1029732': ['Bristol_Bay_1029732', '322-10-10080-2011-3156-4009', '190302030503', 1],
'Bristol_Bay_1021914': ['Bristol_Bay_1021914', '322-10-10080-2243', '190302030102', 1],
'Bristol_Bay_1016515': ['Bristol_Bay_1016515', '322-10-10080-2243-3016', '190302030106', 1],
'Bristol_Bay_1016325': ['Bristol_Bay_1016325', '322-10-10080-2243', '190302030105', 1],
'Bristol_Bay_1015685': ['Bristol_Bay_1015685', '322-10-10080-2217', '190302030210', 1],
'Bristol_Bay_1015186': ['Bristol_Bay_1015186', '322-10-10080-2243', '190302030107', 1],
'Bristol_Bay_1014821': ['Bristol_Bay_1014821', '322-10-10080-2011', '190302030904', 1],
'Prince_William_Sound_78912': ['Prince_William_Sound_78912', '222-10-12040', '190202011307', 1],
'Prince_William_Sound_75002': ['Prince_William_Sound_75002', '271-10-10310-2063', '190202011805', 1],
'Prince_William_Sound_18357': ['Prince_William_Sound_18357', '227-10-17110', '190202030407', 1],
'Prince_William_Sound_30774': ['Prince_William_Sound_30774', '225-20-15030', '190202012510', 1],
'Prince_William_Sound_41123': ['Prince_William_Sound_41123', '221-30-10560', '190202010603', 1],
'Prince_William_Sound_41143': ['Prince_William_Sound_41143', '221-30-10655', '190202011201', 1],
'Prince_William_Sound_43513': ['Prince_William_Sound_43513', '221-30-10517', '190202010602', 1],
'Prince_William_Sound_43793': ['Prince_William_Sound_43793', '221-30-10480', '190202010601', 1],
'Prince_William_Sound_44113': ['Prince_William_Sound_44113', '221-20-10350', '190202010402', 1],
'Prince_William_Sound_45863': ['Prince_William_Sound_45863', '221-20-10260', '190202010301', 1],
'Prince_William_Sound_46065': ['Prince_William_Sound_46065', '228-50-18190', '190202030103', 1],
'Prince_William_Sound_62232': ['Prince_William_Sound_62232', '222-20-12242', '190202011404', 1],
'Prince_William_Sound_66912': ['Prince_William_Sound_66912', '221-50-11060', '190202011202', 1],
'Prince_William_Sound_72972': ['Prince_William_Sound_72972', '221-40-10990', '190202010704', 1],
'Prince_William_Sound_86061': ['Prince_William_Sound_86061', '221-60-11370-2040', '190202010907', 1],
'Prince_William_Sound_74542': ['Prince_William_Sound_74542', '222-50-12570', '190202011504', 1],
'Prince_William_Sound_45835': ['Prince_William_Sound_45835', '224-40-14870', '190202012301', 1],
'Prince_William_Sound_93261': ['Prince_William_Sound_93261', '221-60-11470', '190202011102', 1],
'Prince_William_Sound_91741': ['Prince_William_Sound_91741', '221-60-11370', '190202010906', 1],
'Prince_William_Sound_18737': ['Prince_William_Sound_18737', '227-30-17790', '190202030701', 1],
'Prince_William_Sound_18547': ['Prince_William_Sound_18547', '227-10-17060', '190202030408', 1],
'Prince_William_Sound_41995': ['Prince_William_Sound_41995', '227-20-17590-2003', '190202030401', 1],
'Prince_William_Sound_79792': ['Prince_William_Sound_79792', '223-30-13220', '190202011804', 1],
'Prince_William_Sound_30886': ['Prince_William_Sound_30886', '227-20-17386', '190202030406', 1],
'Prince_William_Sound_43195': ['Prince_William_Sound_43195', '228-60-18120', '190202030105', 1],
'Prince_William_Sound_29704': ['Prince_William_Sound_29704', '224-10-14540', '190202012104', 1],
'Kodiak_48057': ['Kodiak_48057', '257-20-10020', '190207011107', 1],
'Kodiak_63603': ['Kodiak_63603', '252-32-10010', '190207011402', 1],
'Kodiak_66383': ['Kodiak_66383', '252-31-10040', '190207011401', 1],
'Kodiak_77254': ['Kodiak_77254', '252-36-10010', '190207011302', 1],
'Prince_William_Sound_37955': ['Prince_William_Sound_37955', '226-20-16950', '190202030207', 1],
'Kodiak_48197': ['Kodiak_48197', 'NA', '190207011108', 3],
'Prince_William_Sound_91751': ['Prince_William_Sound_91751', 'NA', '190202010905', 3],
'Kodiak_70982': ['Kodiak_70982', 'NA', '190207011206', 3],
'Kodiak_14458': ['Kodiak_14458', 'NA', '190207011905', 3],
'Kodiak_120645': ['Kodiak_120645', 'NA', '190207010814', 3],
'Kodiak_66643': ['Kodiak_66643', 'NA', '190207011410', 3],
'Kodiak_77794': ['Kodiak_77794', 'NA', '190207011506', 3],
'Kodiak_77162': ['Kodiak_77162', 'NA', '190207010208', 3],
'Kodiak_125355': ['Kodiak_125355', 'NA', '190207010813', 3],
'Kodiak_116535': ['Kodiak_116535', 'NA', '190207010607', 3],
'Kodiak_106365': ['Kodiak_106365', 'NA', '190207010707', 3],
'Bristol_Bay_5033175': ['Bristol_Bay_5033175', 'NA', '190303051103', 3],
'Bristol_Bay_5019146': ['Bristol_Bay_5019146', 'NA', '190303051803', 3],
'Bristol_Bay_5018936': ['Bristol_Bay_5018936', 'NA', '190303051805', 3],
'Bristol_Bay_5018456': ['Bristol_Bay_5018456', 'NA', '190303051907', 3],
'Bristol_Bay_5008157': ['Bristol_Bay_5008157', 'NA', '190303052002', 3],
'Bristol_Bay_5007067': ['Bristol_Bay_5007067', 'NA', '190303051505', 3],
'Bristol_Bay_4115902': ['Bristol_Bay_4115902', 'NA', '190303011303', 3],
'Kodiak_49707': ['Kodiak_49707', 'NA', '190207011001', 3],
'Bristol_Bay_4089531': ['Bristol_Bay_4089531', 'NA', '190303010104', 3],
'Bristol_Bay_4089123': ['Bristol_Bay_4089123', 'NA', '190303011002', 3],
'Bristol_Bay_4088983': ['Bristol_Bay_4088983', 'NA', '190303011006', 3],
'Bristol_Bay_4086175': ['Bristol_Bay_4086175', 'NA', '190303030103', 3],
'Bristol_Bay_4083101': ['Bristol_Bay_4083101', 'NA', '190303020501', 3],
'Bristol_Bay_4080505': ['Bristol_Bay_4080505', 'NA', '190303030204', 3],
'Bristol_Bay_4065316': ['Bristol_Bay_4065316', 'NA', '190303030603', 3],
'Bristol_Bay_4051090': ['Bristol_Bay_4051090', 'NA', '190303020103', 3],
'Bristol_Bay_4033788': ['Bristol_Bay_4033788', 'NA', '190303060403', 3],
'Bristol_Bay_4032968': ['Bristol_Bay_4032968', 'NA', '190303060402', 3],
'Bristol_Bay_4031228': ['Bristol_Bay_4031228', 'NA', '190303060803', 3],
'Bristol_Bay_3028865': ['Bristol_Bay_3028865', 'NA', '190302040603', 3],
'Bristol_Bay_3021202': ['Bristol_Bay_3021202', 'NA', '190302040207', 3],
'Bristol_Bay_3017708': ['Bristol_Bay_3017708', 'NA', '190302041104', 3],
'Bristol_Bay_2081462': ['Bristol_Bay_2081462', 'NA', '190302050606', 3],
'Bristol_Bay_2078822': ['Bristol_Bay_2078822', 'NA', '190302050502', 3],
'Bristol_Bay_2077902': ['Bristol_Bay_2077902', 'NA', '190302051101', 3],
'Bristol_Bay_2077232': ['Bristol_Bay_2077232', 'NA', '190302051102', 3],
'Bristol_Bay_2076162': ['Bristol_Bay_2076162', 'NA', '190302051103', 3],
'Bristol_Bay_2070607': ['Bristol_Bay_2070607', 'NA', '190302062311', 3],
'Bristol_Bay_2059915': ['Bristol_Bay_2059915', 'NA', '190302061502', 3],
'Bristol_Bay_2019230': ['Bristol_Bay_2019230', 'NA', '190302050103', 3],
'Bristol_Bay_1028122': ['Bristol_Bay_1028122', 'NA', '190302031110', 3],
'Bristol_Bay_1024403': ['Bristol_Bay_1024403', 'NA', '190302030603', 3],
'Bristol_Bay_1013001': ['Bristol_Bay_1013001', 'NA', '190302031107', 3],
'190202010804': ['190202010804', 'NA', '190202010804', 3],
'190202011502': ['190202011502', 'NA', '190202011502', 3]
}

awcRelateList = []
newCatList = []
dropList = []
dropHucs = []

addRevList = []
noChangeList = []
newWtdHucs = []
hucNewcatdict = {}


for k,v in reviewDict.items():
    if v[3] == 1:
        awcRelateList.append(k)
        append_value(awcQcDict,k,v[1])
    elif v[3] == 2:
        newCatList.append(k)
        cid = v[0].split('_')[-1]
        append_value(hucNewcatdict,v[2],[v[0],cid])
        newWtdHucs.append(v[2])
    elif v[3] == 3:
        dropList.append(k)
        dropHucs.append(v[2])
    elif v[3] == 4:
        addRevList.append(k)
    elif v[3] == 0:
        noChangeList.append(k)

print (f'{len(awcRelateList)} Hucs need awc relationship changed/added\n{100*"-"}')
print (f'{len(newCatList)} Hucs had wrong catchment assigned and must have new watersheds run\n{100*"-"}')
print (f'{len(dropList)} Hucs should be dropped from the model\n{100*"-"}')
print (f'{len(addRevList)} Hucs need additional review\nHUCS to review:\n{addRevList}\n{100*"-"}')
print (f'{len(noChangeList)} Hucs need no actions\n{100*"-"}')
print(f'AWC QC Dictionary:\n{awcQcDict}')
print(f'HUC to new Catchment dictionary:\n{hucNewcatdict}')


CSV table output directory set to D:\GIS\outputs_20230518
191 Hucs need awc relationship changed/added
----------------------------------------------------------------------------------------------------
94 Hucs had wrong catchment assigned and must have new watersheds run
----------------------------------------------------------------------------------------------------
46 Hucs should be dropped from the model
----------------------------------------------------------------------------------------------------
0 Hucs need additional review
HUCS to review:
[]
----------------------------------------------------------------------------------------------------
0 Hucs need no actions
----------------------------------------------------------------------------------------------------
AWC QC Dictionary:
{'Kodiak_80022': '251-40-10030', 'Bristol_Bay_4051420': '325-30-10100-2202-3901', 'Kodiak_77372': '251-30-10020', 'Kodiak_79642': '251-30-10010', 'Kodiak_63963': '251-20-10020', 'Kodiak_4961

## Identify Outlet catchments - **IF RUNNING FOR QC, OVERWRITE INPUT 'hucs' WITH 'qcHucs' FROM BLOCK BELOW ELSE COMMENT OUT OR DO NOT RUN NEXT BLOCK**
Cook_Inlet_75000500002272 - This catchment/AWC pairing may need to be dropped.  NHDPlus shows this reach as draining North but AWC has reach connected to two systems from North to South.  So "outlet catchment"

In [10]:
# # Print HUCS that need new watersheds and create new dataset for qc
# nhdplushucs = os.path.join(outgdb, 'NHDPlusHUC12')
# tauhucs = os.path.join(outgdb, 'NHD_H_HUC12')
# hucQcclause = f'"HUC12" IN ({str(newWtdHucs).strip("[]")})'
# print(hucQcclause)
# nhdPlusQcHucs =  arcpy.FeatureClassToFeatureClass_conversion(nhdplushucs,outgdb,'nhdPlusQc_Hucs',hucQcclause)
# print(f'NHD Plus QC HUC12s for Cook Inlet/Copper River {nhdPlusQcHucs} created...')
# tauQcHucs = arcpy.FeatureClassToFeatureClass_conversion(tauhucs,outgdb,'tauQc_Hucs',hucQcclause)
# print(f'NHD_H QC HUC12s for Tau Regions {tauQcHucs} created...')
# tauhucs = tauQcHucs
# nhdplushucs = nhdPlusQcHucs

In [11]:
# Filter out hucs to be dropped prior to running
nhdplushucs = os.path.join(outgdb, 'NHDPlusHUC12')
tauhucs = os.path.join(outgdb, 'NHD_H_HUC12')
dropclause = f'"HUC12" NOT IN ({str(dropHucs).strip("[]")})'
#print(dropclause)
print(f'{arcpy.GetCount_management(nhdplushucs)} hucs in Nhdplus dataset')
nhdPlusFinalHucs =  arcpy.FeatureClassToFeatureClass_conversion(nhdplushucs,outgdb,'nhdPlusFinal_Hucs',dropclause)
print(f'{arcpy.GetCount_management(nhdPlusFinalHucs)} NHDPlus HUC12s for Cook Inlet/Copper River {nhdPlusFinalHucs} created...')
print(f'{arcpy.GetCount_management(tauhucs)} hucs in NHD_H dataset')
tauFinalHucs = arcpy.FeatureClassToFeatureClass_conversion(tauhucs,outgdb,'tauFinal_Hucs',dropclause)
print(f'{arcpy.GetCount_management(tauFinalHucs)} NHD_H HUC12s for Entire AKSSF Region {tauFinalHucs} created...')
tauhucs = tauFinalHucs
nhdplushucs = nhdPlusFinalHucs

1686 hucs in Nhdplus dataset
1686 NHDPlus HUC12s for Cook Inlet/Copper River D:\GIS\outputs_20230518\outputs_20230518.gdb\nhdPlusFinal_Hucs created...
15385 hucs in NHD_H dataset
15339 NHD_H HUC12s for Entire AKSSF Region D:\GIS\outputs_20230518\outputs_20230518.gdb\tauFinal_Hucs created...


In [12]:
import arcpy, time, os, datetime, operator
from math import *
from collections import Counter

arcpy.env.workspace = data_dir
regions = arcpy.ListWorkspaces()

# Lists
flowlineList = [] # List to store regional NHDFlowline_merge
streamsList = [] # List to store regional streams_merge
vaas_lst = [] # List to store regional vaas_merge tables
nhdplusoutlets = [] # List to store NHDPlus HUC12 outlet catchment centroid points
tauoutlets = [] # List to store TauDEM HUC12 outlet catchment centroid points
nhdplusawccatouts = [] # List to store NHDPlus HUC12 outlet catchments
tauawccatouts = [] # List to store TauDEM HUC12 outlet catchments

# Dictionaries
dist2CoastDict = {}
vaaDict = {}
strDict = {}
catsDict = {}
huc12Dict = {}
nhdidDict = {}
tauidDict = {}
tauhuc12Dict = {}
hucreviewList = []

# Separate data by source type
nhdplus_dat = ['Cook_Inlet','Copper_River']
tauDem_dat = ['Bristol_Bay', 'Kodiak', 'Prince_William_Sound']

# Loop through all processing areas
# rois = nhdplus_dat + tauDem_dat

# Or comment above and specify below specific subset
#regions = ['D:\\GIS\\AKSSF\\Cook_Inlet', 'D:\\GIS\\AKSSF\\Copper_River' ,'D:\\GIS\\AKSSF\\Prince_William_Sound']
regions = ['D:\\GIS\\AKSSF\\Bristol_Bay','D:\\GIS\\AKSSF\\Kodiak','D:\\GIS\\AKSSF\\Prince_William_Sound']
# Start timing function
processStart = time.time()
processStartdt = datetime.datetime.now()
print(f'Begin {datetime.datetime.now()}')
for region in regions:
    upfcs = [] # List to store feature classes to be updated in update cursor
    roi = os.path.basename(region)
    print(roi)
    if roi in nhdplus_dat:
        # Start roi time
        roi_start = time.time()
        hucs = nhdplushucs
        catsList = []
        outletList = []
        print(f'{roi} using data from {region} folder')
        # Set workspace to region folder
        arcpy.env.workspace = region
        gdb = arcpy.ListWorkspaces(workspace_type='FileGDB')
        print(f'GDB {gdb}')
        sourcegdb = gdb[0]
        walk = arcpy.da.Walk(sourcegdb, datatype = ['FeatureClass','Table'])
        for dirpath, dirnames, filenames in walk:
            for filename in filenames:
                if filename == 'cats_merge':
                    cats  = os.path.join(dirpath, filename)
                    append_value(catsDict,roi,cats)
                elif filename == 'NHDFlowline_merge':
                    streamname = roi + '_' + filename
                    streams = os.path.join(outgdb,streamname)
                    if not arcpy.Exists(streams):
                        print(f'Copying {os.path.join(dirpath, filename)} to {outgdb}')
                        arcpy.FeatureClassToFeatureClass_conversion(os.path.join(dirpath,filename),outgdb,streamname)
                    else:
                        print(f'{streams} already created')
                    #upfcs.append(streams)
                    append_value(strDict, roi, streams)
                    flowlineList.append(streams)
                elif filename == 'vaa_merge':
                    vaas = os.path.join(dirpath, filename)
                    append_value(vaaDict, roi, vaas)
                    vaas_lst.append(vaas)

        #Output names and paths
        outletcatsname = roi + '_AwcHuc12_cats_outlets'
        outcatspath = os.path.join(outgdb,outletcatsname)
        outcatspath2 = os.path.join(sourcegdb,'awc_huc12_catchment_outlets')
        outletcatptsname = roi + '_AwcHuc12_cats_outlets_pts'
        outcatptspath = os.path.join(outgdb,outletcatptsname)
        outcatptspath2 = os.path.join(sourcegdb,'awc_huc12_catchment_outlets_pts')

        if not arcpy.Exists(outcatspath):
            # Build Value dictionary to relate NHDPlus id to contributing area
            fields = ['NHDPlusID','TotDASqKm','StreamOrde', 'Slope', 'AreaSqKm', 'ArbolateSu', 'PathLength', 'StartFlag', 'TerminalPa' ]
            fields2 = fields + ['cat_ID_con']
            updfields= ['NHDPlusID','DSContArea','cat_ID_con','str_ord', 'str_slope','ds_dist_outlet_km',"DSContArea_SqKM",'str_slope_dg','TotDASqKm']
            valueDict = {int(r[0]):(r[1]) for r in arcpy.da.SearchCursor(vaas, fields)}
            strValfieldList = ['NHDPlusID','StreamOrde', 'Slope','PathLength', 'TotDASqKm']
            strValDict = {r[0]:(r[1:]) for r in arcpy.da.SearchCursor(vaas, strValfieldList)}
            where_clause=f'"MERGE_SRC" LIKE \'%{roi}%\''
            print(f'where_clause = {where_clause}')
            awc_where_clause=f'"Shape_Length" >= {awcthresh}'
            print(f'Selecting feature from awc = {awc_where_clause}')
            huclayer1 = arcpy.MakeFeatureLayer_management(hucs,'huclayer1',where_clause = where_clause)
            huclayer2 = arcpy.MakeFeatureLayer_management(hucs,'huclayer2',where_clause = where_clause)
            awclayer1 = arcpy.MakeFeatureLayer_management(awc_events,'awclayer1')
            awclayer2 = arcpy.MakeFeatureLayer_management(awc_events,'awclayer2',where_clause = awc_where_clause)
            print(f'{arcpy.GetCount_management(huclayer1)} huc12s in {roi}')
            print(('*'*100))

            # Modify code to record Hucs that would be dropped and flag these for additional QA rather than dropping them here.
            hucselect_awc = arcpy.SelectLayerByLocation_management(huclayer1, "INTERSECT", awclayer1, None, "SUBSET_SELECTION", "NOT_INVERT") # Select all HUC12s that intersect AWC Events
            hucselect_awcList = [r[0] for r in arcpy.da.SearchCursor(hucselect_awc,'HUC12')] # Create a list of HUC12 numbers from selection
            hucselect_clementi_awc = arcpy.SelectLayerByLocation_management(huclayer2, "CONTAINS_CLEMENTINI", awclayer2, None, "SUBSET_SELECTION", "NOT_INVERT") # Select all HUC12s that intersect AWC Events using clementi option
            hucselect_clementi_awcList = [r[0] for r in arcpy.da.SearchCursor(hucselect_clementi_awc,'HUC12')]# Create a list of HUC12 numbers from clementi selection
            hucCheckList = list((Counter(hucselect_awcList) - Counter(hucselect_clementi_awcList)).elements())# Identify Hucs that are dropped as a result of clementi selection and create list to flag for review later
            hucreviewList.extend(hucCheckList)# add to review list
            hucnum = int(arcpy.GetCount_management(hucselect_awc)[0])
            hucnum_clementi = int(arcpy.GetCount_management(hucselect_clementi_awc)[0])
            diff = hucnum - hucnum_clementi
            print(('*'*100))
            print(f'{hucnum} Huc12s in {roi} intersect awc events input\n{hucnum_clementi} intersect awc events with Clementi intersections (difference of {diff})')
            print(('*'*100))
            hucFields = [f for f in arcpy.ListFields(hucselect_awc)]
            vcount =1
            with arcpy.da.SearchCursor(hucselect_awc,['HUC12','SHAPE@']) as cur:
                for row in cur:
                    print(f'Processing HUC {row[0]}')
                    inhuc = row[1]
                    # ADD if statement here to check if HUC was flagged to have a new outlet catchment else run as is
                    if row[0] in hucNewcatdict:
                        cidcon = hucNewcatdict[row[0]][0]
                        outcatch = hucNewcatdict[row[0]][1]
                        print (f'HUC {row[0]} flagged during review\nNew outlet catchment identified as {cidcon}')
                    else:
                        cat_layer = arcpy.MakeFeatureLayer_management(cats,'cat_layer')
                        # Select by location using awc and huc 12
                        arcpy.SelectLayerByLocation_management(cat_layer,'HAVE_THEIR_CENTER_IN',inhuc,'','NEW_SELECTION')
                        print(f'{vcount}. Finding outlet for HUC {row[0]} out of {arcpy.GetCount_management(cat_layer)} catchments ({hucnum-vcount} remain).\n{("*" * 60)}')
                        catList = [r[0] for r in arcpy.da.SearchCursor(cat_layer, 'NHDPlusID')]
                        intersect = list(set(catList).intersection(valueDict))
                        catDict = {int(i):(valueDict[i]) for i in intersect}
                        # Find Catchment with max drainage area
                        outcatch = max(catDict.items(), key = operator.itemgetter(1))[0]
                        cidcon = roi + '_' + str(int(outcatch))
                    append_value(dist2CoastDict,cidcon,row[0])
                    append_value(huc12Dict, row[0], [int(outcatch),roi,valueDict[int(outcatch)]])
                    append_value(nhdidDict,int(outcatch),[roi,row[0], valueDict[int(outcatch)]])
                    outletList.append(int(outcatch))
                    vcount+=1
                del(row)
            del(cur)

            outlet_cats = arcpy.MakeFeatureLayer_management(cats,'outlet_cats')
            out_expression ='"NHDPlusID" IN ' + str(tuple(outletList))
            #print(out_expression)
            outlet_cats_select = arcpy.SelectLayerByAttribute_management(outlet_cats,'NEW_SELECTION', out_expression)
            print(f'Creating copy of {arcpy.GetCount_management(outlet_cats)} outlet catchments for Region {roi} at {outcatspath}')
            print(('*'*100))

            # Copy outputs
            arcpy.FeatureClassToFeatureClass_conversion(outlet_cats_select,outgdb,outletcatsname)
            arcpy.FeatureToPoint_management(outcatspath, outcatptspath, 'INSIDE')
            # Create Copies to akssf data_dir regional gdbs also
            arcpy.FeatureClassToFeatureClass_conversion(outlet_cats_select,sourcegdb,'awc_huc12_catchment_outlets')
            arcpy.FeatureToPoint_management(outcatspath2, outcatptspath2, 'INSIDE')
            nhdplusoutlets.append(outcatptspath)
            nhdplusawccatouts.append(outcatspath)
            # Add total drainage km from value dict to feature classes and cat_ID_con from regDict
            # Add str slope and str order from vaaDict
            upfcs = [outcatspath, outcatptspath,outcatptspath2,outcatptspath2]
            for upfc in upfcs:
                arcpy.AddField_management(upfc,fields[1],'DOUBLE') # TotDASqKm
                arcpy.AddField_management(upfc,fields2[9],'TEXT')#add cat_ID_con field
                arcpy.AddField_management(upfc, "str_slope", field_type="DOUBLE")
                arcpy.AddField_management(upfc, "str_ord", field_type="SHORT")
                arcpy.AddField_management(upfc, "ds_dist_outlet_km", field_type="DOUBLE")
                arcpy.AddField_management(upfc, "DSContArea_SqKM",'DOUBLE') #add DSContArea_SqKM area field
                arcpy.AddField_management(upfc, "DSContArea",'DOUBLE') #add DSCont area field
                arcpy.AddField_management(upfc, "str_slope_dg",'DOUBLE') #add stream slope degrees field
                with arcpy.da.UpdateCursor(upfc,updfields) as cur:
                    for row in cur:
                        if not row[0] in strValDict:
                            print(f'No records for NHDPLUS feature {row[0]} in VAA table')
                        else:
                            dsarea = strValDict[row[0]][3] * 1e+6 # Convert TotDASqKm to area in meters
                            row[1] = dsarea
                            catcon = roi + '_' + str(int(row[0])) # calculate cat_ID_con
                            row[2] = catcon # calculate cat_ID_con
                            strord = strValDict[row[0]][0] # add str order
                            row[3] = strord # add str order
                            strslope = strValDict[row[0]][1] # add str slope
                            row[4] = strslope # add str slope
                            ds_dist = strValDict[row[0]][2] # convert to km
                            row[5] = ds_dist # add distance to outlet from reach end
                            dsareasqkm = strValDict[row[0]][3] # Populate with TotDASqKm
                            row[6] = dsareasqkm
                            strSlopedg = degrees(atan(strslope)) # Convert unitless rise/run to degrees
                            row[7] = strSlopedg # Populate field
                            row[8] = dsareasqkm #  Copy TotDASqKm from vaa table
                            #print(f'Catchment {catcon} has the following attributes\nslope = {strslope} dg\nstream order = {strord}\nCont area = {dsarea}\nDistance to outlet = {ds_dist}\n{"*"*100}')
                        cur.updateRow(row)
                    del(row)
                del(cur)

            # End roi time
            roi_stop = time.time()
            roi_time = int (roi_stop - roi_start)
            print(f'{roi} Elapsed time: ({datetime.timedelta(seconds=roi_time)})')
            print(f'{"*"*60}')
        else:
            print(f'Catchments for {roi} already created at {outcatspath2}')

    elif roi in tauDem_dat:
        # Start roi time
        roi_start = time.time()
        hucs = tauhucs
        catsList = []
        outletList = []
        print(f'{roi} using data from {region} folder')
        # Set workspace to region folder
        arcpy.env.workspace = region
        gdb = arcpy.ListWorkspaces(workspace_type='FileGDB')
        sourcegdb = gdb[0]
        walk = arcpy.da.Walk(sourcegdb, datatype = ['FeatureClass','Table'])
        for dirpath, dirnames, filenames in walk:
            for filename in filenames:
                if filename == 'cats_merge':
                    cats  = os.path.join(dirpath, filename)
                    append_value(catsDict,roi,cats)
                elif filename == 'streams_merge':
                    streamname = roi + '_' + filename
                    streams = os.path.join(outgdb,streamname)
                    if not arcpy.Exists(streams):
                        print(f'Copying {os.path.join(dirpath, filename)} to {outgdb}')
                        arcpy.FeatureClassToFeatureClass_conversion(os.path.join(dirpath,filename),outgdb,streamname)
                    else:
                        print(f'{streams} already created')
                    #upfcs.append(streams)
                    append_value(strDict, roi, streams)
                    streamsList.append(streams)

        #Output names and paths
        outletcatsname = roi + '_TauAwcH12_cats_outlets'
        outcatspath = os.path.join(outgdb,outletcatsname)
        outcatspath2 = os.path.join(sourcegdb,'awc_huc12_catchment_outlets')
        outletcatptsname = roi + '_TauAwcH12_cats_outlets_pts'
        outcatptspath = os.path.join(outgdb,outletcatptsname)
        outcatptspath2 = os.path.join(sourcegdb,'awc_huc12_catchment_outlets_pts')
        print(('-'*100),'\n')
        if not arcpy.Exists(outcatspath):
            # Build Value dictionary to relate TauDEM gridcodes to contributing area
            if roi == 'Bristol_Bay':
                fields = ['catID','DSContArea']
                fields2 = fields + ['cat_ID_con']
                fields3 = ['catID','DSContArea','cat_ID_con']
                strValfieldList = ['catID','strmOrder', 'Slope', 'USContArea', 'DSContArea', 'DOUTEND', 'DOUTSTART']
                updfields= ['catID','DSContArea','cat_ID_con','str_ord', 'str_slope','ds_dist_outlet_km','DSContArea_SqKM','str_slope_dg']
                strValDict = {r[0]:(r[1:]) for r in arcpy.da.SearchCursor(streams, strValfieldList)}
            else:
                fields = ['LINKNO','DSContArea']
                fields2 = fields + ['cat_ID_con']
                fields3 = ['gridcode','DSContArea','cat_ID_con']
                updfields= ['gridcode','DSContArea','cat_ID_con','str_ord', 'str_slope','ds_dist_outlet_km','DSContArea_SqKM','str_slope_dg']
                strValfieldList = ['LINKNO','strmOrder', 'Slope', 'USContArea', 'DSContArea', 'DOUTEND', 'DOUTSTART']
                strValDict = {r[0]:(r[1:]) for r in arcpy.da.SearchCursor(streams, strValfieldList)}
            valueDict = {int(r[0]):(r[1]) for r in arcpy.da.SearchCursor(streams, fields)}

            awc_where_clause=f'"Shape_Length" >= {awcthresh}'
            print(f'Selecting feature from awc = {awc_where_clause}')
            huclayer1 = arcpy.MakeFeatureLayer_management(hucs,'huclayer1')
            huclayer2 = arcpy.MakeFeatureLayer_management(hucs,'huclayer2')
            awclayer1 = arcpy.MakeFeatureLayer_management(awc_events,'awclayer1')
            awclayer2 = arcpy.MakeFeatureLayer_management(awc_events,'awclayer2',where_clause = awc_where_clause)
            hucselect_reg1 = arcpy.SelectLayerByLocation_management(huclayer1,'INTERSECT',streams,'','NEW_SELECTION') #Select only Hucs in TauDEM roi using streams
            hucselect_reg2 = arcpy.SelectLayerByLocation_management(huclayer2,'INTERSECT',streams,'','NEW_SELECTION') #Select only Hucs in TauDEM roi using streams
            print(f'{arcpy.GetCount_management(hucselect_reg1)} huc12s in {roi}')
            print(('*'*100))
            # Modify code to record Hucs that would be dropped and flag these for additional QA rather than drop them here.
            hucselect_awc = arcpy.SelectLayerByLocation_management(hucselect_reg1, "INTERSECT", awclayer1, None, "SUBSET_SELECTION", "NOT_INVERT") # Select all HUC12s that intersect AWC Events
            hucselect_awcList = [r[0] for r in arcpy.da.SearchCursor(hucselect_awc,'HUC12')] # Create a list of HUC12 numbers from selection
            hucselect_clementi_awc = arcpy.SelectLayerByLocation_management(hucselect_reg2, "CONTAINS_CLEMENTINI", awclayer2, None, "SUBSET_SELECTION", "NOT_INVERT") # Select all HUC12s that intersect AWC Events using clementi option and streams above threshold
            hucselect_clementi_awcList = [r[0] for r in arcpy.da.SearchCursor(hucselect_clementi_awc,'HUC12')]# Create a list of HUC12 numbers from clementi selection
            hucCheckList = list((Counter(hucselect_awcList) - Counter(hucselect_clementi_awcList)).elements())# Identify Hucs that are dropped as a result of clementi selection and create list to flag for review later
            hucreviewList.extend(hucCheckList)# add to review list
            hucnum = int(arcpy.GetCount_management(hucselect_awc)[0])
            hucnum_clementi = int(arcpy.GetCount_management(hucselect_clementi_awc)[0])
            diff = hucnum - hucnum_clementi
            print(('*'*100))
            print(f'{hucnum} Huc12s in {roi} intersect awc events input\n{hucnum_clementi} intersect awc events with Clementi intersections (difference of {diff})')
            print(('*'*100))
            hucFields = [f for f in arcpy.ListFields(hucselect_awc)]
            vcount =1
            with arcpy.da.SearchCursor(hucselect_awc,['HUC12','SHAPE@']) as cur:
                for row in cur:
                    print(f'Processing HUC {row[0]}')
                    inhuc = row[1]
                    if row[0] in hucNewcatdict:
                        cidcon = hucNewcatdict[row[0]][0]
                        outcatch = hucNewcatdict[row[0]][1]
                        print (f'HUC {row[0]} flagged during review\nNew outlet catchment identified as {cidcon}')
                    else:
                        cat_layer = arcpy.MakeFeatureLayer_management(cats,'cat_layer')
                        # Select by location using awc and huc 12
                        arcpy.SelectLayerByLocation_management(cat_layer,'HAVE_THEIR_CENTER_IN',inhuc,'','NEW_SELECTION')
                        print(f'{vcount}. Finding outlet for HUC {row[0]} out of {arcpy.GetCount_management(cat_layer)} catchments ({hucnum-vcount} remain).\n{("*" * 60)}')
                        catList = [r[0] for r in arcpy.da.SearchCursor(cat_layer, f'{fields3[0]}')]
                        intersect = list(set(catList).intersection(valueDict))
                        catDict = {int(i):(valueDict[i]) for i in intersect}
                        # Find Catchment with max drainage area
                        outcatch = max(catDict.items(), key = operator.itemgetter(1))[0]
                        cidcon = roi +'_'+ str(int(outcatch))
                    append_value(dist2CoastDict,cidcon,row[0])
                    append_value(tauhuc12Dict, row[0], [int(outcatch),roi,valueDict[int(outcatch)]])
                    append_value(tauidDict,cidcon,[roi,row[0], valueDict[int(outcatch)]])
                    outletList.append(int(outcatch))
                    vcount+=1
                del(row)
            del(cur)
            outlet_cats = arcpy.MakeFeatureLayer_management(cats,'outlet_cats')
            out_expression =f'"{fields3[0]}" IN ' + str(tuple(outletList))
            #print(out_expression)
            outlet_cats_select = arcpy.SelectLayerByAttribute_management(outlet_cats,'NEW_SELECTION', out_expression)
            print(f'Creating copy of {arcpy.GetCount_management(outlet_cats)} outlet catchments for Region {roi} at {outcatspath}')
            print(('*'*100))

            # Copy outputs
            arcpy.FeatureClassToFeatureClass_conversion(outlet_cats_select,outgdb,outletcatsname)
            arcpy.FeatureToPoint_management(outcatspath, outcatptspath, 'INSIDE')
            # Create Copies to akssf data_dir regional gdbs also
            arcpy.FeatureClassToFeatureClass_conversion(outlet_cats_select,sourcegdb,'awc_huc12_catchment_outlets')
            arcpy.FeatureToPoint_management(outcatspath2, outcatptspath2, 'INSIDE')
            tauoutlets.append(outcatptspath)
            tauawccatouts.append(outcatspath)
            # Add total drainage km from value dict to feature classes and cat_ID_con from regDict
            # Add Stream slope and stream order from stream dictionary
            upfcs = [outcatspath, outcatptspath,outcatptspath2,outcatptspath2]
            for upfc in upfcs:
                arcpy.AddField_management(upfc,fields[1],'DOUBLE') #add DSCont area field
                arcpy.AddField_management(upfc,fields2[2],'TEXT')#add cat_ID_con field
                arcpy.AddField_management(upfc, "str_slope", field_type="DOUBLE")
                arcpy.AddField_management(upfc, "str_ord", field_type="SHORT")
                arcpy.AddField_management(upfc, "ds_dist_outlet_km", field_type="DOUBLE")
                arcpy.AddField_management(upfc, "DSContArea_SqKM",'DOUBLE') # add DSCont area field
                arcpy.AddField_management(upfc, 'str_slope_dg','DOUBLE') # add stream slope in degrees field
                with arcpy.da.UpdateCursor(upfc,updfields) as cur:
                    for row in cur:
                        dsarea = strValDict[row[0]][3] # Update ds contributing area
                        row[1] = int(dsarea)
                        catcon = roi + '_' + str(int(row[0])) # calculate cat_ID_con
                        row[2] = catcon # calculate cat_ID_con
                        strord = strValDict[row[0]][0] # add str order
                        row[3] = strord # add str order
                        strslope = strValDict[row[0]][1] # add str slope
                        row[4] = strslope # add str slope
                        ds_dist = strValDict[row[0]][4] * 1e-3 # convert to km
                        row[5] = ds_dist # add distance to outlet from reach end
                        dsareasqkm = int(strValDict[row[0]][3]) * 1e-6 # Update ds contributing area
                        row[6] = dsareasqkm
                        strSlopedg = degrees(atan(strslope))
                        row[7] = strSlopedg
                        #print(f'Catchment {catcon} has the following attributes\nslope = {strslope} dg\nstream order = {strord}\nCont area = {dsarea}\nDistance to outlet = {ds_dist}\n{"*"*100}')
                        cur.updateRow(row)
                    del(row)
                del(cur)
            # End roi time
            roi_stop = time.time()
            roi_time = int (roi_stop - roi_start)
            print(f'{roi} Elapsed time: ({datetime.timedelta(seconds=roi_time)})')
            print(f'{"*"*60}')

# End timing
processEnd = time.time()
processElapsed = int(processEnd - processStart)
processSuccess_time = datetime.datetime.now()
# Report success
print(f'Process completed at {processSuccess_time.strftime("%Y-%m-%d %H:%M")} '
      f'(Elapsed time: {datetime.timedelta(seconds=processElapsed)})')
print(f'{"*"*100}')

Begin 2023-05-18 14:38:24.251699
Bristol_Bay
Bristol_Bay using data from D:\GIS\AKSSF\Bristol_Bay folder
Copying D:\GIS\AKSSF\Bristol_Bay\Bristol_Bay.gdb\streams_merge to D:\GIS\outputs_20230518\outputs_20230518.gdb
---------------------------------------------------------------------------------------------------- 

Selecting feature from awc = "Shape_Length" >= 500
794 huc12s in Bristol_Bay
****************************************************************************************************
****************************************************************************************************
581 Huc12s in Bristol_Bay intersect awc events input
571 intersect awc events with Clementi intersections (difference of 10)
****************************************************************************************************
Processing HUC 190302051406
1. Finding outlet for HUC 190302051406 out of 476 catchments (580 remain).
************************************************************
Processing H

## Write huc review list to output text file

In [13]:
# no need to run if
# print (os.getcwd())
# with open("HUCS4Review.txt", "w") as output:

#     output.write(str(hucreviewList))
hucreviewList


['190303021201',
 '190303011602',
 '190302061704',
 '190302050407',
 '190302051402',
 '190303030703',
 '190303030804',
 '190303040204',
 '190303050102',
 '190303011003',
 '190202012307',
 '190202011606',
 '190202010907',
 '190202012506',
 '190202012204',
 '190202011101',
 '190202010904',
 '190202010401',
 '190202012001',
 '190202030302',
 '190202030208',
 '190202030201',
 '190202030202',
 '190202011108',
 '190202011601']

## Merge all outlet points together and calculate distance to coastline
This chunk is dependent on the data dictionaries created in Step 2
Calculate Distance to Coast from outlet catchment point to the nearest coastline as a straight line distance
 * Generate near table and export as seperate csv

NHDPlus Section


In [14]:
# import arcpy, datetime
# import numpy as pd
#
# # Input path to coastline
# # Merge all catchment outlet centroids togethera
# nhdoutletsname = 'AKSSF_NHDPlus_awcHuc12_outlet_cats_points'
# nhdoutletspath = os.path.join(outgdb, nhdoutletsname)
#
# #if not arcpy.Exists(nhdoutletspath):
# all_nhd_outlet_pts = arcpy.Merge_management(nhdplusoutlets,nhdoutletspath)
# # Start timing function
# start = datetime.datetime.now()
# print(f'Getting distance to coast {datetime.datetime.now()}...')
# arcpy.analysis.Near(all_nhd_outlet_pts, coast, None, "NO_LOCATION", "NO_ANGLE", "GEODESIC", "NEAR_DIST NEAR_DIST")
# arcpy.AlterField_management(all_nhd_outlet_pts,'NEAR_DIST','dist_catch_coast_km','dist_catch_coast_km' )
# arcpy.AddField_management(all_nhd_outlet_pts,'HUC12','TEXT')
# arcpy.AddField_management(all_nhd_outlet_pts,'HUC12_Review','SHORT')
#
# # Convert distance in meters to km
# with arcpy.da.UpdateCursor(all_nhd_outlet_pts,['dist_catch_coast_km','NHDPlusID','HUC12','HUC12_Review']) as cur:
#     for row in cur:
#         row[0] = row[0] * 0.001
#         Huc12 = nhdidDict[row[1]][1] # add HuC12 id
#         row[2] = Huc12
#         if Huc12 in hucreviewList:
#             row[3] = 1
#         else:
#             row[3] = 0
#         cur.updateRow(row)
#     del(row)
# del(cur)
# print(f'Process complete')
# # else:
# #     print(f'Outlet points already created at {nhdoutletspath}')


TauDEM Section


In [15]:
import arcpy, datetime
import numpy as pd

# Merge all catchment outlet centroids together
tauoutname = 'AKSSF_TauDEM_awcHuc12_outlet_cats_points'
tauoutpath = os.path.join(outgdb, tauoutname)

#if not arcpy.Exists(tauoutpath):
all_tau_outpts = arcpy.Merge_management(tauoutlets,tauoutpath)
# Start timing function
start = datetime.datetime.now()
print(f'Getting distance to coast {datetime.datetime.now()}...')
arcpy.analysis.Near(all_tau_outpts, coast, None, "NO_LOCATION", "NO_ANGLE", "GEODESIC", "NEAR_DIST NEAR_DIST")
arcpy.AlterField_management(all_tau_outpts,'NEAR_DIST','dist_catch_coast_km','dist_catch_coast_km' )
arcpy.AddField_management(all_tau_outpts,'HUC12','TEXT')
arcpy.AddField_management(all_tau_outpts,'DSContAreaSqKM','DOUBLE')
arcpy.AddField_management(all_tau_outpts,'HUC12_Review','SHORT')

# Convert distance in meters to km
with arcpy.da.UpdateCursor(all_tau_outpts,['dist_catch_coast_km','cat_ID_con','HUC12','DSContArea','DSContAreaSqKM','HUC12_Review']) as cur:
    for row in cur:
        row[0] = row[0] * 0.001
        Huc12 = tauidDict[row[1]][1] # Identify HUC12
        row[2] = Huc12 #add HUC12
        row[4] = int(row[3])/1000000 #convert sq meters to sq km
        if Huc12 in hucreviewList:
            row[5] = 1
        else:
            row[5] = 0
        cur.updateRow(row)
    del(row)
del(cur)
print(f'Process complete')
# else:
#     print(f'Outlet points already created at {tauoutpath}')

Getting distance to coast 2023-05-18 14:42:49.738448...
Process complete


## Merge catchment outlets

In [16]:
print(f'Merging all available catchment outlet points')
# NHDPoints

# nhdoutletsname = 'AKSSF_NHDPlus_awcHuc12_outlet_cats_points'
# nhdoutletspath = os.path.join(outgdb, nhdoutletsname)
nhdoutletspath = r'D:\GIS\AKSSF_awcHuc12_cv_Final\AKSSF_awcHuc12_cv_Final.gdb\AKSSF_NHDPlus_awcHuc12_outlet_cats_points'


# Taupoints
tauoutname = 'AKSSF_TauDEM_awcHuc12_outlet_cats_points'
tauoutpath = os.path.join(outgdb, tauoutname)

# All points
catpointsname = 'AKSSF_awcHuc12_outlet_cats_points'
catpointspath = os.path.join(outgdb, catpointsname)

# Create FieldMappings object to manage merge output fields
out_fms = arcpy.FieldMappings()

# Add all fields from both point fcs
out_fms.addTable(nhdoutletspath)
out_fms.addTable(tauoutpath)

# Add input fields
out_fm_dsdrain = arcpy.FieldMap()
out_fm_dsdrain.addInputField(nhdoutletspath,'TotDASqKm')
out_fm_dsdrain.addInputField(tauoutpath,'DSContAreaSqKM')

# Set name of new output field "DsContAreaSK"
dsdrain = out_fm_dsdrain.outputField
dsdrain.name = "DsContAreaSqKm"
out_fm_dsdrain.outputField = dsdrain

# add to field mappings
out_fms.addFieldMap(out_fm_dsdrain)

for field in out_fms.fields:
    if field.name not in ['cat_ID_con', 'DsContAreaSqKm','dist_catch_coast_km', 'HUC12', 'HUC12_Review']:
        out_fms.removeFieldMap(out_fms.findFieldMapIndex(field.name))

#if not arcpy.Exists(catpointspath):
addSourceInfo = "ADD_SOURCE_INFO"
cats_outlets = arcpy.Merge_management([nhdoutletspath,tauoutpath],
                                      catpointspath,
                                      out_fms,
                                      addSourceInfo)

#else:
#    print(f'AKSSF AWC Catchment outlets already identified and exported to {catpointspath}')
print(f'Merge Complete')

Merging all available catchment outlet points
Merge Complete


### Convert to df and examine

In [17]:
import numpy
import pandas as pd
pd.set_option("display.max_rows", None)
# Make catchment points df
cat_df = pd.DataFrame()
cat_field_list = []

for field in arcpy.ListFields(catpointspath):
    print(field.name)
    cat_field_list.append(field.name)

cat_arr = arcpy.da.TableToNumPyArray(catpointspath, ['cat_ID_con','dist_catch_coast_km','DsContAreaSqKm','HUC12','HUC12_Review'], skip_nulls = False)
cat_df = pd.DataFrame(cat_arr)
cat_df = cat_df.set_index('cat_ID_con')
cat_df

OBJECTID
Shape
cat_ID_con
dist_catch_coast_km
HUC12
HUC12_Review
DsContAreaSqKm
MERGE_SRC


dist_catch_coast_km  DsContAreaSqKm  \
cat_ID_con                                                         
Cook_Inlet_75004200000901              21.633384       36.962575   
Cook_Inlet_75004200001724              17.599013      170.812175   
Cook_Inlet_75004200000437               0.318196        7.584725   
Cook_Inlet_75004200001493               0.147499        9.640600   
Cook_Inlet_75004200009084               0.787633       26.753250   
Cook_Inlet_75004200003619               0.089052      135.005850   
Cook_Inlet_75004200001047               0.548926       12.012100   
Cook_Inlet_75004200016346               0.171205       10.734100   
Cook_Inlet_75004200010717               0.349695       15.916525   
Cook_Inlet_75004200010096               0.076809        7.266700   
Cook_Inlet_75004200003399               0.173348       37.866925   
Cook_Inlet_75004200000722               0.029182       48.072025   
Cook_Inlet_75004200000726               0.315951       66.517075   
Cook_Inlet_75004200012986               1.332331       43.229850   
Cook_Inlet_75004200008847               0.015401        3.652100   
Cook_Inlet_75004200010465               0.021366       10.441625   
Cook_Inlet_75004200014411               0.195336       25.663575   
Cook_Inlet_75004200012680               0.175628       28.307425   
Cook_Inlet_75004200000559               0.087143        2.790175   
Cook_Inlet_75004200007843               0.218678        1.171575   
Cook_Inlet_75004200009093               0.456912       22.003525   
Cook_Inlet_75004200008970               0.082471       14.768975   
Cook_Inlet_75004200005429              21.477566       37.976200   
Cook_Inlet_75004200012771               0.016949      127.594800   
Cook_Inlet_75004200012099               2.280098      266.149950   
Cook_Inlet_75004200001003               0.309558       14.935775   
Cook_Inlet_75004200000848               0.748290       10.283725   
Cook_Inlet_75004200011012               0.110729      289.799275   
Cook_Inlet_75004200006975               0.128601       19.503725   
Cook_Inlet_75004200005415              16.890604       55.250425   
Cook_Inlet_75004200000064               0.985950       97.162700   
Cook_Inlet_75004200001191               0.367926       19.096450   
Cook_Inlet_75004200001574               0.100115        3.595850   
Cook_Inlet_75004200003989               6.715231      403.877375   
Cook_Inlet_75004200002199               0.204518      101.170825   
Cook_Inlet_75004200005203               0.481730       64.664875   
Cook_Inlet_75004200001716               0.872756      295.298075   
Cook_Inlet_75004200008853               0.297196       58.593775   
Cook_Inlet_75004200008845               1.072117       15.334600   
Cook_Inlet_75004200005283               0.106344        4.820600   
Cook_Inlet_75004200005907               0.112917        1.054550   
Cook_Inlet_75004300004332               0.488941      330.124075   
Cook_Inlet_75004300005723               0.634398       65.409050   
Cook_Inlet_75004300006970               0.194162      501.735400   
Cook_Inlet_75004300002057              21.842191       45.969325   
Cook_Inlet_75004300005518              13.313859       73.485400   
Cook_Inlet_75004300004701               6.612002      154.661600   
Cook_Inlet_75004300004365               5.063402       93.164800   
Cook_Inlet_75004300006839               0.064884       71.286925   
Cook_Inlet_75004300007978               0.183661       87.060725   
Cook_Inlet_75004300007859               0.704871       26.989025   
Cook_Inlet_75004300005004               0.267006      230.420400   
Cook_Inlet_75004300005103              40.356818       56.978100   
Cook_Inlet_75004300000311               9.980660       51.811850   
Cook_Inlet_75004300008012               0.980620       59.414950   
Cook_Inlet_75004300001135               0.075955       57.483925   
Cook_Inlet_75004300007259               0.190951      136.892900   
Cook_Inlet_750043

### Export csv of outlet points


In [18]:
import os
#Export CSV to read into R
catpts_outname = 'AKSSF_awcHuc12_dist_catch_coast_km.csv'
outlets_csv = os.path.join(outdir,catpts_outname)
if not arcpy.Exists(outlets_csv):
    arcpy.da.NumPyArrayToTable(cat_arr,outlets_csv)
    print(f'CSV export {outlets_csv} complete')
else:
    print(f'Csv of catchment outlet points already exported to {outlets_csv}')
print('----------')

CSV export D:\GIS\outputs_20230518\AKSSF_awcHuc12_dist_catch_coast_km.csv complete
----------


# Section 3 - Create Watersheds
* If watersheds have already been created there is no need to run this section again in order for subsequent process to run.
### 2022-04-06 Need to Modify a bit to accept an input list or point file to run a subset of additional watersheds based on QC review of the original outputs
I think just set the idlist = list of catchment id's found during qc and make sure to save to a new location and not overwrite originals.

In [19]:
# Watersheds
import arcpy, time, datetime, os
import pandas as pd
from functools import reduce
import arcpy, time, os, datetime, operator

arcpy.env.workspace = data_dir
regions = arcpy.ListWorkspaces()
arcpy.env.overwriteOutput = True
arcpy.env.qualifiedFieldNames = False
sr = arcpy.SpatialReference(3338)  #'NAD_1983_Alaska_Albers'
arcpy.env.outputCoordinateSystem = sr

wtdDict = {}

# Separate data by source type
nhdplus_dat = ['Cook_Inlet','Copper_River']
tauDem_dat = ['Bristol_Bay', 'Kodiak', 'Prince_William_Sound']

# Limit to Cook inlet for testing
#regions = ['D:\\GIS\\AKSSF\\Cook_Inlet', 'D:\\GIS\\AKSSF\\Copper_River' ,'D:\\GIS\\AKSSF\\Prince_William_Sound']
regions = ['D:\\GIS\\AKSSF\\Bristol_Bay', 'D:\\GIS\\AKSSF\\Kodiak', 'D:\\GIS\\AKSSF\\Prince_William_Sound']
#regions = ['D:\\GIS\\AKSSF\\Bristol_Bay']

# Start timing function
processStart = time.time()
processStartdt = datetime.datetime.now()

for region in regions:
    reg_start = time.time()
    roi = os.path.basename(region)
    print(roi)
    if roi in nhdplus_dat:
        try:
            wtdList = []
            arcpy.env.workspace = region
            gdb = arcpy.ListWorkspaces(workspace_type='FileGDB')
            ingdb = gdb[0]
            # set inputs
            vaa = os.path.join(ingdb, "vaa_merge")
            cats = os.path.join(ingdb, "cats_merge")
            streams = os.path.join(ingdb, "NHDFlowline_merge")
            outcats = os.path.join(ingdb, "awc_huc12_catchment_outlets")
            # Create list of nhdplus ids for outlet catchments
            idList = [int(row[0]) for row in arcpy.da.SearchCursor(outcats,'NHDPlusID')]
            #Make test list of few small catchments
            #idList = [75004400004166,75004400004344, 75004400010328]
            # Get list of index names for cats merge and add index if not already created
            index_names = [i.name for i in arcpy.ListIndexes(cats)]
            print(index_names)
            if 'NHDPlusID_index' not in index_names:
                print (f'Creating index for {cats}')
                arcpy.AddIndex_management(cats,'NHDPlusID','NHDPlusID_index')
            else:
                print(f'{cats} Indexed')

            #watersheds feature dataset for storing fcs
            fdatname = roi + '_Watersheds'
            fdat = os.path.join(outgdb,fdatname)
            if not arcpy.Exists(fdat):
                arcpy.management.CreateFeatureDataset(outgdb, fdatname, sr)
            else:
                print(f'{fdat} exists for {roi}')

            vaa_df1 = pd.DataFrame(arcpy.da.TableToNumPyArray(vaa, ("NHDPlusID", "FromNode", "ToNode", "StartFlag")))
            stream_df = pd.DataFrame(arcpy.da.TableToNumPyArray(streams, ("NHDPlusID", "FType")))
            dfs = [vaa_df1, stream_df]
            vaa_df = reduce(lambda left,right: pd.merge(left,right,on='NHDPlusID',how="outer"), dfs)
            # remove pipelines
            vaa_df = vaa_df[(vaa_df['FType'] != 428 )]
            vaa_df

            c=1
            for id in idList:
                iteration_start = time.time()
                print(f'{c}. Starting watershed for catchment {str(id)} ({(len(idList) - c)} remaining)')
                rec = [id]
                up_ids = []
                up_ids.append(rec)
                rec_len = len(rec)
                hws_sum = 0

                while rec_len != hws_sum:
                    fromnode = vaa_df.loc[vaa_df["NHDPlusID"].isin(rec), "FromNode"]
                    rec = vaa_df.loc[vaa_df["ToNode"].isin(fromnode), "NHDPlusID"]
                    rec_len = len(rec)
                    rec_hws = vaa_df.loc[vaa_df["ToNode"].isin(fromnode), "StartFlag"]
                    hws_sum = sum(rec_hws)
                    up_ids.append(rec)
                #up_ids is a list with more than numbers, use extend to only keep numeric nhdplusids
                newup_ids = []
                for x in up_ids:
                    newup_ids.extend(x)

                tempLayer = "catsLyr"
                expression = '"NHDPlusID" IN ({0})'.format(', '.join(map(str, newup_ids)) or 'NULL')
                arcpy.MakeFeatureLayer_management(cats, tempLayer, where_clause=expression)
                outdis = "memory/wtd_" + str(round(id))
                outwtd = os.path.join(fdat,f'{roi}_wtd_{str(int(id))}')
                dis = arcpy.Dissolve_management(tempLayer, outdis)
                watershed = arcpy.EliminatePolygonPart_management(dis, outwtd,"PERCENT", "0 SquareKilometers", 90, "CONTAINED_ONLY")
                wtdList.append(outwtd)
                append_value(wtdDict,roi,outwtd)

                # Stop iteration timer
                iteration_stop = time.time()
                iter_time = int (iteration_stop - iteration_start)
                print(f'Elapsed time: ({datetime.timedelta(seconds=iter_time)})')
                print(f'{"*"*60}')
                c+=1

            wtd_merge = arcpy.Merge_management(wtdList, os.path.join(ingdb,'awc_huc12_wtds_merge'),'','ADD_SOURCE_INFO')
            arcpy.AddField_management(wtd_merge,'cat_ID_con','TEXT')
            arcpy.AddField_management(wtd_merge,'cat_ID','DOUBLE')
            arcpy.AddField_management(wtd_merge,'cat_ID_txt','TEXT')
            arcpy.AddField_management(wtd_merge,'NHDPlusID','DOUBLE')
            with arcpy.da.UpdateCursor(wtd_merge,['MERGE_SRC','NHDPlusID','cat_ID_con','cat_ID','cat_ID_txt']) as cur:
                for row in cur:
                    # Pull nhdplus id from merge source and calculate fields
                    nhdplusid= int(row[0].split('_')[-1])
                    row[1] = nhdplusid
                    row[2] = roi + '_' + str(nhdplusid)
                    row[3] = nhdplusid
                    row[4] = str(nhdplusid)
                    cur.updateRow(row)
                del(row)
            del(cur)
            arcpy.CopyFeatures_management(wtd_merge,os.path.join(outgdb,f'{roi}_AwcHuc12_wtds_merge' ))

            # Stop iteration timer
            reg_stop = time.time()
            reg_time = int (reg_stop - reg_start)
            print(f'{roi} Elapsed time: ({datetime.timedelta(seconds=reg_time)})')
            print(f'{"*"*100}')

        except:
            e = sys.exc_info()[1]
            print(e.args[0])
            arcpy.AddError(e.args[0])

    elif roi in tauDem_dat:
        try:
            reg_start = time.time()
            wtdList = []
            arcpy.env.workspace = region
            gdb = arcpy.ListWorkspaces(workspace_type='FileGDB')
            ingdb = gdb[0]
            # set inputs
            cats = os.path.join(ingdb, "cats_merge")
            streams = os.path.join(ingdb, "streams_merge")
            outcats = os.path.join(ingdb, "awc_huc12_catchment_outlets")

            # Create list of catID/gridcode ids for outlet catchments
            idList = [int(row[0]) for row in arcpy.da.SearchCursor(outcats,'catID')]
            index_names = [i.name for i in arcpy.ListIndexes(cats)]
            if 'catid_index' not in index_names:
                print (f'Creating index for {cats}')
                arcpy.AddIndex_management(cats, "catID", "catid_index")
            else:
                print(f'{cats} Indexed')
            #watersheds feature dataset for storing fcs
            fdatname = roi + '_Watersheds'
            fdat = os.path.join(outgdb,fdatname)
            if not arcpy.Exists(fdat):
                arcpy.management.CreateFeatureDataset(outgdb, fdatname, sr)
            else:
                print(f'{fdat} exists for {roi}')
            fields = arcpy.ListFields(streams)
            if roi == 'Bristol_Bay':
                str_df_fields = ["catID", "upCatID1", "upCatID2"]
                str_df = pd.DataFrame(arcpy.da.FeatureClassToNumPyArray(streams, ("catID", "upCatID1", "upCatID2")))
                hws_codes = [999999, 1999999, 2999999, 3999999, 4999999]
            else:
                str_df_fields = ["LINKNO", "USLINKNO1", "USLINKNO2"]
                str_df = pd.DataFrame(arcpy.da.FeatureClassToNumPyArray(streams, ("LINKNO", "USLINKNO1", "USLINKNO2")))
                hws_codes = [-1]

            # Generate watersheds
            c=1
            for id in idList:
                iteration_start = time.time()
                print(f'{c}. Starting watershed for catchment {str(id)} ({(len(idList) - c)} remaining)')
                rec = [id]
                up_ids = []
                sum_rec = sum(rec)
                while(sum_rec > 0):
                    up_ids.append(rec)
                    rec = str_df.loc[str_df[str_df_fields[0]].isin(rec), (str_df_fields[1], str_df_fields[2])]
                    rec = pd.concat([rec[str_df_fields[1]], rec[str_df_fields[2]]])
                    sum_rec = sum(rec)
                # up_ids is a list with more than numbers, use extend to only keep numeric nhdplusids
                newup_ids = []
                for x in up_ids:
                    newup_ids.extend(x)

                tempLayer = "catsLyr"
                expression = '"catID" IN ({0})'.format(', '.join(map(str, newup_ids)) or 'NULL')
                arcpy.MakeFeatureLayer_management(cats, tempLayer)
                arcpy.management.SelectLayerByAttribute(tempLayer, "NEW_SELECTION", expression, None)
                print("Starting dissolve")
                outdis = "memory/wtd_" + str(round(id))
                outwtd = os.path.join(fdat,f'{roi}_wtd_{str(int(id))}')
                dis = arcpy.Dissolve_management(tempLayer, outdis)
                watershed = arcpy.EliminatePolygonPart_management(dis, outwtd,"PERCENT", "0 SquareKilometers", 90, "CONTAINED_ONLY")
                wtdList.append(watershed)
                append_value(wtdDict,roi,outwtd)

                # Stop iteration timer
                iteration_stop = time.time()
                iter_time = int (iteration_stop - iteration_start)
                print(f'Elapsed time: ({datetime.timedelta(seconds=iter_time)})')
                print(f'{"*"*60}')
                c+=1
            print(f'Begin merge all watersheds for {roi}')
            wtd_merge = arcpy.Merge_management(wtdList, os.path.join(ingdb,'awc_huc12_wtds_merge'),'','ADD_SOURCE_INFO')
            arcpy.AddField_management(wtd_merge,'cat_ID_con','TEXT')
            arcpy.AddField_management(wtd_merge,'cat_ID','DOUBLE')
            arcpy.AddField_management(wtd_merge,'cat_ID_txt','TEXT')
            with arcpy.da.UpdateCursor(wtd_merge,['MERGE_SRC','cat_ID_con','cat_ID','cat_ID_txt']) as cur:
                for row in cur:
                    gridcode= int(row[0].split('_')[-1])
                    row[1] = roi + '_' + str(gridcode)
                    row[2] = int(gridcode)
                    row[3] = str(gridcode)
                    cur.updateRow(row)
                del(row)
            del(cur)
            print(f'Additional copy of merged watersheds saved to {os.path.join(outgdb, f"{roi}_AwcHuc12_wtds_merge" )}')
            arcpy.CopyFeatures_management(wtd_merge,os.path.join(outgdb, f'{roi}_AwcHuc12_wtds_merge' ))

            # Stop iteration timer
            reg_stop = time.time()
            reg_time = int (reg_stop - reg_start)
            print(f'{roi} Elapsed time: ({datetime.timedelta(seconds=reg_time)})')
            print(f'{"*"*100}')

        except:
            e = sys.exc_info()[1]
            print(e.args[0])
            arcpy.AddError(e.args[0])
    else:
        print(f'{roi} not found - check inputs')
        sys.exit(f'{roi} not found - check inputs')

# End timing
processEnd = time.time()
processElapsed = int(processEnd - processStart)
processSuccess_time = datetime.datetime.now()

# Report success
print(f'Process completed at {processSuccess_time.strftime("%Y-%m-%d %H:%M")} '
      f'(Elapsed time: {datetime.timedelta(seconds=processElapsed)})')
print(f'{"*"*100}')




Bristol_Bay
D:\GIS\AKSSF\Bristol_Bay\Bristol_Bay.gdb\cats_merge Indexed
1. Starting watershed for catchment 1003859 (580 remaining)
Starting dissolve
Elapsed time: (0:00:01)
************************************************************
2. Starting watershed for catchment 1004129 (579 remaining)
Starting dissolve
Elapsed time: (0:00:01)
************************************************************
3. Starting watershed for catchment 1006868 (578 remaining)
Starting dissolve
Elapsed time: (0:00:01)
************************************************************
4. Starting watershed for catchment 1007408 (577 remaining)
Starting dissolve
Elapsed time: (0:00:01)
************************************************************
5. Starting watershed for catchment 1008168 (576 remaining)
Starting dissolve
Elapsed time: (0:00:01)
************************************************************
6. Starting watershed for catchment 1008527 (575 remaining)
Starting dissolve
Elapsed time: (0:00:01)
***********

## TROUBLESHOOTING BLOCK
### Zonal statistics as table is failing with unknown error when run on watershed_merge and slope/elev rasters if using 'ALL' statistics.
Try alternative methods.  Below is test chunk for iterating over a list of stats individually and join results back to a copy of the merged watershed table.
* Cannot Run ZonalStatistics because tool does not process overlapping polygons as individual features whereas ZonalStatistics as table will




In [20]:
### TEST CHUNK###

# import os, arcpy,time, datetime
# arcpy.env.overwriteOutput = True
#
# testoutgdb = r"C:\\Users\\dwmerrigan\\Documents\\GitHub\\ArcGIS_Default\\ArcGIS_Default.gdb"
# wtd_merge = r"D:\\GIS\\AKSSF_awcHuc12_cv\\AKSSF_awcHuc12_cv.gdb\\Cook_Inlet_AwcHuc12_wtds_merge"
# wtd_cur_fields = ['cat_ID_txt', 'cat_ID',"cat_ID_con"]
# elev_rast = r"D:\\GIS\\AKSSF\\Cook_Inlet\\elev.tif"
# zstats = ['MIN_MAX_MEAN','STD']
# roi = 'Cook_Inlet'
#
# # Elevation variables
# wtd_merge_elev_table_name = roi + "_Watersheds_Merge_ElevZstats"
# wtd_merge_elev_table_path = os.path.join(testoutgdb, wtd_merge_elev_table_name)
#
# # list to store zonal stat tables
# wtdelevstats =[]
#
# # Create field mappings
# elev_fm = arcpy.FieldMap()
# elev_fms = arcpy.FieldMappings()
# for field in arcpy.ListFields(wtd_merge)[6:]:
#     elev_fm = arcpy.FieldMap()
#     elev_fm.addInputField(wtd_merge,field.name)
#     elev_fm.mergeRule = 'First'
#     # Set properties of the output name.
#     f_name = elev_fm.outputField
#     f_name.name = field.name
#     f_name.aliasName = field.name
#     elev_fm.outputField = f_name
#     elev_fms.addFieldMap(elev_fm)
#
# # Make copy of watershed merge input as table to join stats fields
# wtd_elev_metrics_table = arcpy.TableToTable_conversion(wtd_merge,
#                                                        testoutgdb,
#                                                        wtd_merge_elev_table_name,
#                                                        '',
#                                                        elev_fms,
#                                                        )
# # Add region identifier field for watershed tables                                                )
# arcpy.AddField_management(wtd_elev_metrics_table,'region',field_type='TEXT')
# # expression to calculate region field with roi name
# exp =  '"'+roi+'"'
# arcpy.CalculateField_management(wtd_elev_metrics_table,'region',exp)
#
# zstat_start = time.time()
# for stat in zstats:
#     outstattable = os.path.join(testoutgdb,f'{roi}_wtdElev{stat}')
#     zstat_start1 = time.time()
#     try:
#         print (f'running {stat}')
#         stat_table = ZonalStatisticsAsTable(in_zone_data = wtdmerge,
#                                             zone_field = wtd_cur_fields[0],
#                                             in_value_raster = elev_rast,
#                                             out_table = outstattable,
#                                             statistics_type=stat
#                                             )
#
#         stat_fields = [f.name for f in arcpy.ListFields(stat_table)]
#         arcpy.JoinField_management(wtd_elev_metrics_table,
#                                wtd_cur_fields[0],
#                                stat_table,
#                                wtd_cur_fields[0],
#                                stat_fields[5:]
#                                )
#
#         # Report time
#         zstat_stop1 = time.time()
#         zstat_time1 = int (zstat_stop1 - zstat_start1)
#         print(f'Watershed elev Zonal Stats for {stat} Elapsed time: ({datetime.timedelta(seconds=zstat_time1)})')
#         print(f'{"*"*100}')
#     except:
#         e = sys.exc_info()[1]
#         print(e.args[0])
#         arcpy.AddError(e.args[0])
# # Report time
# zstat_stop = time.time()
# zstat_time = int (zstat_stop - zstat_start)
# print(f'Watershed elev Zonal Stats for {roi} Elapsed time: ({datetime.timedelta(seconds=zstat_time)})')
# print(f'{"*"*100}')

# Section 4 Calculate Covariates


In [21]:
from arcpy.sa import *
arcpy.env.workspace = data_dir
arcpy.env.overwriteOutput = True
sr = arcpy.SpatialReference(3338) #'NAD_1983_Alaska_Albers'
arcpy.env.outputCoordinateSystem = sr
regions  = arcpy.ListWorkspaces(workspace_type="Folder")

# Lists for variables not needed at present time
#cat_asp_ztables = []
#wtd_asp_ztables = []
#cat_pernorth_taba_tables=[]

# Lists to store output tables
wtd_pernorth_taba_tables=[]
wtd_lp_tabint_tables = []
wtd_glac_tabint_tables = []
wtd_wet_taba_tables = []
cat_elev_ztables = []
wtd_elev_ztables = []
cat_slope_ztables = []
wtd_slope_ztables = []
lcld_Ztables = []

# Clear lists
cat_cur_fields = []
wtd_cur_fields = []

# Start timing function
processStart = time.time()
processStartdt = datetime.datetime.now()

# Split data by type
nhdplus_dat = ['Cook_Inlet','Copper_River']
tauDem_dat = ['Bristol_Bay', 'Kodiak', 'Prince_William_Sound']

# Limit to ci for testing
#regions = ['D:\\GIS\\AKSSF\\Cook_Inlet', 'D:\\GIS\\AKSSF\\Copper_River' ,'D:\\GIS\\AKSSF\\Prince_William_Sound']
regions = ['D:\\GIS\\AKSSF\\Bristol_Bay', 'D:\\GIS\\AKSSF\\Kodiak','D:\\GIS\\AKSSF\\Prince_William_Sound']
#regions = ['D:\\GIS\\AKSSF\\Prince_William_Sound']
# Try with both data types
# regions = ['D:\\GIS\\AKSSF\\Prince_William_Sound','D:\\GIS\\AKSSF\\Cook_Inlet','D:\\GIS\\AKSSF\\Copper_River']

for region in regions:
    roi = os.path.basename(region)
    # expression to calculate region field with roi name
    exp =  '"'+roi+'"'
    if roi in nhdplus_dat:
        lakes_fc = nhd_lakes_fc
        # Fields for update cursor
        cat_cur_fields = ['cat_ID_txt', 'NHDPlusID',"cat_ID_con"]
        wtd_cur_fields = ['cat_ID_txt', 'cat_ID',"cat_ID_con"]
        print (f'{roi} in {nhdplus_dat} AKSSF list, using cat_fields {cat_cur_fields} and watershed fields {wtd_cur_fields}')
        print(f'{"*"*100}')
    # Set data and variables unique to regions with TauDEM Data
    elif roi in tauDem_dat:
        lakes_fc = tau_lakes_fc
        # Fields for update cursor
        if roi == 'Bristol_Bay':
            cat_cur_fields = ['cat_ID_txt', 'catID',"cat_ID_con"]
            wtd_cur_fields = ['cat_ID_txt', 'cat_ID',"cat_ID_con"]
        else:
            cat_cur_fields = ['cat_ID_txt', 'gridcode',"cat_ID_con"]
            wtd_cur_fields = ['cat_ID_txt', 'cat_ID',"cat_ID_con"]
        print (f'{roi} in {tauDem_dat} TauDEM list, using cat_fields {cat_cur_fields} and watershed fields {wtd_cur_fields}')
        print(f'{"*"*100}')
    # Start iter timing function
    iteration_start = time.time()
    # Set workspace to region folder
    arcpy.env.workspace = region
    walk = arcpy.da.Walk(region, datatype = ['FeatureClass','RasterDataset'])
    for dirpath, dirnames, filenames in walk:
        for filename in filenames:
            # Set merged watersheds dataset
            if 'awc_huc12_wtds_merge'== filename:
                wtdpath = os.path.join(dirpath,filename)
                wtdname = roi +'_'+ filename
                # Make local copy projected in AKAlbers
                wtd_merge = os.path.join(dirpath, filename)
                print(f'Merged watershed dataset {filename} found')
                print(f'{"*"*100}')
                wtdfieldnames = []
                wtdlstFields = arcpy.ListFields(wtd_merge)
                for field in wtdlstFields:
                    wtdfieldnames.append(field.name)
                if str(wtd_cur_fields[0]) in wtdfieldnames:
                    print (f'{wtd_cur_fields[0]} field already in dataset')
                    print(f'{"*"*100}')
                else:
                    print (f'Adding {wtd_cur_fields[0]} field to watershed dataset {wtd_merge}')
                    print(f'{"*"*100}')
                    # add cat_ID_txt field and concat cat_ID + region
                    arcpy.AddField_management(wtd_merge, str(wtd_cur_fields[0]),field_type='TEXT')
                    # populate cat_ID_txt
                    with arcpy.da.UpdateCursor(wtd_merge, wtd_cur_fields[0:2]) as cur:
                        for row in cur:
                            strval = str(row[1])
                            row[0] = strval.replace('.0',"")
                            # Update rows
                            cur.updateRow(row)
                        del(row)
                    del(cur)
                if str(wtd_cur_fields[2]) in wtdfieldnames:
                    print (f'{wtd_cur_fields[2]} field already in dataset {wtd_merge}')
                    print(f'{"*"*100}')
                else:
                    print (f'Adding {wtd_cur_fields[2]} field to watershed dataset {wtd_merge}')
                    print(f'{"*"*100}')
                    # add cat_ID_con field and concat cat_ID + region
                    arcpy.AddField_management(wtd_merge, str(wtd_cur_fields[2]),field_type='TEXT')
                    # populate cat_ID_txt
                    with arcpy.da.UpdateCursor(wtd_merge, wtd_cur_fields) as cur:
                        for row in cur:
                            strval = str(row[1])
                            row[2] = str(roi) +'_'+ strval.replace(".0","")
                            # Update rows
                            cur.updateRow(row)
                        del(row)
                    del(cur)

            # Select glaciers fc
            elif 'glaciers' == filename:
                # Make local copy projected in AKAlbers
                glacpath = os.path.join(dirpath, filename)
                glacname = roi+'_'+filename
                glac_fc = glacpath

            # Select elevation raster
            elif 'elev.tif' == filename:
                elev_rast = os.path.join(dirpath, filename)

            # # Select aspect raster
            # elif 'aspect' in filename:
            #     asp_rast = os.path.join(dirpath, filename)

            # Select north raster
            elif 'north.tif' == filename:
                nor_rast = os.path.join(dirpath, filename)

            # Select slope raster
            elif 'slope.tif' == filename:
                slope_rast = os.path.join(dirpath, filename)

            # Select wetland raster
            elif 'wetlands.tif' == filename:
                wet_rast = os.path.join(dirpath, filename)

            # Select catch_int fc (catchments of interest for region) and make a copy
            elif 'awc_huc12_catchment_outlets' == filename:
                # Make local copy projected in AKAlbers
                catspath = os.path.join(dirpath,filename)
                catsname = roi +"_"+filename
                cats = catspath
                catlstfields = arcpy.ListFields(cats)
                catfieldnames = []
                for field in catlstfields:
                    catfieldnames.append(field.name)
                if str(cat_cur_fields[0]) in catfieldnames:
                    print (f'{cat_cur_fields[0]} field already in dataset {cats}')
                    print(f'{"*"*100}')
                else:
                    print (f'Adding {cat_cur_fields[0]} field to catchment dataset {cats}')
                    print(f'{"*"*100}')
                    # add cat_ID_txt field
                    arcpy.AddField_management(cats, str(cat_cur_fields[0]), field_type='TEXT')
                    # populate cat_ID_txt
                    with arcpy.da.UpdateCursor(cats, cat_cur_fields[0:2]) as cur:
                        for row in cur:
                            strval = str(row[1])
                            row[0] = strval.replace('.0',"")
                            # Update rows
                            cur.updateRow(row)
                        del(row)
                    del(cur)
                if str(cat_cur_fields[2]) in catfieldnames:
                    print (f'{cat_cur_fields[2]} field already in dataset {cats}')
                    print(f'{"*"*100}')
                else:
                    print (f'Adding {cat_cur_fields[2]} field to catchment dataset {cats}')
                    print(f'{"*"*100}')
                    # add cat_ID_txt field & cat_ID + region concat field
                    arcpy.AddField_management(cats,str(cat_cur_fields[2]),field_type='TEXT')
                    # populate cat_ID_con
                    with arcpy.da.UpdateCursor(cats, cat_cur_fields) as cur:
                        for row in cur:
                            strval = str(row[1])
                            row[2] = str(roi) +'_'+ strval.replace('.0',"")
                            # Update rows
                            cur.updateRow(row)
                        del(row)
                    del(cur)

    print (f'Calculating topographic metrics for catchments & watersheds of interest in {roi} region')
    print ('----------')
    print(f'Geodatabase: {outgdb}')
    print ('----------')
    print (f'Watershed Merge: {wtd_merge}')
    print (f'  Projection {arcpy.Describe(wtd_merge).spatialReference.name}')
    print ('----------')
    print (f'HUC12 Catchment Outlets: {cats}')
    print (f'  Projection {arcpy.Describe(cats).spatialReference.name}')
    print ('----------')
    print (f'Elevation Raster: {elev_rast}')
    print (f'  Projection: {arcpy.Describe(elev_rast).spatialReference.name}')
    print ('----------')
    print (f'North Aspect Raster: {nor_rast}')
    print (f'  Projection: {arcpy.Describe(nor_rast).spatialReference.name}')
    print ('----------')
    print (f'Wetlands Raster: {wet_rast}')
    print (f'  Projection {arcpy.Describe(wet_rast).spatialReference.name}')
    print ('----------')
    print (f'Slope Raster: {slope_rast}')
    print (f'  Projection {arcpy.Describe(slope_rast).spatialReference.name}')
    print ('----------')
    print (f'Lakes Ponds fc: {lakes_fc}')
    print (f'  Projection {arcpy.Describe(lakes_fc).spatialReference.name}')
    print ('----------')
    print (f'Glaciers fc: {glac_fc} ')
    print (f'  Projection {arcpy.Describe(glac_fc).spatialReference.name}')
    print ('----------')
    print (f'{arcpy.GetCount_management(wtd_merge)} Watersheds to process')
    print ('----------')
    print (f'Catchment intersect {cats} selected')
    print ('----------')

    # # Aspect variables
    # wtd_merge_asp_table_name = roi + "_AwcHuc12_wtd_mer_AspectZstats"
    # wtd_merge_asp_table_path = os.path.join(outgdb, wtd_merge_asp_table_name)
    # cat_asp_table_name = roi + "_AwcHuc12_cats_AspectZstats"
    # cat_asp_table_path = os.path.join(outgdb, cat_asp_table_name)

    # Percent North variables
    wtd_merge_pernorth_table_name = roi + "_AwcHuc12_wtd_mer_PerNorth"
    wtd_merge_pernorth_table_path = os.path.join(outgdb, wtd_merge_pernorth_table_name)
    # cat_pernorth_table_name = roi + "_AwcHuc12_cats_PercentNorth"
    # cat_pernorth_table_path = os.path.join(outgdb, cat_pernorth_table_name)

    # Elevation variables
    wtd_merge_elev_table_name = roi + "_AwcHuc12_wtd_mer_ElevZstats"
    wtd_merge_elev_table_path = os.path.join(outgdb, wtd_merge_elev_table_name)
    cat_elev_table_name = roi + "_AwcHuc12_cats_ElevZstats"
    cat_elev_table_path = os.path.join(outgdb, cat_elev_table_name)

    # Slope variables
    wtd_merge_slope_table_name = roi + "_AwcHuc12_wtd_mer_SlopeZstats"
    wtd_merge_slope_table_path = os.path.join(outgdb, wtd_merge_slope_table_name)
    cat_slope_table_name = roi + "_AwcHuc12_cats_SlopeZstats"
    cat_slope_table_path = os.path.join(outgdb, cat_slope_table_name)

    # Lakes Ponds variables
    wtd_merge_lp_table_name = roi + "_AwcHuc12_wtd_mer_PerLakes"
    wtd_merge_lp_table_path = os.path.join(outgdb, wtd_merge_lp_table_name)
    cat_lp_table_name = roi + "_AwcHuc12_cats_PerLakes"
    cat_lp_path = os.path.join(outgdb, cat_lp_table_name)

    # Wetlands variables
    wtd_merge_wetlands_table_name = roi + "_AwcHuc12_wtd_mer_PerWet"
    wtd_merge_wetlands_table_path = os.path.join(outgdb, wtd_merge_wetlands_table_name)
    cat_wetlands_table_name = roi + "AwcHuc12_cats_PerWet"
    cat_wetlands_table_path = os.path.join(outgdb, cat_wetlands_table_name)

    # Glaciers
    wtd_merge_glac_table_name = roi + "_AwcHuc12_wtd_mer_PerGlac"
    wtd_merge_glac_table_path = os.path.join(outgdb, wtd_merge_glac_table_name)
    cat_glac_table_name = roi + "_AwcHuc12_cats_Glaciers"
    cat_glac_table_path = os.path.join(outgdb, cat_glac_table_name)

    try: # Zonal Stats section
        print(f'Begin Slope zonal statistics min/mean/max std dev for watersheds and catchments in {roi}'
              f' region')
        # Statistics to run for watersheds - 'ALL' is not an option at this time as tool will fail with unknown error
        zstats = ['MIN_MAX_MEAN','STD']
        # Begin Zonal Stats
        zstat_start = time.time()
        zstat_start1 = time.time()

        # Watershed slope Zonal Statistics
        print(f'Calculating {roi} watershed slope zonal stats...')
        arcpy.env.snapRaster = slope_rast
        arcpy.env.cellSize = slope_rast

        # Create field mappings
        slope_fm = arcpy.FieldMap()
        slope_fms = arcpy.FieldMappings()
        for field in arcpy.ListFields(wtd_merge)[6:]:
            slope_fm = arcpy.FieldMap()
            slope_fm.addInputField(wtd_merge,field.name)
            slope_fm.mergeRule = 'First'
            # Set properties of the output name.
            f_name = slope_fm.outputField
            f_name.name = field.name
            f_name.aliasName = field.name
            slope_fm.outputField = f_name
            slope_fms.addFieldMap(slope_fm)

        # Make copy of watershed merge input as table to join stats fields
        wtd_slope_metrics_table = arcpy.TableToTable_conversion(wtd_merge,
                                                               outgdb,
                                                               wtd_merge_slope_table_name,
                                                               '',
                                                               slope_fms,
                                                               )
        # Add region identifier field for watershed tables                                                )
        arcpy.AddField_management(wtd_slope_metrics_table,'region',field_type='TEXT')
        arcpy.CalculateField_management(wtd_slope_metrics_table,'region',exp)

        for stat in zstats:
            outstattable = os.path.join(outgdb,f'{roi}_wtdSlope_{stat}')
            zstat_start1 = time.time()
            print (f'running {stat}')
            stat_table = ZonalStatisticsAsTable(in_zone_data = wtd_merge,
                                                zone_field = wtd_cur_fields[0],
                                                in_value_raster = slope_rast,
                                                out_table = outstattable,
                                                statistics_type=stat
                                                )

            stat_fields = [f.name for f in arcpy.ListFields(stat_table)]
            arcpy.JoinField_management(wtd_slope_metrics_table,
                                   wtd_cur_fields[0],
                                   stat_table,
                                   wtd_cur_fields[0],
                                   stat_fields[5:] # Keep only stat field/s
                                   )

            # Report time
            zstat_stop1 = time.time()
            zstat_time1 = int (zstat_stop1 - zstat_start1)
            print(f'Watershed Slope Zonal {stat} for {roi} complete.\nElapsed time: ({datetime.timedelta(seconds=zstat_time1)})')
            print(f'{"*"*100}')

        # Append watershed slope table to list
        wtd_slope_ztables.append(wtd_slope_metrics_table)


        # Elevation Zonal statistics  for watersheds
        print(f'Begin Elevation zonal statistics min/mean/max std dev for watersheds and catchments in {roi}'
              f' region')
        zstat_start2 = time.time()
        arcpy.env.snapRaster = elev_rast
        arcpy.env.cellSize = elev_rast

        # Create field mappings
        elev_fm = arcpy.FieldMap()
        elev_fms = arcpy.FieldMappings()
        for field in arcpy.ListFields(wtd_merge)[6:]:
            elev_fm = arcpy.FieldMap()
            elev_fm.addInputField(wtd_merge,field.name)
            elev_fm.mergeRule = 'First'
            # Set properties of the output name.
            f_name = elev_fm.outputField
            f_name.name = field.name
            f_name.aliasName = field.name
            elev_fm.outputField = f_name
            elev_fms.addFieldMap(elev_fm)

        # Make copy of watershed merge input as table to join stats fields
        wtd_elev_metrics_table = arcpy.TableToTable_conversion(wtd_merge,
                                                               outgdb,
                                                               wtd_merge_elev_table_name,
                                                               '',
                                                               elev_fms,
                                                               )
        # Add region identifier field for watershed tables                                                )
        arcpy.AddField_management(wtd_elev_metrics_table,'region',field_type='TEXT')
        arcpy.CalculateField_management(wtd_elev_metrics_table,'region',exp)

        for stat in zstats:
            outstattable = os.path.join(outgdb,f'{roi}_wtdElev_{stat}')
            zstat_start1 = time.time()
            print (f'running {stat}')
            stat_table = ZonalStatisticsAsTable(in_zone_data = wtd_merge,
                                                zone_field = wtd_cur_fields[0],
                                                in_value_raster = elev_rast,
                                                out_table = outstattable,
                                                statistics_type=stat
                                                )

            stat_fields = [f.name for f in arcpy.ListFields(stat_table)]
            arcpy.JoinField_management(wtd_elev_metrics_table,
                                   wtd_cur_fields[0],
                                   stat_table,
                                   wtd_cur_fields[0],
                                   stat_fields[5:] # Keep only stat field/s
                                   )

            # Report time
            zstat_stop2 = time.time()
            zstat_time2 = int (zstat_stop2 - zstat_start2)
            print(f'Watershed Elevation Zonal {stat} for {roi} complete.\nElapsed time: ({datetime.timedelta(seconds=zstat_time2)})')
            print(f'{"*"*100}')
        # Append watershed elev table to list
        wtd_elev_ztables.append(wtd_elev_metrics_table)


        # Elevation zonal statistics for catchments
        print(f'Calculating {roi} catchment elevation zonal stats...')
        zstat_start3 = time.time()
        arcpy.env.snapRaster = elev_rast
        arcpy.env.cellSize = elev_rast
        cat_elev_metrics_table = ZonalStatisticsAsTable(in_zone_data = cats ,
                                                        zone_field = cat_cur_fields[0],
                                                        in_value_raster = elev_rast,
                                                        out_table = cat_elev_table_path,
                                                        statistics_type='ALL'
                                                        )
        # Add region identifier field for catchment table
        arcpy.AddField_management(cat_elev_metrics_table,'region',field_type='TEXT')
        # Add cat_ID_Con field
        arcpy.AddField_management(cat_elev_metrics_table,'cat_ID_con',field_type='TEXT')

        # Update fields
        with arcpy.da.UpdateCursor(cat_elev_metrics_table,['region','cat_ID_txt','cat_ID_con']) as cur:
            for row in cur:
                row[0] = roi
                strval = str(row[1])
                row[2] = roi+"_"+strval.replace(".0","")
                # Update
                cur.updateRow(row)
            del(row)
        del(cur)
        # Append catchment elev table to list
        cat_elev_ztables.append(cat_elev_metrics_table)
        # Report time
        zstat_stop3 = time.time()
        zstat_time3 = int (zstat_stop3 - zstat_start3)
        print(f'Elevation Zonal Stats for {roi} catchments complete.\nElapsed time: ({datetime.timedelta(seconds=zstat_time3)})')
        print(f'{"*"*100}')

        # Slope zonal statistics for catchments
        zstat_start4 = time.time()
        print(f'Calculating {roi} catchment slope zonal stats...')
        arcpy.env.snapRaster = slope_rast
        arcpy.env.cellSize = slope_rast
        cat_slope_metrics_table = ZonalStatisticsAsTable(in_zone_data = cats ,
                                                        zone_field = cat_cur_fields[0],
                                                        in_value_raster = slope_rast,
                                                        out_table = cat_slope_table_path,
                                                        statistics_type='ALL'
                                                        )
        # Add region identifier field for catchment table
        arcpy.AddField_management(cat_slope_metrics_table,'region',field_type='TEXT')
        # Add cat_ID_Con field
        arcpy.AddField_management(cat_slope_metrics_table,'cat_ID_con',field_type='TEXT')

        # Update region field
        with arcpy.da.UpdateCursor(cat_slope_metrics_table,['region','cat_ID_txt','cat_ID_con']) as cur:
            for row in cur:
                row[0] = roi
                strval =str(row[1])
                row[2] = roi+"_"+strval.replace(".0","")
                # Update
                cur.updateRow(row)
            del(row)
        del(cur)
        # Append catchment slope table to list
        cat_slope_ztables.append(cat_slope_metrics_table)
        # Report time
        zstat_stop4 = time.time()
        zstat_time4 = int (zstat_stop4 - zstat_start4)
        print(f'Slope Zonal Stats for {roi} catchments complete.\nElapsed time: ({datetime.timedelta(seconds=zstat_time4)})')
        print(f'{"*"*100}')


        # # Aspect Zonal statistics  for watersheds
        # print(f'Calculating {roi} watershed aspect zonal stats...')
        # wtd_asp_metrics_table = ZonalStatisticsAsTable(in_zone_data = wtd_merge, zone_field ="cat_ID_txt",
        #                                                in_value_raster = asp_rast, out_table = wtd_merge_asp_table_path,
        #                                                statistics_type='ALL')
        # arcpy.AddField_management(wtd_asp_metrics_table, 'region', field_type='TEXT')
        # Add cat_ID_Con field
        # arcpy.AddField_management(wtd_asp_metrics_table,'cat_ID_con',field_type='TEXT')
        # arcpy.CalculateField_management(wtd_asp_metrics_table, 'region', 'roi')
        # Update region field
        # with arcpy.da.UpdateCursor(wtd_asp_metrics_table,['region','cat_ID_txt','cat_ID_con']) as cur:
        #     for row in cur:
        #         row[0] = roi
        #         strval = str(row[1])
        #         row[2] = roi+"_"+strval.replace(".0","")
        #         # Update
        #         cur.updateRow(row)
        #     del(row)
        # del(cur)
        # wtd_asp_ztables.append(wtd_asp_metrics_table)

        # # Aspect Zonal statistics for catchments
        # print(f'Calculating {roi} catchment aspect zonal stats...')
        # cat_asp_metrics_table = ZonalStatisticsAsTable(in_zone_data = cats, zone_field ="cat_ID_txt",
        #                                                in_value_raster = asp_rast, out_table = cat_asp_table_path,
        #                                                statistics_type='ALL')
        # arcpy.AddField_management(cat_asp_metrics_table, 'region', field_type='TEXT')
        # Add cat_ID_Con field
        # arcpy.AddField_management(cat_asp_metrics_table,'cat_ID_con',field_type='TEXT')
        # arcpy.CalculateField_management(cat_asp_metrics_table, 'region', 'roi')
        # Update region field
        # with arcpy.da.UpdateCursor(cat_asp_metrics_table,['region','cat_ID_txt','cat_ID_con']) as cur:
        #     for row in cur:
        #         strval = str(row[1])
        #         row[2] = roi+"_"+strval.replace(".0","")
        #         # Update
        #         cur.updateRow(row)
        #     del(row)
        # del(cur)
        # cat_asp_ztables.append(cat_asp_metrics_table)

        zstat_stop = time.time()
        zstat_time = int (zstat_stop - zstat_start)
        print(f'All Zonal Stats for {roi} Elapsed time: ({datetime.timedelta(seconds=zstat_time)})')
        print(f'{"*"*100}')

        # Tabulate Area with north grid and watersheds
        tabarea_start = time.time()
        tabarea_start1 = time.time()
        print(f'Begin tabulate area of north facing cells for watersheds and catchments in {roi} region')
        print(f'{"*"*100}')
        # Percent North Tabulate area for watersheds
        wtd_per_north_tabarea = arcpy.sa.TabulateArea(in_zone_data= wtd_merge,
                                                      zone_field= wtd_cur_fields[0],
                                                      in_class_data=nor_rast,
                                                      class_field="Value",
                                                      out_table = wtd_merge_pernorth_table_path
                                                      )
        # Add region and percent north fields
        arcpy.AlterField_management(wtd_per_north_tabarea,'CAT_ID_TXT','CAT_ID_TXT_DEL','CAT_ID_TXT_DEL')
        arcpy.AddField_management(wtd_per_north_tabarea, 'region', field_type='TEXT')
        arcpy.AddField_management(wtd_per_north_tabarea, 'AwcHuc12_wtd_north_per', field_type='Float')
        arcpy.AddField_management(wtd_per_north_tabarea, wtd_cur_fields[0], field_type='TEXT')
        arcpy.AddField_management(wtd_per_north_tabarea, wtd_cur_fields[2], field_type='TEXT')
        wtdnorfields = [f.name for f in arcpy.ListFields(wtd_per_north_tabarea)]
        #print (wtdnorfields)
        with arcpy.da.UpdateCursor(wtd_per_north_tabarea, wtdnorfields) as cur:
            for row in cur:
                strval = str(row[1])
                row[4] = roi
                row[5] = row[3]/(row[3]+row[2])*100
                row[6] = strval.replace('.0','')
                row[7] = roi +'_'+ strval.replace(".0","")
                # Update
                cur.updateRow(row)
            del(row)
        del(cur)
        # Drop UPPERCASE field form tab area
        arcpy.DeleteField_management(wtd_per_north_tabarea,'CAT_ID_TXT_DEL')
        # Append watershed percent north table to list
        wtd_pernorth_taba_tables.append(wtd_per_north_tabarea)
        # Report tab area times
        tabarea_stop1 = time.time()
        tabarea_time1 = int (tabarea_stop1 - tabarea_start1)
        print(f'Watershed percent north Tabulate area/intersections for {roi} complete.\nElapsed time: ({datetime.timedelta(seconds=tabarea_time1)})')
        print(f'{"*"*100}')

        # Percent Lakes Ponds using Tabulate Intersection for watersheds
        print(f'Begin watershed percent lakes ponds for {roi}')
        tabarea_start2 = time.time()
        wtd_lp_tabint = arcpy.TabulateIntersection_analysis(wtd_merge,
                                                            zone_fields=wtd_cur_fields[0],
                                                            in_class_features=lakes_fc,
                                                            out_table=wtd_merge_lp_table_path,
                                                            class_fields='Ftype',
                                                            out_units="SQUARE_METERS"
                                                            )
        # Add region and cat id fields
        arcpy.AlterField_management(wtd_lp_tabint,'PERCENTAGE','AwcHuc12_wtd_lake_per','AwcHuc12_wtd_lake_per')
        arcpy.AlterField_management(wtd_lp_tabint,'AREA','AwcHuc12_wtd_lake_area_sqm','AwcHuc12_wtd_lake_area_sqm')
        arcpy.AddField_management(wtd_lp_tabint, 'region', field_type='TEXT')
        arcpy.AddField_management(wtd_lp_tabint, wtd_cur_fields[1], field_type='TEXT')
        arcpy.AddField_management(wtd_lp_tabint, wtd_cur_fields[2], field_type='TEXT')
        wtdlpfields = [f.name for f in arcpy.ListFields(wtd_lp_tabint)]
        #print (wtdlpfields)
        with arcpy.da.UpdateCursor(wtd_lp_tabint, wtdlpfields) as cur:
            for row in cur:
                strval = str(row[1])
                row[5] = roi
                row[6] = strval.replace('.0','')
                row[7] = roi +'_'+ strval.replace(".0","")
                # Update
                cur.updateRow(row)
            del(row)
        del(cur)

        # Append watershed lakes ponds table to list
        wtd_lp_tabint_tables.append(wtd_lp_tabint)
        # Report tab area times
        tabarea_stop2 = time.time()
        tabarea_time2 = int (tabarea_stop2 - tabarea_start2)
        print(f'Percent Lakes Tabulate area/intersections for {roi} complete.\nElapsed time: ({datetime.timedelta(seconds=tabarea_time2)})')
        print(f'{"*"*100}')

        # Percent glaciers using Tabulate Intersection for watersheds
        tabarea_start3 = time.time()
        print(f'Begin tabulate intersection between {glac_fc} and watersheds in {roi} region')
        print(f'{"*"*100}')
        wtd_glac_tabint = arcpy.TabulateIntersection_analysis(wtd_merge,
                                                            zone_fields=wtd_cur_fields[0],
                                                            in_class_features=glac_fc,
                                                            out_table=wtd_merge_glac_table_path,
                                                            class_fields='O1Region',
                                                            out_units="SQUARE_METERS"
                                                            )
        # Add region and cat id fields
        arcpy.AlterField_management(wtd_glac_tabint,'PERCENTAGE','AwcHuc12_wtd_glacier_per','AwcHuc12_wtd_glacier_per')
        arcpy.AlterField_management(wtd_glac_tabint,'AREA','AwcHuc12_wtd_glacier_area_sqm','AwcHuc12_wtd_glacier_area_sqm')
        arcpy.AddField_management(wtd_glac_tabint, 'region', field_type='TEXT')
        arcpy.AddField_management(wtd_glac_tabint, wtd_cur_fields[1], field_type='TEXT')
        arcpy.AddField_management(wtd_glac_tabint, wtd_cur_fields[2], field_type='TEXT')
        wtdglacfields = [f.name for f in arcpy.ListFields(wtd_glac_tabint)]
        #print (wtdglacfields)
        with arcpy.da.UpdateCursor(wtd_glac_tabint, wtdglacfields) as cur:
            for row in cur:
                strval = str(row[1])
                row[5] = roi
                row[6] = strval.replace('.0','')
                row[7] = roi +'_'+ strval.replace(".0","")
                # Update
                cur.updateRow(row)
            del(row)
        del(cur)
        # Append watershed percent glacier table to list
        wtd_glac_tabint_tables.append(wtd_glac_tabint)
        # Report tab area times
        tabarea_stop3 = time.time()
        tabarea_time3 = int (tabarea_stop3 - tabarea_start3)
        print(f'Percent Glacier Tabulate area/intersections for {roi} complete.\nElapsed time: ({datetime.timedelta(seconds=tabarea_time3)})')
        print(f'{"*"*100}')

        # Tabulate Area with wetlands grid and watersheds
        tabarea_start4 = time.time()
        print(f'Begin tabulate intersection between {wet_rast} and watersheds in {roi} region')
        print(f'{"*"*100}')
        # Wetlands tabulate area for watersheds
        wtd_per_wet_tabarea = arcpy.sa.TabulateArea(in_zone_data= wtd_merge,
                                                      zone_field= wtd_cur_fields[0],
                                                      in_class_data=wet_rast,
                                                      class_field="Value",
                                                      out_table=wtd_merge_wetlands_table_path
                                                      )
        # Add region and percent wet fields
        arcpy.AlterField_management(wtd_per_wet_tabarea,'CAT_ID_TXT','CAT_ID_TXT_DEL','CAT_ID_TXT_DEL')
        arcpy.AddField_management(wtd_per_wet_tabarea, 'region', field_type='TEXT')
        arcpy.AddField_management(wtd_per_wet_tabarea, 'AwcHuc12_wtd_wet_per', field_type='Float')
        arcpy.AddField_management(wtd_per_wet_tabarea, wtd_cur_fields[0], field_type='TEXT')
        arcpy.AddField_management(wtd_per_wet_tabarea, wtd_cur_fields[2], field_type='TEXT')
        wtdwetfields = [f.name for f in arcpy.ListFields(wtd_per_wet_tabarea)]
        #print (wtdwetfields)
        with arcpy.da.UpdateCursor(wtd_per_wet_tabarea, wtdwetfields) as cur:
            for row in cur:
                strval = str(row[1])
                row[4] = roi
                row[5] = row[3]/(row[3]+row[2])*100
                row[6] = strval.replace('.0','')
                row[7] = roi +'_'+ strval.replace(".0","")
                # Update
                cur.updateRow(row)
            del(row)
        del(cur)
        # Drop UPPERCASE field form tab area
        arcpy.DeleteField_management(wtd_per_wet_tabarea,'CAT_ID_TXT_DEL')
        # Append watershed percent wetlands table to list
        wtd_wet_taba_tables.append(wtd_per_wet_tabarea)
        # Report tab area times
        tabarea_stop4 = time.time()
        tabarea_time4 = int (tabarea_stop4 - tabarea_start4)
        print(f'Percent Wetlands Tabulate area/intersections for {roi} complete.\nElapsed time: ({datetime.timedelta(seconds=tabarea_time4)})')
        print(f'{"*"*100}')

        # # Percent North Tabulate Area for catchments
        # cat_per_north_tabarea = arcpy.sa.TabulateArea(in_zone_data= cats, zone_field='cat_ID_con',
        #                                             in_class_data=nor_rast,"Value",
        #                                             out_table=cat_pernorth_table_path)

        # # Add and calculate region identifier field for catchment table
        # arcpy.AlterField_management(cat_per_north_tabarea,'CAT_ID_TXT','CAT_ID_TXT_DEL','CAT_ID_TXT_DEL')
        # arcpy.AddField_management(cat_per_north_tabarea, 'region', field_type='TEXT')
        # arcpy.AddField_management(cat_per_north_tabarea, 'cat_north_per', field_type='Float')
        # arcpy.AddField_management(cat_per_north_tabarea, cat_cur_fields[0], field_type='TEXT')
        # arcpy.AddField_management(cat_per_north_tabarea, cat_cur_fields[2], field_type='TEXT')
        # catnorfields = [f.name for f in arcpy.ListFields(cat_per_north_tabarea)]
        # print (catnorfields)
        # with arcpy.da.UpdateCursor(cat_per_north_tabarea,catnorfields) as cur:
        #     for row in cur:
        #         strval = str(row[1])
        #         row[4] = roi
        #         row[5] = row[3]/(row[3]+row[2])*100
        #         row[6] = strval.replace('.0','')
        #         row[7] = roi +'_'+ strval.replace(".0","")
        #         # Update
        #         cur.updateRow(row)
        #     del(row)
        # del(cur)
        # Drop UPPERCASE field form tab area
        # arcpy.DeleteField_management(cat_per_north_tabarea,'CAT_ID_TXT_DEL')
        # # Append catchment percent north table to list
        # cat_pernorth_taba_tables.append(cat_per_north_tabarea)
        # Report tab area times
        tabarea_stop = time.time()
        tabarea_time = int (tabarea_stop - tabarea_start)
        print(f'Tabulate area/intersections for {roi} complete\nElapsed time: ({datetime.timedelta(seconds=tabarea_time)})')
        print(f'{"*"*100}')

        # Begin LCLD calculations
        walk = arcpy.da.Walk(lcld_folder, datatype='RasterDataset')
        for dirpath, dirnames, filenames in walk:
            for filename in filenames:
                raspath = os.path.join(dirpath, filename)
                year = filename[0:4]
                lcld_outname = roi+'_AwcHuc12_lcld_'+str(year)+'_zStats'
                lcld_outpath = os.path.join(outgdb, lcld_outname)
                print(f'Year: {year} - raster path {raspath}')
                colname = 'AwcHuc12_wtd_lcld_mn_' + str(year)
                # lcld zonal statistics as table for all akssf watersheds
                print(f'Calculating {filename} zonal stats for all {roi} watersheds...')
                #arcpy.env.snapRaster = raspath
                #arcpy.env.cellSize = raspath

                # Begin Zonal Stats
                lcldzstat_start = time.time()
                print(f'Begin zonal stats for {filename}')
                lcld_table = ZonalStatisticsAsTable(in_zone_data = wtd_merge,
                                                                zone_field = 'cat_ID_con',
                                                                in_value_raster = raspath,
                                                                out_table = lcld_outpath,
                                                                statistics_type='MEAN'
                                                                )
                # Append zTable to table list
                lcld_Ztables.append(lcld_outpath)
                arcpy.AlterField_management(lcld_table,'MEAN', colname,colname)
                proc_list = [row[0] for row in arcpy.da.SearchCursor(lcld_table,'cat_ID_con')]
                lcldzstat_stop = time.time()
                lcldzstat_time = int (lcldzstat_stop - lcldzstat_start)
                print(f'Zonal Stats for {filename} - Elapsed time: ({datetime.timedelta(seconds=lcldzstat_time)})')


    except:
        e = sys.exc_info()[1]
        print(f'ERRFLAG!!! = {e.args[0]}')
        arcpy.AddError(e.args[0])

    iter_stop = time.time()
    iter_time = int(iter_stop - iteration_start)
    print(f'All Covariates for {roi} completed.\nElapsed time: ({datetime.timedelta(seconds=iter_time)})')
    print(f'{"*"*100}')

# End timing
processEnd = time.time()
processElapsed = int(processEnd - processStart)
processSuccess_time = datetime.datetime.now()

# Report success
print(f'Process completed at {processSuccess_time.strftime("%Y-%m-%d %H:%M")} '
      f'(Elapsed time: {datetime.timedelta(seconds=processElapsed)})')
print(f'{"*"*100}')


Bristol_Bay in ['Bristol_Bay', 'Kodiak', 'Prince_William_Sound'] TauDEM list, using cat_fields ['cat_ID_txt', 'catID', 'cat_ID_con'] and watershed fields ['cat_ID_txt', 'cat_ID', 'cat_ID_con']
****************************************************************************************************
Adding cat_ID_txt field to catchment dataset D:\GIS\AKSSF\Bristol_Bay\Bristol_Bay.gdb\awc_huc12_catchment_outlets
****************************************************************************************************
Adding cat_ID_con field to catchment dataset D:\GIS\AKSSF\Bristol_Bay\Bristol_Bay.gdb\awc_huc12_catchment_outlets
****************************************************************************************************
Merged watershed dataset awc_huc12_wtds_merge found
****************************************************************************************************
cat_ID_txt field already in dataset
***************************************************************************************

## Examine LCLD tables and merge/export
* Discovered one watershed for PWS (Prince_William_Sound_23854) only has 6 years of LCLD data attributed to it.  Modis Coverage along the Coastline and PWS in particular is poor and many of the Islands/Coastlines have limited coverage.

In [22]:
arcpy.env.workspace = outgdb
lcld_Ztables = [t for t in arcpy.ListTables('*AwcHuc12_lcld_*')]
from collections import OrderedDict
lcld_Dict = {}
dfs = []
lcld_cols = []
drop_cols = ['OBJECTID','ZONE_CODE', 'AREA', 'COUNT']
for table in lcld_Ztables:
    cols = [f.name for f in arcpy.ListFields(table)]
    search_cols = [x for x in cols if x not in drop_cols]
    #cols.remove(drop_cols)
    print(search_cols)
    lcld_cols.append(search_cols)
    tblname = table[-16:]
    print(tblname)
    with arcpy.da.SearchCursor(table, search_cols) as cur:
        for row in cur:
            #print(f'row  - {row} = {lcld_Dict,row[0],row[1]}')
            append_value(lcld_Dict,row[0],row[1])


lcld_cols = [item for sublist in lcld_cols for item in sublist]
lcld_cols = list(OrderedDict.fromkeys(lcld_cols))
print(lcld_cols)

#Create list of tuples containing unique id followed by mean lcld for years 2001-2019
row_values = [(k,)+tuple(v) for k,v in lcld_Dict.items()]

['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2001']
lcld_2001_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2002']
lcld_2002_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2003']
lcld_2003_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2004']
lcld_2004_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2005']
lcld_2005_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2006']
lcld_2006_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2007']
lcld_2007_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2008']
lcld_2008_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2009']
lcld_2009_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2010']
lcld_2010_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2011']
lcld_2011_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2012']
lcld_2012_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2013']
lcld_2013_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2014']
lcld_2014_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2015']
lcld_2015_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2016']
lcld_2016_zStats
['cat_ID_con', 'AwcHuc12

Create an empty table to append yearly data
 * Attempting to convert to df and numpy arrays has been unsuccessful

In [23]:
lcld_table = arcpy.CreateTable_management(outgdb,'AKSSF_awcHuc12_ALL_LCLD_mn')
arcpy.AddField_management(lcld_table.getOutput(0),lcld_cols[0],'TEXT')
cur = arcpy.da.InsertCursor(lcld_table.getOutput(0),lcld_cols[0])
# Populate table with cat_ID_con values stored in list of lcld tuples
try:
    for row in row_values:
        cur.insertRow([row[0]])
        del(row)
    del(cur)
except:
    e = sys.exc_info()[1]
    print(f'ERRFLAG!!! = {e.args[0]}\n')
    # Get the traceback object
    tb = sys.exc_info()[2]
    tbinfo = traceback.format_tb(tb)[0]
    # Concatenate information together concerning the error into a message string
    pymsg = "PYTHON ERRORS:\nTraceback info:\n" + tbinfo + "\nError Info:\n" + str(sys.exc_info()[1])
    msgs = "ArcPy ERRORS:\n" + arcpy.GetMessages(2) + "\n"
    # Return Python error messages for use in script tool or Python window
    arcpy.AddError(pymsg)
    arcpy.AddError(msgs)
    # Print Python error messages for use in Python / Python window
    print(pymsg)
    print(msgs)
    arcpy.AddError(e.args[0])
print(f'LCDL table has {arcpy.GetCount_management(lcld_table)} records of {len(row_values)} input rows')

LCDL table has 805 records of 805 input rows


In [24]:

years = [x for x in range(2001,2020)]
lcldyr_Dict = {}
for y in years:
    for table in lcld_Ztables:
        if str(y) in table:
            append_value(lcldyr_Dict,str(y),table)
#print(lcldyr_Dict)

for k, v in lcldyr_Dict.items():
    year = k
    intables = v
    print (f'{year} using tables {intables} with val {v}\n')
    tempTable = arcpy.Merge_management(v,f'memory\\tempTable')
    infields = [f.name for f in arcpy.ListFields(tempTable)]
    print(f'Joining field {infields[5]} from {tempTable} to {lcld_table}')
    print(f'{"*"*100}\n')
    arcpy.JoinField_management(lcld_table,lcld_cols[0],tempTable,lcld_cols[0],infields[5])

2001 using tables ['Bristol_Bay_AwcHuc12_lcld_2001_zStats', 'Kodiak_AwcHuc12_lcld_2001_zStats', 'Prince_William_Sound_AwcHuc12_lcld_2001_zStats'] with val ['Bristol_Bay_AwcHuc12_lcld_2001_zStats', 'Kodiak_AwcHuc12_lcld_2001_zStats', 'Prince_William_Sound_AwcHuc12_lcld_2001_zStats']

Joining field AwcHuc12_wtd_lcld_mn_2001 from memory\tempTable to D:\GIS\outputs_20230518\outputs_20230518.gdb\AKSSF_awcHuc12_ALL_LCLD_mn
****************************************************************************************************

2002 using tables ['Bristol_Bay_AwcHuc12_lcld_2002_zStats', 'Kodiak_AwcHuc12_lcld_2002_zStats', 'Prince_William_Sound_AwcHuc12_lcld_2002_zStats'] with val ['Bristol_Bay_AwcHuc12_lcld_2002_zStats', 'Kodiak_AwcHuc12_lcld_2002_zStats', 'Prince_William_Sound_AwcHuc12_lcld_2002_zStats']

Joining field AwcHuc12_wtd_lcld_mn_2002 from memory\tempTable to D:\GIS\outputs_20230518\outputs_20230518.gdb\AKSSF_awcHuc12_ALL_LCLD_mn
********************************************************

In [25]:
# Convert to df and examine
# Make catchment lcld df
lcld_df = pd.DataFrame()
lcld_field_list = []
for field in arcpy.ListFields(lcld_table):
    lcld_field_list.append(field.name)
lcld_arr = arcpy.da.TableToNumPyArray(lcld_table,lcld_field_list)
lcld_df = pd.DataFrame(lcld_arr)
#lcld_df = lcld_df.drop(["OBJECTID","AwcHuc12_cat_elev_ZONE_CODE"],axis=1)
lcld_df = lcld_df.set_index('cat_ID_con')
#dfs.append(lcld_df)
lcld_df


OBJECTID  AwcHuc12_wtd_lcld_mn_2001  \
cat_ID_con                                                        
Bristol_Bay_1003859                1                 498.455807   
Bristol_Bay_1004129                2                 502.010116   
Bristol_Bay_1006868                3                 489.903477   
Bristol_Bay_1007408                4                 474.249194   
Bristol_Bay_1008168                5                 475.257172   
Bristol_Bay_1008527                6                 492.340235   
Bristol_Bay_1008597                7                 458.097105   
Bristol_Bay_1013111                8                 417.809235   
Bristol_Bay_1013306                9                 446.836640   
Bristol_Bay_1013765               10                 468.245079   
Bristol_Bay_1014251               11                 428.934352   
Bristol_Bay_1014341               12                 463.903521   
Bristol_Bay_1014516               13                 458.398097   
Bristol_Bay_1014641               14                 413.475299   
Bristol_Bay_1014786               15                 431.167366   
Bristol_Bay_1014821               16                 481.083656   
Bristol_Bay_1015186               17                 492.303775   
Bristol_Bay_1015281               18                 475.355691   
Bristol_Bay_1015516               19                 481.522403   
Bristol_Bay_1015685               20                 498.386584   
Bristol_Bay_1015771               21                 462.998699   
Bristol_Bay_1015821               22                 458.416158   
Bristol_Bay_1016325               23                 502.928045   
Bristol_Bay_1016515               24                 478.751408   
Bristol_Bay_1016825               25                 447.442045   
Bristol_Bay_1021823               26                 414.523728   
Bristol_Bay_1021914               27                 518.995709   
Bristol_Bay_1021984               28                 432.043196   
Bristol_Bay_1022264               29                 429.365305   
Bristol_Bay_1023034               30                 470.377071   
Bristol_Bay_1025113               31                 507.252904   
Bristol_Bay_1025432               32                 428.857623   
Bristol_Bay_1025533               33                 488.258449   
Bristol_Bay_1025683               34                 508.095647   
Bristol_Bay_1025783               35                 433.526570   
Bristol_Bay_1026233               36                 417.388678   
Bristol_Bay_1026463               37                 428.329983   
Bristol_Bay_1026613               38                 505.521983   
Bristol_Bay_1026983               39                 459.720617   
Bristol_Bay_1027852               40                 430.438721   
Bristol_Bay_1028212               41                 510.128934   
Bristol_Bay_1028322               42                 496.323281   
Bristol_Bay_1029732               43                 509.646140   
Bristol_Bay_1029872               44                 476.326014   
Bristol_Bay_1030072               45                 432.272771   
Bristol_Bay_1030462               46                 417.794413   
Bristol_Bay_1030642               47                 423.511440   
Bristol_Bay_1031022               48                 489.357250   
Bristol_Bay_2019750               49                 557.672064   
Bristol_Bay_2020120               50                 553.604577   
Bristol_Bay_2040341               51                 549.573135   
Bristol_Bay_2041261               52                 545.492641   
Bristol_Bay_2042341               53                 537.392748   
Bristol_Bay_2060975               54                 461.988276   
Bristol_Bay_2061205               55                 477.024447   
Bristol_Bay_2061325               56                 469.178089   
Bristol_Bay_2063167               57                 482.815156   
Bristol_Bay_2063257               58                 530.224999   
Bristol_

In [26]:
# Export LCLD table
arcpy.TableToTable_conversion(lcld_table,outdir,'AKSSF_awcHuc12_wtd_lcld_mn.csv')
print(f'Table exported...{outdir}')


Table exported...D:\GIS\outputs_20230518


## Drop unnecessary fields and rename as needed from merged tables.
- Create Key value dictionary and use update cursor to rename fields.

In [27]:

# Input table names/paths
cat_elev_ztables = [t for t in arcpy.ListTables('*_AwcHuc12_cats_ElevZstats')]
cat_slope_ztables = [t for t in arcpy.ListTables('*_AwcHuc12_cats_SlopeZstats')]
wtd_elev_ztables = [t for t in arcpy.ListTables('*_AwcHuc12_wtd_mer_ElevZstats')]
wtd_slope_ztables = [t for t in arcpy.ListTables('*_AwcHuc12_wtd_mer_SlopeZstats')]
wtd_pernorth_taba_tables = [t for t in arcpy.ListTables('*_AwcHuc12_wtd_mer_PerNorth')]
wtd_wet_taba_tables = [t for t in arcpy.ListTables('*_AwcHuc12_wtd_mer_PerWet')]
wtd_glac_tabint_tables = [t for t in arcpy.ListTables('*_AwcHuc12_wtd_mer_PerGlac')]
wtd_lp_tabint_tables = [t for t in arcpy.ListTables('*_AwcHuc12_wtd_mer_PerLakes')]

# Output Table names/paths
wtd_per_north_table_out = os.path.join(outgdb, 'AKSSF_awchuc12_wtd_north_per')
cat_elev_table_out = os.path.join(outgdb,'AKSSF_awchuc12_cat_elev')
cat_slope_table_out = os.path.join(outgdb,'AKSSF_awchuc12_cat_slope')
wtd_elev_table_out = os.path.join(outgdb, 'AKSSF_awchuc12_wtd_elev')
wtd_per_glac_table_out = os.path.join(outgdb, 'AKSSF_awchuc12_wtd_glacier_per')
wtd_per_lp_table_out = os.path.join(outgdb, 'AKSSF_awchuc12_wtd_lakepond_per')
wtd_slope_table_out = os.path.join(outgdb, 'AKSSF_awchuc12_wtd_slope')
wtd_wet_table_out = os.path.join(outgdb, 'AKSSF_awchuc12_wtd_wetland_per')

# Merge all regional tables together
outtables = []
wtd_per_north = arcpy.Merge_management(wtd_pernorth_taba_tables, wtd_per_north_table_out)
arcpy.AlterField_management(wtd_per_north,"VALUE_0","AwcHuc12_non_north_area","AwcHuc12_non_north_area")
arcpy.AlterField_management(wtd_per_north,"VALUE_1","AwcHuc12_north_area","AwcHuc12_north_area")
outtables.append(wtd_per_north)
cat_elev = arcpy.Merge_management(cat_elev_ztables, cat_elev_table_out)
outtables.append(cat_elev)
wtd_elev = arcpy.Merge_management(wtd_elev_ztables, wtd_elev_table_out)
outtables.append(wtd_elev)
wtd_slope = arcpy.Merge_management(wtd_slope_ztables, wtd_slope_table_out)
outtables.append(wtd_slope)
cat_slope = arcpy.Merge_management(cat_slope_ztables, cat_slope_table_out)
outtables.append(cat_slope)
wtd_wet = arcpy.Merge_management(wtd_wet_taba_tables, wtd_wet_table_out)
arcpy.AlterField_management(wtd_wet,"VALUE_0","AwcHuc12_non_wetland_area","AwcHuc12_non_wetland_area")
arcpy.AlterField_management(wtd_wet,"VALUE_1","AwcHuc12_wetland_area","AwcHuc12_wetland_area")
outtables.append(wtd_wet)
wtd_glac = arcpy.Merge_management(wtd_glac_tabint_tables, wtd_per_glac_table_out)
outtables.append(wtd_glac)
wtd_lp = arcpy.Merge_management(wtd_lp_tabint_tables, wtd_per_lp_table_out)
outtables.append(wtd_lp)
print ('Tables merged')
print('----------')


Tables merged
----------


In [28]:
#Set up field dictionary
elevDict = { 'ZONE_CODE': ('AwcHuc12_cat_elev_ZONE_CODE', 'AwcHuc12_wtd_elev_ZONE_CODE'),
         'COUNT': ('AwcHuc12_cat_elev_COUNT', 'AwcHuc12_wtd_elev_COUNT'),
          'AREA': ('AwcHuc12_cat_elev_AREA', 'AwcHuc12_wtd_elev_AREA'),
          'MIN': ('AwcHuc12_cat_elev_MIN', 'AwcHuc12_wtd_elev_MIN'),
          'MAX': ('AwcHuc12_cat_elev_MAX', 'AwcHuc12_wtd_elev_MAX'),
          'RANGE': ('AwcHuc12_cat_elev_RANGE', 'AwcHuc12_wtd_elev_RANGE'),
          'MEAN': ('AwcHuc12_cat_elev_MEAN', 'AwcHuc12_wtd_elev_MEAN'),
          'STD': ('AwcHuc12_cat_elev_STD', 'AwcHuc12_wtd_elev_STD'),
          'SUM': ('AwcHuc12_cat_elev_SUM', 'AwcHuc12_wtd_elev_SUM'),
          'VARIETY': ('AwcHuc12_cat_elev_VARIETY', 'AwcHuc12_wtd_elev_VARIETY'),
          'MAJORITY': ('AwcHuc12_cat_elev_MAJORITY', 'AwcHuc12_wtd_elev_MAJORITY'),
          'MINORITY': ('AwcHuc12_cat_elev_MINORITY', 'AwcHuc12_wtd_elev_MINORITY'),
          'MEDIAN': ('AwcHuc12_cat_elev_MEDIAN', 'AwcHuc12_wtd_elev_MEDIAN'),
          'PCT90': ('AwcHuc12_cat_elev_PCT90', 'AwcHuc12_wtd_elev_PCT90')
         }

slopeDict = { 'ZONE_CODE': ('AwcHuc12_cat_slope_ZONE_CODE', 'AwcHuc12_wtd_slope_ZONE_CODE'),
         'COUNT': ('AwcHuc12_cat_slope_COUNT', 'AwcHuc12_wtd_slope_COUNT'),
          'AREA': ('AwcHuc12_cat_slope_AREA', 'AwcHuc12_wtd_slope_AREA'),
          'MIN': ('AwcHuc12_cat_slope_MIN', 'AwcHuc12_wtd_slope_MIN'),
          'MAX': ('AwcHuc12_cat_slope_MAX', 'AwcHuc12_wtd_slope_MAX'),
          'RANGE': ('AwcHuc12_cat_slope_RANGE', 'AwcHuc12_wtd_slope_RANGE'),
          'MEAN': ('AwcHuc12_cat_slope_MEAN', 'AwcHuc12_wtd_slope_MEAN'),
          'STD': ('AwcHuc12_cat_slope_STD', 'AwcHuc12_wtd_slope_STD'),
          'SUM': ('AwcHuc12_cat_slope_SUM', 'AwcHuc12_wtd_slope_SUM'),
          'VARIETY': ('AwcHuc12_cat_slope_VARIETY', 'AwcHuc12_wtd_slope_VARIETY'),
          'MAJORITY': ('AwcHuc12_cat_slope_MAJORITY', 'AwcHuc12_wtd_slope_MAJORITY'),
          'MINORITY': ('AwcHuc12_cat_slope_MINORITY', 'AwcHuc12_wtd_slope_MINORITY'),
          'MEDIAN': ('AwcHuc12_cat_slope_MEDIAN', 'AwcHuc12_wtd_slope_MEDIAN'),
          'PCT90': ('AwcHuc12_cat_slope_PCT90', 'AwcHuc12_wtd_slope_PCT90')
         }

# Rename fields for elevation tables
for field in arcpy.ListFields(wtd_elev):
    keyval = field.name
    if keyval in elevDict:
        newname = elevDict[keyval][1]
        newalias = elevDict[keyval][1]
        print (keyval, newname)
        arcpy.AlterField_management(wtd_elev, keyval, newname, newalias)

for field in arcpy.ListFields(cat_elev):
    keyval = field.name
    if keyval in elevDict:
        newname = elevDict[keyval][0]
        newalias = elevDict[keyval][0]
        print (keyval, newname)
        arcpy.AlterField_management(cat_elev, keyval, newname, newalias)

# Rename fields for slope tables
for field in arcpy.ListFields(wtd_slope):
    keyval = field.name
    if keyval in slopeDict:
        newname = slopeDict[keyval][1]
        newalias = slopeDict[keyval][1]
        print (keyval, newname)
        arcpy.AlterField_management(wtd_slope, keyval, newname, newalias)

for field in arcpy.ListFields(cat_slope):
    keyval = field.name
    if keyval in slopeDict:
        newname = slopeDict[keyval][0]
        newalias = slopeDict[keyval][0]
        print (keyval, newname)
        arcpy.AlterField_management(cat_slope, keyval, newname, newalias)

MIN AwcHuc12_wtd_elev_MIN
MAX AwcHuc12_wtd_elev_MAX
MEAN AwcHuc12_wtd_elev_MEAN
STD AwcHuc12_wtd_elev_STD
ZONE_CODE AwcHuc12_cat_elev_ZONE_CODE
COUNT AwcHuc12_cat_elev_COUNT
AREA AwcHuc12_cat_elev_AREA
MIN AwcHuc12_cat_elev_MIN
MAX AwcHuc12_cat_elev_MAX
RANGE AwcHuc12_cat_elev_RANGE
MEAN AwcHuc12_cat_elev_MEAN
STD AwcHuc12_cat_elev_STD
SUM AwcHuc12_cat_elev_SUM
VARIETY AwcHuc12_cat_elev_VARIETY
MAJORITY AwcHuc12_cat_elev_MAJORITY
MINORITY AwcHuc12_cat_elev_MINORITY
MEDIAN AwcHuc12_cat_elev_MEDIAN
PCT90 AwcHuc12_cat_elev_PCT90
MIN AwcHuc12_wtd_slope_MIN
MAX AwcHuc12_wtd_slope_MAX
MEAN AwcHuc12_wtd_slope_MEAN
STD AwcHuc12_wtd_slope_STD
ZONE_CODE AwcHuc12_cat_slope_ZONE_CODE
COUNT AwcHuc12_cat_slope_COUNT
AREA AwcHuc12_cat_slope_AREA
MIN AwcHuc12_cat_slope_MIN
MAX AwcHuc12_cat_slope_MAX
RANGE AwcHuc12_cat_slope_RANGE
MEAN AwcHuc12_cat_slope_MEAN
STD AwcHuc12_cat_slope_STD
SUM AwcHuc12_cat_slope_SUM
MEDIAN AwcHuc12_cat_slope_MEDIAN
PCT90 AwcHuc12_cat_slope_PCT90


### Create HUC12 fc for mapping and display purposes and add cat_ID_con to relate back to watersheds.

In [29]:
import arcpy, os
NHDPlusHUCS = os.path.join(outgdb,r'NHDPlusHUC12')
NHD_H_Hucs = os.path.join(outgdb,'NHD_H_HUC12')
nhd_hList = []
nhdPlusList = []
HUC12s2pointsDict = {}
sites  = os.path.join(outgdb,r'AKSSF_awcHuc12_outlet_cats_points')
with arcpy.da.SearchCursor(sites, ['cat_ID_con','HUC12']) as cur:
    for row in cur:
        regionname = row[0].rsplit('_', 1)[0]
        if regionname in nhdplus_dat:
            nhdPlusList.append(row[1])
        elif regionname in tauDem_dat:
            nhd_hList.append(row[1])
        #print(regionname)
        append_value(HUC12s2pointsDict,row[1],[row[0],regionname])
print(len(HUC12s2pointsDict))
HUC12s2pointsDict

1663


{'190202020501': ['Cook_Inlet_75004200000901', 'Cook_Inlet'],
 '190202020503': ['Cook_Inlet_75004200001724', 'Cook_Inlet'],
 '190202020705': ['Cook_Inlet_75004200000437', 'Cook_Inlet'],
 '190202020303': ['Cook_Inlet_75004200001493', 'Cook_Inlet'],
 '190202020511': ['Cook_Inlet_75004200009084', 'Cook_Inlet'],
 '190202021002': ['Cook_Inlet_75004200003619', 'Cook_Inlet'],
 '190202021003': ['Cook_Inlet_75004200001047', 'Cook_Inlet'],
 '190202020602': ['Cook_Inlet_75004200016346', 'Cook_Inlet'],
 '190202021201': ['Cook_Inlet_75004200010717', 'Cook_Inlet'],
 '190202021004': ['Cook_Inlet_75004200010096', 'Cook_Inlet'],
 '190202021103': ['Cook_Inlet_75004200003399', 'Cook_Inlet'],
 '190202020403': ['Cook_Inlet_75004200000722', 'Cook_Inlet'],
 '190202020101': ['Cook_Inlet_75004200000726', 'Cook_Inlet'],
 '190202021001': ['Cook_Inlet_75004200012986', 'Cook_Inlet'],
 '190202021303': ['Cook_Inlet_75004200008847', 'Cook_Inlet'],
 '190202021404': ['Cook_Inlet_75004200010465', 'Cook_Inlet'],
 '190202

## Select and Merge

In [30]:
# Select HUCS from respective datasets using appropriate lists
arcpy.env.overwriteOutput = True
field = 'HUC12'
operator = 'IN'
nhdPlusvalue = str(nhdPlusList).strip("[]")
nhdHvalue = str(nhd_hList).strip("[]")
nhdplussba = """"{}" {} ({})""".format(field, operator, nhdPlusvalue)
nhdhsba = """"{}" {} ({})""".format(field, operator, nhdHvalue)

# Make Selections using lists
nhdplus_select = arcpy.SelectLayerByAttribute_management(NHDPlusHUCS,'NEW_SELECTION', nhdplussba)
nhd_h_select = arcpy.SelectLayerByAttribute_management(NHD_H_Hucs,'NEW_SELECTION', nhdhsba)

print(f'Hucs in NHDPlusList = {len(nhdPlusList)}\nHucs in NHD_H_List = {len(nhd_hList)}\nTotal Hucs in lists = {len(nhd_hList) + len(nhdPlusList)}')
print (f'Total hucs selected for merge  = {int(arcpy.GetCount_management(nhdplus_select)[0]) + int(arcpy.GetCount_management(nhd_h_select)[0])}')

outHucname = "AKSSF_awcHuc12s"
outhucpath = os.path.join(outgdb,outHucname)
#Merge HUCS
arcpy.Merge_management([nhdplus_select,nhd_h_select],outhucpath,'','ADD_SOURCE_INFO')
arcpy.AddField_management(outhucpath,'cat_ID_con','TEXT')
arcpy.AddField_management(outhucpath,'region','TEXT')
print('Merge Complete')

# Use update cursor to add cat_ID_con to merged Hucs from value dictionary
with arcpy.da.UpdateCursor(outhucpath,['HUC12','cat_ID_con','region']) as cur:
    for row in cur:
        #print(f'HUC {row[0]} associated with catchment/watershed {HUC12s2pointsDict[row[0]][0]}')
        row[1] = HUC12s2pointsDict[row[0]][0]
        row[2] = HUC12s2pointsDict[row[0]][1]
        cur.updateRow(row)
    del(row)
del(cur)
print('cat_ID_con and region fields updated')



Hucs in NHDPlusList = 858
Hucs in NHD_H_List = 805
Total Hucs in lists = 1663
Total hucs selected for merge  = 1663
Merge Complete
cat_ID_con and region fields updated


## Export Tables


In [31]:
# # Export copies of dbf tables as csv
for table in outtables:
    tablename = arcpy.Describe(table).basename + ".csv"
    tablepath = os.path.join(outdir,tablename)
    print( tablepath)
    arcpy.conversion.TableToTable(table, outdir, tablename)

D:\GIS\outputs_20230518\AKSSF_awchuc12_wtd_north_per.csv
D:\GIS\outputs_20230518\AKSSF_awchuc12_cat_elev.csv
D:\GIS\outputs_20230518\AKSSF_awchuc12_wtd_elev.csv
D:\GIS\outputs_20230518\AKSSF_awchuc12_wtd_slope.csv
D:\GIS\outputs_20230518\AKSSF_awchuc12_cat_slope.csv
D:\GIS\outputs_20230518\AKSSF_awchuc12_wtd_wetland_per.csv
D:\GIS\outputs_20230518\AKSSF_awchuc12_wtd_glacier_per.csv
D:\GIS\outputs_20230518\AKSSF_awchuc12_wtd_lakepond_per.csv


In [32]:
import pandas as pd
pd.options.display.float_format = '{:.2f}'.format # only display 2 decimal places
# list to store covariate data frames
dfs = []

In [33]:
# Make catchment elev df
cat_df = pd.DataFrame()
cat_field_list = []
for field in arcpy.ListFields(cat_elev):
    cat_field_list.append(field.name)
cat_elev_arr = arcpy.da.TableToNumPyArray(cat_elev,cat_field_list)
cat_df = pd.DataFrame(cat_elev_arr)
cat_df = cat_df.drop(["OBJECTID","AwcHuc12_cat_elev_ZONE_CODE","region","cat_ID_txt"],axis=1)
cat_df = cat_df.set_index('cat_ID_con')
dfs.append(cat_df)
cat_df


AwcHuc12_cat_elev_COUNT  AwcHuc12_cat_elev_AREA  \
cat_ID_con                                                                    
Bristol_Bay_1003859                         2442.00               244200.00   
Bristol_Bay_1004129                          380.00                38000.00   
Bristol_Bay_1006868                        20499.00              2049900.00   
Bristol_Bay_1007408                        17509.00              1750900.00   
Bristol_Bay_1008168                        13266.00              1326600.00   
Bristol_Bay_1008527                        19118.00              1911800.00   
Bristol_Bay_1008597                         2299.00               229900.00   
Bristol_Bay_1013111                         2342.00               234200.00   
Bristol_Bay_1013306                         2292.00               229200.00   
Bristol_Bay_1013765                         3506.00               350600.00   
Bristol_Bay_1014251                          227.00                22700.00   
Bristol_Bay_1014341                         1854.00               185400.00   
Bristol_Bay_1014516                          929.00                92900.00   
Bristol_Bay_1014641                         8158.00               815800.00   
Bristol_Bay_1014786                         2842.00               284200.00   
Bristol_Bay_1014821                         1968.00               196800.00   
Bristol_Bay_1015186                         6630.00               663000.00   
Bristol_Bay_1015281                         4465.00               446500.00   
Bristol_Bay_1015516                        14462.00              1446200.00   
Bristol_Bay_1015685                        18349.00              1834900.00   
Bristol_Bay_1015771                         1571.00               157100.00   
Bristol_Bay_1015821                         1141.00               114100.00   
Bristol_Bay_1016325                         3355.00               335500.00   
Bristol_Bay_1016515                         2797.00               279700.00   
Bristol_Bay_1016825                        13973.00              1397300.00   
Bristol_Bay_1021823                         2164.00               216400.00   
Bristol_Bay_1021914                            1.00                  100.00   
Bristol_Bay_1021984                         2996.00               299600.00   
Bristol_Bay_1022264                         3043.00               304300.00   
Bristol_Bay_1023034                         9215.00               921500.00   
Bristol_Bay_1025113                        11051.00              1105100.00   
Bristol_Bay_1025432                         1193.00               119300.00   
Bristol_Bay_1025533                         5297.00               529700.00   
Bristol_Bay_1025683                        13682.00              1368200.00   
Bristol_Bay_1025783                          863.00                86300.00   
Bristol_Bay_1026233                         1101.00               110100.00   
Bristol_Bay_1026463                         4154.00               415400.00   
Bristol_Bay_1026613                         1556.00               155600.00   
Bristol_Bay_1026983                         9003.00               900300.00   
Bristol_Bay_1027852                         6344.00               634400.00   
Bristol_Bay_1028212                          314.00                31400.00   
Bristol_Bay_1028322                        10280.00              1028000.00   
Bristol_Bay_1029732                         5302.00               530200.00   
Bristol_Bay_1029872                         1692.00               169200.00   
Bristol_Bay_1030072                        30586.00              3058600.00   
Bristol_Bay_1030462                         8143.00               814300.00   
Bristol_Bay_1030642                         1288.00               128800.00   
Bristol_Bay_1031022                         1699.00               169900.00   
Bristol_Bay_2019750                          183.00                18300.00   

In [34]:
# Make catchment slope df
cat_sl_df = pd.DataFrame()
cat_sl_field_list = []
for field in arcpy.ListFields(cat_slope):
    cat_sl_field_list.append(field.name)
cat_sl_arr = arcpy.da.TableToNumPyArray(cat_slope, cat_sl_field_list)
cat_sl_df = pd.DataFrame(cat_sl_arr)
cat_sl_df = cat_sl_df.drop(["OBJECTID", "AwcHuc12_cat_slope_ZONE_CODE","region","cat_ID_txt"],axis=1)
cat_sl_df = cat_sl_df.set_index('cat_ID_con')
dfs.append(cat_sl_df)
cat_sl_df

AwcHuc12_cat_slope_COUNT  AwcHuc12_cat_slope_AREA  \
cat_ID_con                                                                      
Bristol_Bay_1003859                          2442.00                244200.00   
Bristol_Bay_1004129                           380.00                 38000.00   
Bristol_Bay_1006868                         20499.00               2049900.00   
Bristol_Bay_1007408                         17509.00               1750900.00   
Bristol_Bay_1008168                         13266.00               1326600.00   
Bristol_Bay_1008527                         19118.00               1911800.00   
Bristol_Bay_1008597                          2299.00                229900.00   
Bristol_Bay_1013111                          2342.00                234200.00   
Bristol_Bay_1013306                          2292.00                229200.00   
Bristol_Bay_1013765                          3506.00                350600.00   
Bristol_Bay_1014251                           227.00                 22700.00   
Bristol_Bay_1014341                          1854.00                185400.00   
Bristol_Bay_1014516                           929.00                 92900.00   
Bristol_Bay_1014641                          8158.00                815800.00   
Bristol_Bay_1014786                          2842.00                284200.00   
Bristol_Bay_1014821                          1968.00                196800.00   
Bristol_Bay_1015186                          6630.00                663000.00   
Bristol_Bay_1015281                          4465.00                446500.00   
Bristol_Bay_1015516                         14462.00               1446200.00   
Bristol_Bay_1015685                         18349.00               1834900.00   
Bristol_Bay_1015771                          1571.00                157100.00   
Bristol_Bay_1015821                          1141.00                114100.00   
Bristol_Bay_1016325                          3355.00                335500.00   
Bristol_Bay_1016515                          2797.00                279700.00   
Bristol_Bay_1016825                         13973.00               1397300.00   
Bristol_Bay_1021823                          2164.00                216400.00   
Bristol_Bay_1021914                             1.00                   100.00   
Bristol_Bay_1021984                          2996.00                299600.00   
Bristol_Bay_1022264                          3043.00                304300.00   
Bristol_Bay_1023034                          9215.00                921500.00   
Bristol_Bay_1025113                         11051.00               1105100.00   
Bristol_Bay_1025432                          1193.00                119300.00   
Bristol_Bay_1025533                          5297.00                529700.00   
Bristol_Bay_1025683                         13682.00               1368200.00   
Bristol_Bay_1025783                           863.00                 86300.00   
Bristol_Bay_1026233                          1101.00                110100.00   
Bristol_Bay_1026463                          4154.00                415400.00   
Bristol_Bay_1026613                          1556.00                155600.00   
Bristol_Bay_1026983                          9003.00                900300.00   
Bristol_Bay_1027852                          6344.00                634400.00   
Bristol_Bay_1028212                           314.00                 31400.00   
Bristol_Bay_1028322                         10280.00               1028000.00   
Bristol_Bay_1029732                          5302.00                530200.00   
Bristol_Bay_1029872                          1692.00                169200.00   
Bristol_Bay_1030072                         30586.00               3058600.00   
Bristol_Bay_1030462                          8143.00                814300.00   
Bristol_Bay_1030642                          1288.00                128800.00   
Bristol_Bay_1031022                          1699.00       

In [35]:
# Make watershed elev df
wtd_df = pd.DataFrame()
wtd_field_list = []
for field in arcpy.ListFields(wtd_elev):
    wtd_field_list.append(field.name)
wtd_elev_arr = arcpy.da.TableToNumPyArray(wtd_elev,wtd_field_list)
wtd_df = pd.DataFrame(wtd_elev_arr)
wtd_df = wtd_df.drop(["OBJECTID","cat_ID","region", "cat_ID_txt"],axis=1)
wtd_df = wtd_df.set_index('cat_ID_con')
dfs.append(wtd_df)
wtd_df

AwcHuc12_wtd_elev_MIN  AwcHuc12_wtd_elev_MAX  \
cat_ID_con                                                                 
Bristol_Bay_1003859                             4                    884   
Bristol_Bay_1004129                             5                    784   
Bristol_Bay_1006868                             4                    820   
Bristol_Bay_1007408                             4                    638   
Bristol_Bay_1008168                             4                    768   
Bristol_Bay_1008527                             8                    907   
Bristol_Bay_1008597                             4                    766   
Bristol_Bay_1013111                            45                    121   
Bristol_Bay_1013306                            10                    678   
Bristol_Bay_1013765                            44                    750   
Bristol_Bay_1014251                             8                    121   
Bristol_Bay_1014341                            60                    574   
Bristol_Bay_1014516                             6                   1471   
Bristol_Bay_1014641                            27                    128   
Bristol_Bay_1014786                             4                    601   
Bristol_Bay_1014821                            60                   2164   
Bristol_Bay_1015186                            10                   1843   
Bristol_Bay_1015281                            33                   2164   
Bristol_Bay_1015516                             4                   1843   
Bristol_Bay_1015685                             4                   1212   
Bristol_Bay_1015771                             0                   2164   
Bristol_Bay_1015821                             0                   2164   
Bristol_Bay_1016325                            39                   1843   
Bristol_Bay_1016515                            38                    582   
Bristol_Bay_1016825                             4                    983   
Bristol_Bay_1021823                             3                     69   
Bristol_Bay_1021914                            91                   1843   
Bristol_Bay_1021984                            13                    110   
Bristol_Bay_1022264                             7                    125   
Bristol_Bay_1023034                             4                   1843   
Bristol_Bay_1025113                           142                   1627   
Bristol_Bay_1025432                             2                     91   
Bristol_Bay_1025533                           134                   1006   
Bristol_Bay_1025683                           190                   1624   
Bristol_Bay_1025783                             4                    120   
Bristol_Bay_1026233                             2                    266   
Bristol_Bay_1026463                             2                    125   
Bristol_Bay_1026613                           140                   2164   
Bristol_Bay_1026983                             2                   1843   
Bristol_Bay_1027852                            68                    367   
Bristol_Bay_1028212                           215                   1270   
Bristol_Bay_1028322                           140                   1270   
Bristol_Bay_1029732                           169                   2164   
Bristol_Bay_1029872                           106                   1006   
Bristol_Bay_1030072                             1                    120   
Bristol_Bay_1030462                            12                    266   
Bristol_Bay_1030642                             2                     92   
Bristol_Bay_1031022                            75                   2164   
Bristol_Bay_2019750                           240                   2696   
Bristol_Bay_2020120                           209                   2696   
Bristol_Bay_2040341                           145                   3127   


In [36]:
# Make watershed slope df
wtd_sl_df = pd.DataFrame()
wtd_sl_field_list = []
for field in arcpy.ListFields(wtd_slope):
    wtd_sl_field_list.append(field.name)
wtd_sl_arr = arcpy.da.TableToNumPyArray(wtd_slope, wtd_sl_field_list)
wtd_sl_df = pd.DataFrame(wtd_sl_arr)
wtd_sl_df = wtd_sl_df.drop(["OBJECTID","cat_ID","region","cat_ID","cat_ID_txt"],axis=1)
wtd_sl_df = wtd_sl_df.set_index('cat_ID_con')
dfs.append(wtd_sl_df)
wtd_sl_df

AwcHuc12_wtd_slope_MIN  AwcHuc12_wtd_slope_MAX  \
cat_ID_con                                                                   
Bristol_Bay_1003859                           0.00                   66.37   
Bristol_Bay_1004129                           0.00                   73.40   
Bristol_Bay_1006868                           0.00                   64.50   
Bristol_Bay_1007408                           0.00                   69.63   
Bristol_Bay_1008168                           0.00                   69.45   
Bristol_Bay_1008527                           0.00                   65.65   
Bristol_Bay_1008597                           0.00                   59.33   
Bristol_Bay_1013111                           0.00                   28.27   
Bristol_Bay_1013306                           0.00                   62.87   
Bristol_Bay_1013765                           0.00                   51.61   
Bristol_Bay_1014251                           0.00                   29.36   
Bristol_Bay_1014341                           0.00                   31.69   
Bristol_Bay_1014516                           0.00                   44.97   
Bristol_Bay_1014641                           0.00                   28.27   
Bristol_Bay_1014786                           0.00                   53.81   
Bristol_Bay_1014821                           0.00                   79.29   
Bristol_Bay_1015186                           0.00                   78.01   
Bristol_Bay_1015281                           0.00                   79.29   
Bristol_Bay_1015516                           0.00                   78.01   
Bristol_Bay_1015685                           0.00                   76.97   
Bristol_Bay_1015771                           0.00                   79.29   
Bristol_Bay_1015821                           0.00                   79.29   
Bristol_Bay_1016325                           0.00                   73.55   
Bristol_Bay_1016515                           0.00                   55.84   
Bristol_Bay_1016825                           0.00                   68.53   
Bristol_Bay_1021823                           0.00                   19.25   
Bristol_Bay_1021914                           0.00                   71.82   
Bristol_Bay_1021984                           0.00                   27.87   
Bristol_Bay_1022264                           0.00                   27.87   
Bristol_Bay_1023034                           0.00                   78.01   
Bristol_Bay_1025113                           0.00                   77.21   
Bristol_Bay_1025432                           0.00                   22.01   
Bristol_Bay_1025533                           0.00                   49.87   
Bristol_Bay_1025683                           0.00                   79.29   
Bristol_Bay_1025783                           0.00                   30.56   
Bristol_Bay_1026233                           0.00                   33.07   
Bristol_Bay_1026463                           0.00                   27.87   
Bristol_Bay_1026613                           0.00                   79.29   
Bristol_Bay_1026983                           0.00                   78.01   
Bristol_Bay_1027852                           0.00                   26.61   
Bristol_Bay_1028212                           0.00                   67.75   
Bristol_Bay_1028322                           0.00                   70.42   
Bristol_Bay_1029732                           0.00                   75.29   
Bristol_Bay_1029872                           0.00                   50.57   
Bristol_Bay_1030072                           0.00                   30.56   
Bristol_Bay_1030462                           0.00                   33.07   
Bristol_Bay_1030642                           0.00                   32.58   
Bristol_Bay_1031022                           0.00                   79.29   
Bristol_Bay_2019750                           0.00                   79.14   
Bristol_Bay_2020120                           0.00

In [37]:
# Make watershed north df
wtd_n_df = pd.DataFrame()
wtd_n_field_list = []
for field in arcpy.ListFields(wtd_per_north):
    wtd_n_field_list.append(field.name)
wtd_n_arr = arcpy.da.TableToNumPyArray(wtd_per_north,wtd_n_field_list)
wtd_n_df = pd.DataFrame(wtd_n_arr)
wtd_n_df = wtd_n_df.drop(["OBJECTID","region","cat_ID_txt"],axis=1)
wtd_n_df = wtd_n_df.set_index('cat_ID_con')
dfs.append(wtd_n_df)
wtd_n_df

AwcHuc12_non_north_area  AwcHuc12_north_area  \
cat_ID_con                                                                 
Bristol_Bay_1003859                     28858800.00          11117100.00   
Bristol_Bay_1004129                     31559900.00          13776000.00   
Bristol_Bay_1006868                     28295800.00           7494500.00   
Bristol_Bay_1007408                     28011800.00          14585000.00   
Bristol_Bay_1008168                     31691300.00          13906600.00   
Bristol_Bay_1008527                     48138000.00          21431500.00   
Bristol_Bay_1008597                     79852800.00          38042100.00   
Bristol_Bay_1013111                     47818500.00           8398100.00   
Bristol_Bay_1013306                     67294700.00          32347100.00   
Bristol_Bay_1013765                     38967200.00          10430700.00   
Bristol_Bay_1014251                    124763400.00          17990400.00   
Bristol_Bay_1014341                     86907200.00          34984200.00   
Bristol_Bay_1014516                     46516300.00          14396700.00   
Bristol_Bay_1014641                    220276100.00          36181000.00   
Bristol_Bay_1014786                     56522800.00          25367000.00   
Bristol_Bay_1014821                   1232531000.00         416769000.00   
Bristol_Bay_1015186                    483514400.00          84106000.00   
Bristol_Bay_1015281                   1427660800.00         471785200.00   
Bristol_Bay_1015516                    600063400.00         129078800.00   
Bristol_Bay_1015685                     77776500.00          22390200.00   
Bristol_Bay_1015771                   1959145800.00         552734800.00   
Bristol_Bay_1015821                   5850097900.00        1160288400.00   
Bristol_Bay_1016325                    302127300.00          49813700.00   
Bristol_Bay_1016515                     37588200.00          20518200.00   
Bristol_Bay_1016825                     65902300.00           4449300.00   
Bristol_Bay_1021823                     37701100.00           5083600.00   
Bristol_Bay_1021914                    120230800.00          11926200.00   
Bristol_Bay_1021984                     82255500.00          18297800.00   
Bristol_Bay_1022264                    156216800.00          30680100.00   
Bristol_Bay_1023034                   2803880800.00         453965800.00   
Bristol_Bay_1025113                     79126400.00          42217900.00   
Bristol_Bay_1025432                     52812300.00          11463300.00   
Bristol_Bay_1025533                     95288700.00          36030100.00   
Bristol_Bay_1025683                    134842500.00          52058200.00   
Bristol_Bay_1025783                    101125100.00          17298000.00   
Bristol_Bay_1026233                    186909800.00          19340700.00   
Bristol_Bay_1026463                    228338800.00          41689100.00   
Bristol_Bay_1026613                    537324200.00         216247400.00   
Bristol_Bay_1026983                   3380456500.00         533124800.00   
Bristol_Bay_1027852                     64427100.00          53846800.00   
Bristol_Bay_1028212                    127050700.00          19427000.00   
Bristol_Bay_1028322                    216260100.00          32518900.00   
Bristol_Bay_1029732                    241174200.00          97011400.00   
Bristol_Bay_1029872                    150526700.00          67756700.00   
Bristol_Bay_1030072                    166887000.00          25902800.00   
Bristol_Bay_1030462                     86969600.00          11718500.00   
Bristol_Bay_1030642                    170025700.00          23084400.00   
Bristol_Bay_1031022                   1090944900.00         354655400.00   
Bristol_Bay_2019750                    305554500.00          96808300.00   
Bristol_Bay_2020120                    388836300.00         123534900.00   
Bristol_Bay_2040341                    721403600.00         211553900.00   


In [38]:
# Make watershed wetland df
wtd_wet_df = pd.DataFrame()
wtd_wet_field_list = []
for field in arcpy.ListFields(wtd_wet):
    wtd_wet_field_list.append(field.name)
wtd_wet_arr = arcpy.da.TableToNumPyArray(wtd_wet,wtd_wet_field_list)
wtd_wet_df = pd.DataFrame(wtd_wet_arr)
wtd_wet_df = wtd_wet_df.drop(["OBJECTID","region","cat_ID_txt"],axis=1)
wtd_wet_df = wtd_wet_df.set_index('cat_ID_con')
dfs.append(wtd_wet_df)
wtd_wet_df

AwcHuc12_non_wetland_area  AwcHuc12_wetland_area  \
cat_ID_con                                                                     
Bristol_Bay_1003859                       39885000.00               90900.00   
Bristol_Bay_1004129                       45335900.00                   0.00   
Bristol_Bay_1006868                       35771400.00               18900.00   
Bristol_Bay_1007408                       42448300.00              148500.00   
Bristol_Bay_1008168                       45586200.00               11700.00   
Bristol_Bay_1008527                       69256800.00              312700.00   
Bristol_Bay_1008597                      113550100.00             4344800.00   
Bristol_Bay_1013111                       51929100.00             4287500.00   
Bristol_Bay_1013306                       97826400.00             1815400.00   
Bristol_Bay_1013765                       48337800.00             1060100.00   
Bristol_Bay_1014251                      135907800.00             6846000.00   
Bristol_Bay_1014341                      121171300.00              720100.00   
Bristol_Bay_1014516                       57341200.00             3571800.00   
Bristol_Bay_1014641                      241035600.00            15421500.00   
Bristol_Bay_1014786                       74947900.00             6941900.00   
Bristol_Bay_1014821                     1631492700.00            17807300.00   
Bristol_Bay_1015186                      563423600.00             4196800.00   
Bristol_Bay_1015281                     1878308400.00            21137600.00   
Bristol_Bay_1015516                      716102500.00            13039700.00   
Bristol_Bay_1015685                       99965700.00              201000.00   
Bristol_Bay_1015771                     2456593300.00            55287300.00   
Bristol_Bay_1015821                     6794763200.00           215623100.00   
Bristol_Bay_1016325                      350363500.00             1577500.00   
Bristol_Bay_1016515                       57958400.00              148000.00   
Bristol_Bay_1016825                       63199600.00             7152000.00   
Bristol_Bay_1021823                       35034000.00             7750700.00   
Bristol_Bay_1021914                      132041000.00              116000.00   
Bristol_Bay_1021984                       93004400.00             7548900.00   
Bristol_Bay_1022264                      159658700.00            27238200.00   
Bristol_Bay_1023034                     3200848700.00            56997900.00   
Bristol_Bay_1025113                      121212000.00              132300.00   
Bristol_Bay_1025432                       62218700.00             2056900.00   
Bristol_Bay_1025533                      130713900.00              604900.00   
Bristol_Bay_1025683                      185100800.00             1799900.00   
Bristol_Bay_1025783                      113886200.00             4536900.00   
Bristol_Bay_1026233                      192574400.00            13676100.00   
Bristol_Bay_1026463                      236380000.00            33647900.00   
Bristol_Bay_1026613                      746714100.00             6857500.00   
Bristol_Bay_1026983                     3782088500.00           131492800.00   
Bristol_Bay_1027852                      115676200.00             2597700.00   
Bristol_Bay_1028212                      146468300.00                9400.00   
Bristol_Bay_1028322                      246834200.00             1944800.00   
Bristol_Bay_1029732                      335608000.00             2577600.00   
Bristol_Bay_1029872                      217067800.00             1215600.00   
Bristol_Bay_1030072                      182667600.00            10122200.00   
Bristol_Bay_1030462                       97633400.00             1054700.00   
Bristol_Bay_1030642                      183413300.00             9696800.00   
Bristol_Bay_1031022                     1432089200.00            13511100.00   
Bristol_Bay_2019750         

In [39]:
# Make watershed lakes df
wtd_lp_df = pd.DataFrame()
wtd_lp_field_list = []
for field in arcpy.ListFields(wtd_lp):
    wtd_lp_field_list.append(field.name)
wtd_lp_arr = arcpy.da.TableToNumPyArray(wtd_lp, wtd_lp_field_list)
wtd_lp_df = pd.DataFrame(wtd_lp_arr)
wtd_lp_df = wtd_lp_df.drop(["OBJECTID","region","cat_ID_txt","cat_ID","ftype"],axis=1)
wtd_lp_df = wtd_lp_df.set_index('cat_ID_con')
dfs.append(wtd_lp_df)
wtd_lp_df

AwcHuc12_wtd_lake_area_sqm  AwcHuc12_wtd_lake_per
cat_ID_con                                                                   
Bristol_Bay_1003859                         3636237.03                   9.10
Bristol_Bay_1004129                          674207.91                   1.49
Bristol_Bay_1006868                          900364.40                   2.52
Bristol_Bay_1007408                          201401.29                   0.47
Bristol_Bay_1008168                           81693.79                   0.18
Bristol_Bay_1008527                           76558.55                   0.11
Bristol_Bay_1008597                         1626923.64                   1.38
Bristol_Bay_1013111                         6882348.75                  12.24
Bristol_Bay_1013306                         1657556.02                   1.66
Bristol_Bay_1013765                          585534.87                   1.19
Bristol_Bay_1014251                        12056896.63                   8.45
Bristol_Bay_1014341                         2822562.49                   2.32
Bristol_Bay_1014516                         5427597.07                   8.91
Bristol_Bay_1014641                        20399012.98                   7.95
Bristol_Bay_1014786                         1446369.60                   1.77
Bristol_Bay_1014821                        12483562.70                   0.76
Bristol_Bay_1015186                         3118643.58                   0.55
Bristol_Bay_1015281                        19308085.67                   1.02
Bristol_Bay_1015516                        11986586.39                   1.64
Bristol_Bay_1015685                          190237.77                   0.19
Bristol_Bay_1015771                        74361268.86                   2.96
Bristol_Bay_1015821                      1427831095.21                  20.37
Bristol_Bay_1016325                          880449.69                   0.25
Bristol_Bay_1016515                          108873.23                   0.19
Bristol_Bay_1016825                         4643240.53                   6.60
Bristol_Bay_1021823                         3228016.99                   7.54
Bristol_Bay_1021914                           56491.31                   0.04
Bristol_Bay_1021984                        15630203.99                  15.54
Bristol_Bay_1022264                        26263369.25                  14.05
Bristol_Bay_1023034                      1216077379.66                  37.33
Bristol_Bay_1025113                          400612.44                   0.33
Bristol_Bay_1025432                         6125166.60                   9.53
Bristol_Bay_1025533                         1953483.37                   1.49
Bristol_Bay_1025683                          144962.50                   0.08
Bristol_Bay_1025783                        16720621.11                  14.12
Bristol_Bay_1026233                        17242946.12                   8.36
Bristol_Bay_1026463                        37436531.42                  13.86
Bristol_Bay_1026613                         2681447.23                   0.36
Bristol_Bay_1026983                      1287345906.34                  32.89
Bristol_Bay_1027852                         1411932.63                   1.19
Bristol_Bay_1028212                           64669.36                   0.04
Bristol_Bay_1028322                         3213242.35                   1.29
Bristol_Bay_1029732                         1263883.08                   0.37
Bristol_Bay_1029872                         1981032.15                   0.91
Bristol_Bay_1030072                        24899664.47                  12.92
Bristol_Bay_1030462                         6802559.67                   6.89
Bristol_Bay_1030642                        20407374.39                  10.57
Bristol_Bay_1031022                         9990477.62                   0.69
Bristol_Bay_2019750                          498897.28                   0.12
Bristol_Bay_2020120                          56196

In [40]:
# Make watershed glacier df
wtd_glac_df = pd.DataFrame()
wtd_glac_field_list = []
for field in arcpy.ListFields(wtd_glac):
    wtd_glac_field_list.append(field.name)
wtd_glac_arr = arcpy.da.TableToNumPyArray(wtd_glac, wtd_glac_field_list)
wtd_glac_df = pd.DataFrame(wtd_glac_arr)
wtd_glac_df = wtd_glac_df.drop(["OBJECTID","region","cat_ID_txt","cat_ID","O1Region"],axis=1)
wtd_glac_df = wtd_glac_df.set_index('cat_ID_con')
dfs.append(wtd_glac_df)
wtd_glac_df

AwcHuc12_wtd_glacier_area_sqm  \
cat_ID_con                                                  
Bristol_Bay_1014821                           33846601.94   
Bristol_Bay_1015186                            8152617.83   
Bristol_Bay_1015281                           33846601.94   
Bristol_Bay_1015516                            8152617.83   
Bristol_Bay_1015771                           33846601.94   
Bristol_Bay_1015821                           41999219.77   
Bristol_Bay_1016325                            8152617.83   
Bristol_Bay_1021914                            8152617.83   
Bristol_Bay_1023034                            8152617.83   
Bristol_Bay_1025113                            1511613.62   
Bristol_Bay_1025683                            3134739.76   
Bristol_Bay_1026613                           33846601.94   
Bristol_Bay_1026983                            8152617.83   
Bristol_Bay_1029732                           29200248.56   
Bristol_Bay_1031022                           33846601.94   
Bristol_Bay_2019750                          173249088.06   
Bristol_Bay_2020120                          191458460.14   
Bristol_Bay_2040341                          303785318.57   
Bristol_Bay_2041261                          326750769.57   
Bristol_Bay_2042341                           61160558.56   
Bristol_Bay_2063257                            2032208.46   
Bristol_Bay_2066734                            2534639.98   
Bristol_Bay_2067097                            3361201.69   
Bristol_Bay_2068147                             703004.31   
Bristol_Bay_2068597                            5745549.70   
Bristol_Bay_2069087                            5745549.70   
Bristol_Bay_2069144                            1498522.87   
Bristol_Bay_2069287                            5745549.70   
Bristol_Bay_2069737                            6448554.01   
Bristol_Bay_2069987                            6448554.01   
Bristol_Bay_2070127                            6448554.01   
Bristol_Bay_2070217                          546357631.38   
Bristol_Bay_2070527                          552806185.39   
Bristol_Bay_2072204                             773825.95   
Bristol_Bay_2073174                             383831.59   
Bristol_Bay_2073484                            5200998.73   
Bristol_Bay_2073634                            6699521.60   
Bristol_Bay_2075404                           22453056.98   
Bristol_Bay_2076202                           19643854.06   
Bristol_Bay_2076454                          517205152.80   
Bristol_Bay_2076994                          517205152.80   
Bristol_Bay_2078492                           27899414.46   
Bristol_Bay_2079202                           62458051.65   
Bristol_Bay_2082463                            2205563.42   
Bristol_Bay_2082862                           16608542.53   
Bristol_Bay_2083162                           30201750.37   
Bristol_Bay_2083292                          328704271.05   
Bristol_Bay_2084672                           76377906.84   
Bristol_Bay_2085216                             703004.31   
Bristol_Bay_2086766                             703004.31   
Bristol_Bay_2087903                          514999590.99   
Bristol_Bay_2088163                          517205152.80   
Bristol_Bay_2088766                          546357631.38   
Bristol_Bay_2089306                          546357631.38   
Bristol_Bay_2089656                          546357631.38   
Bristol_Bay_2089756                          546357631.38   
Bristol_Bay_3021744                             261237.94   
Bristol_Bay_3022083                             326639.95   
Bristol_Bay_3024343                          255090705.21   
Bristol_Bay_3024533                          255090705.21   
Bristol_Bay_3024783                          255090705.21   
Bristol_Bay_3029305                           68063522.87   
Bristol_Bay_3030445                             463686.34   
Bristol_Bay_3030555                           68063522.87   
Br


## Merge all covariate dataframes together and drop unnecessary columns
## No Longer using dfs to merge and Export - Instead Merge watershed polygons and join fields
 * Recalculate cat_ID as float64 type
 * Reorder columns
 * Export final csv


In [41]:
# Merge all data frames together
import numpy as np
from functools import reduce
df_final = reduce(lambda left,right: pd.merge(left,right,on='cat_ID_con',how="outer"), dfs)

df_final.columns = list(uniquify(df_final))
#List of final columns in the order to output
# final_cols_old = ['cat_ID_txt','cat_ID','region', 'AwcHuc12_cat_slope_COUNT', 'AwcHuc12_cat_slope_AREA', 'AwcHuc12_cat_slope_MIN', 'AwcHuc12_cat_slope_MAX',
#               'AwcHuc12_cat_slope_RANGE','AwcHuc12_cat_slope_MEAN', 'AwcHuc12_cat_slope_STD', 'AwcHuc12_cat_slope_SUM', 'AwcHuc12_cat_slope_MEDIAN', 'AwcHuc12_cat_slope_PCT90',
#               'AwcHuc12_cat_elev_COUNT', 'AwcHuc12_cat_elev_AREA', 'AwcHuc12_cat_elev_MIN', 'AwcHuc12_cat_elev_MAX', 'AwcHuc12_cat_elev_RANGE', 'AwcHuc12_cat_elev_MEAN', 'AwcHuc12_cat_elev_STD',
#               'AwcHuc12_cat_elev_SUM', 'AwcHuc12_cat_elev_VARIETY', 'AwcHuc12_cat_elev_MAJORITY', 'AwcHuc12_cat_elev_MINORITY', 'AwcHuc12_cat_elev_MEDIAN', 'AwcHuc12_cat_elev_PCT90',
#               'AwcHuc12_wtd_elev_COUNT', 'AwcHuc12_wtd_elev_AREA', 'AwcHuc12_wtd_elev_MIN', 'AwcHuc12_wtd_elev_MAX', 'AwcHuc12_wtd_elev_RANGE', 'AwcHuc12_wtd_elev_MEAN',
#               'AwcHuc12_wtd_elev_STD', 'AwcHuc12_wtd_elev_SUM', 'AwcHuc12_wtd_elev_VARIETY', 'AwcHuc12_wtd_elev_MAJORITY', 'AwcHuc12_wtd_elev_MINORITY',
#               'AwcHuc12_wtd_elev_MEDIAN', 'AwcHuc12_wtd_elev_PCT90', 'AwcHuc12_wtd_slope_COUNT', 'AwcHuc12_wtd_slope_AREA', 'AwcHuc12_wtd_slope_MIN', 'AwcHuc12_wtd_slope_MAX',
#               'AwcHuc12_wtd_slope_RANGE', 'AwcHuc12_wtd_slope_MEAN', 'AwcHuc12_wtd_slope_STD', 'AwcHuc12_wtd_slope_SUM', 'AwcHuc12_wtd_slope_MEDIAN', 'AwcHuc12_wtd_slope_PCT90',
#               'AwcHuc12_non_north_area', 'AwcHuc12_north_area', 'AwcHuc12_wtd_north_per', 'non_wetland_area', 'AwcHuc12_wetland_area', 'AwcHuc12_wtd_wet_per',
#               'AwcHuc12_wtd_lake_area_sqm', 'AwcHuc12_wtd_lake_per', 'AwcHuc12_wtd_glacier_area_sqm', 'AwcHuc12_wtd_glacier_per' ]
final_cols = ['AwcHuc12_cat_slope_COUNT', 'AwcHuc12_cat_slope_AREA', 'AwcHuc12_cat_slope_MIN', 'AwcHuc12_cat_slope_MAX',
              'AwcHuc12_cat_slope_RANGE','AwcHuc12_cat_slope_MEAN', 'AwcHuc12_cat_slope_STD', 'AwcHuc12_cat_slope_SUM', 'AwcHuc12_cat_slope_MEDIAN', 'AwcHuc12_cat_slope_PCT90',
              'AwcHuc12_cat_elev_COUNT', 'AwcHuc12_cat_elev_AREA', 'AwcHuc12_cat_elev_MIN', 'AwcHuc12_cat_elev_MAX', 'AwcHuc12_cat_elev_RANGE', 'AwcHuc12_cat_elev_MEAN', 'AwcHuc12_cat_elev_STD',
              'AwcHuc12_cat_elev_SUM', 'AwcHuc12_cat_elev_VARIETY', 'AwcHuc12_cat_elev_MAJORITY', 'AwcHuc12_cat_elev_MINORITY', 'AwcHuc12_cat_elev_MEDIAN', 'AwcHuc12_cat_elev_PCT90',
              'AwcHuc12_wtd_elev_MIN', 'AwcHuc12_wtd_elev_MAX','AwcHuc12_wtd_elev_MEAN','AwcHuc12_wtd_elev_STD','AwcHuc12_wtd_slope_MIN', 'AwcHuc12_wtd_slope_MAX','AwcHuc12_wtd_slope_MEAN',
              'AwcHuc12_wtd_slope_STD','AwcHuc12_non_north_area', 'AwcHuc12_north_area', 'AwcHuc12_wtd_north_per', 'non_wetland_area', 'AwcHuc12_wetland_area', 'AwcHuc12_wtd_wet_per',
              'AwcHuc12_wtd_lake_area_sqm', 'AwcHuc12_wtd_lake_per', 'AwcHuc12_wtd_glacier_area_sqm', 'AwcHuc12_wtd_glacier_per' ]

# #Export merged dataframe to csv
cov_csv_out = os.path.join(outdir,'AKSSF_awcHuc12s_Covariates.csv')
df_final.to_csv(cov_csv_out, encoding = 'utf-8')
print('Export all covariates dataframe to csv complete')

df_final

Export all covariates dataframe to csv complete


AwcHuc12_cat_elev_COUNT  AwcHuc12_cat_elev_AREA  \
cat_ID_con                                                                    
Bristol_Bay_1003859                         2442.00               244200.00   
Bristol_Bay_1004129                          380.00                38000.00   
Bristol_Bay_1006868                        20499.00              2049900.00   
Bristol_Bay_1007408                        17509.00              1750900.00   
Bristol_Bay_1008168                        13266.00              1326600.00   
Bristol_Bay_1008527                        19118.00              1911800.00   
Bristol_Bay_1008597                         2299.00               229900.00   
Bristol_Bay_1013111                         2342.00               234200.00   
Bristol_Bay_1013306                         2292.00               229200.00   
Bristol_Bay_1013765                         3506.00               350600.00   
Bristol_Bay_1014251                          227.00                22700.00   
Bristol_Bay_1014341                         1854.00               185400.00   
Bristol_Bay_1014516                          929.00                92900.00   
Bristol_Bay_1014641                         8158.00               815800.00   
Bristol_Bay_1014786                         2842.00               284200.00   
Bristol_Bay_1014821                         1968.00               196800.00   
Bristol_Bay_1015186                         6630.00               663000.00   
Bristol_Bay_1015281                         4465.00               446500.00   
Bristol_Bay_1015516                        14462.00              1446200.00   
Bristol_Bay_1015685                        18349.00              1834900.00   
Bristol_Bay_1015771                         1571.00               157100.00   
Bristol_Bay_1015821                         1141.00               114100.00   
Bristol_Bay_1016325                         3355.00               335500.00   
Bristol_Bay_1016515                         2797.00               279700.00   
Bristol_Bay_1016825                        13973.00              1397300.00   
Bristol_Bay_1021823                         2164.00               216400.00   
Bristol_Bay_1021914                            1.00                  100.00   
Bristol_Bay_1021984                         2996.00               299600.00   
Bristol_Bay_1022264                         3043.00               304300.00   
Bristol_Bay_1023034                         9215.00               921500.00   
Bristol_Bay_1025113                        11051.00              1105100.00   
Bristol_Bay_1025432                         1193.00               119300.00   
Bristol_Bay_1025533                         5297.00               529700.00   
Bristol_Bay_1025683                        13682.00              1368200.00   
Bristol_Bay_1025783                          863.00                86300.00   
Bristol_Bay_1026233                         1101.00               110100.00   
Bristol_Bay_1026463                         4154.00               415400.00   
Bristol_Bay_1026613                         1556.00               155600.00   
Bristol_Bay_1026983                         9003.00               900300.00   
Bristol_Bay_1027852                         6344.00               634400.00   
Bristol_Bay_1028212                          314.00                31400.00   
Bristol_Bay_1028322                        10280.00              1028000.00   
Bristol_Bay_1029732                         5302.00               530200.00   
Bristol_Bay_1029872                         1692.00               169200.00   
Bristol_Bay_1030072                        30586.00              3058600.00   
Bristol_Bay_1030462                         8143.00               814300.00   
Bristol_Bay_1030642                         1288.00               128800.00   
Bristol_Bay_1031022                         1699.00               169900.00   
Bristol_Bay_2019750                          183.00                18300.00   


## Merge watersheds and join covariates for data explore in GIS
* Collect all _wtds_merge polygons and merge together
* Join Covariates using cat_ID_con field


In [42]:
arcpy.env.workspace = outgdb
outtables.append(lcld_table)
# Merge watersheds
wtds = [fc for fc in arcpy.ListFeatureClasses('*_wtds_merge','POLYGON')]
akssf_h12wtds = arcpy.Merge_management(wtds,'AKSSF_awcHuc12_Watersheds_Merge')
dropfields = ['OBJECTID','cat_ID_con', 'cat_ID', 'cat_ID_txt', 'region','O1Region','FType','NHDPlusID']
for table in outtables:
    tname = table.getOutput(0).split("\\")[-1]
    fields =[f.name for f in arcpy.ListFields(tname) if f.name not in dropfields]
    print(f'Joining fields : {fields} to all Watersheds\n{("*"*100)}')
    arcpy.JoinField_management(akssf_h12wtds,'cat_ID_con',table, 'cat_ID_con', fields)
akssf_h12wtds_table = arcpy.TableToTable_conversion(akssf_h12wtds,outgdb,'AKSSF_awcHuc12_Covariates')

Joining fields : ['AwcHuc12_non_north_area', 'AwcHuc12_north_area', 'AwcHuc12_wtd_north_per'] to all Watersheds
****************************************************************************************************
Joining fields : ['AwcHuc12_cat_elev_ZONE_CODE', 'AwcHuc12_cat_elev_COUNT', 'AwcHuc12_cat_elev_AREA', 'AwcHuc12_cat_elev_MIN', 'AwcHuc12_cat_elev_MAX', 'AwcHuc12_cat_elev_RANGE', 'AwcHuc12_cat_elev_MEAN', 'AwcHuc12_cat_elev_STD', 'AwcHuc12_cat_elev_SUM', 'AwcHuc12_cat_elev_VARIETY', 'AwcHuc12_cat_elev_MAJORITY', 'AwcHuc12_cat_elev_MINORITY', 'AwcHuc12_cat_elev_MEDIAN', 'AwcHuc12_cat_elev_PCT90'] to all Watersheds
****************************************************************************************************
Joining fields : ['AwcHuc12_wtd_elev_MIN', 'AwcHuc12_wtd_elev_MAX', 'AwcHuc12_wtd_elev_MEAN', 'AwcHuc12_wtd_elev_STD'] to all Watersheds
****************************************************************************************************
Joining fields : ['AwcHuc12_wtd

In [43]:
# Export watershed as table after join fields
akssf_h12_cov_csv = arcpy.conversion.TableToTable(akssf_h12wtds_table, outdir, 'AKSSF_awcHuc12s_Covariates.csv')
print('Export all covariates dataframe to csv complete')


Export all covariates dataframe to csv complete


In [44]:
import pandas as pd
import numpy as np

#convert to df and check
wtds_df = pd.DataFrame()
wtds_fl = []

for field in arcpy.ListFields(akssf_h12wtds_table):
    wtds_fl.append(field.name)
akssf_h12wtds_arr = arcpy.da.TableToNumPyArray(akssf_h12wtds_table, wtds_fl)
akssf_h12wtds_arr
wtds_df = pd.DataFrame(akssf_h12wtds_arr)
wtds_df = wtds_df.set_index('cat_ID_con')
wtds_df


OBJECTID  ORIG_FID  \
cat_ID_con                                       
Bristol_Bay_1003859                1         1   
Bristol_Bay_1004129                2         1   
Bristol_Bay_1006868                3         1   
Bristol_Bay_1007408                4         1   
Bristol_Bay_1008168                5         1   
Bristol_Bay_1008527                6         1   
Bristol_Bay_1008597                7         1   
Bristol_Bay_1013111                8         1   
Bristol_Bay_1013306                9         1   
Bristol_Bay_1013765               10         1   
Bristol_Bay_1014251               11         1   
Bristol_Bay_1014341               12         1   
Bristol_Bay_1014516               13         1   
Bristol_Bay_1014641               14         1   
Bristol_Bay_1014786               15         1   
Bristol_Bay_1014821               16         1   
Bristol_Bay_1015186               17         1   
Bristol_Bay_1015281               18         1   
Bristol_Bay_1015516               19         1   
Bristol_Bay_1015685               20         1   
Bristol_Bay_1015771               21         1   
Bristol_Bay_1015821               22         1   
Bristol_Bay_1016325               23         1   
Bristol_Bay_1016515               24         1   
Bristol_Bay_1016825               25         1   
Bristol_Bay_1021823               26         1   
Bristol_Bay_1021914               27         1   
Bristol_Bay_1021984               28         1   
Bristol_Bay_1022264               29         1   
Bristol_Bay_1023034               30         1   
Bristol_Bay_1025113               31         1   
Bristol_Bay_1025432               32         1   
Bristol_Bay_1025533               33         1   
Bristol_Bay_1025683               34         1   
Bristol_Bay_1025783               35         1   
Bristol_Bay_1026233               36         1   
Bristol_Bay_1026463               37         1   
Bristol_Bay_1026613               38         1   
Bristol_Bay_1026983               39         1   
Bristol_Bay_1027852               40         1   
Bristol_Bay_1028212               41         1   
Bristol_Bay_1028322               42         1   
Bristol_Bay_1029732               43         1   
Bristol_Bay_1029872               44         1   
Bristol_Bay_1030072               45         1   
Bristol_Bay_1030462               46         1   
Bristol_Bay_1030642               47         1   
Bristol_Bay_1031022               48         1   
Bristol_Bay_2019750               49         1   
Bristol_Bay_2020120               50         1   
Bristol_Bay_2040341               51         1   
Bristol_Bay_2041261               52         1   
Bristol_Bay_2042341               53         1   
Bristol_Bay_2060975               54         1   
Bristol_Bay_2061205               55         1   
Bristol_Bay_2061325               56         1   
Bristol_Bay_2063167               57         1   
Bristol_Bay_2063257               58         1   
Bristol_Bay_2064245               59         1   
Bristol_Bay_2064327               60         1   
Bristol_Bay_2064385               61         1   
Bristol_Bay_2065025               62         1   
Bristol_Bay_2065485               63         1   
Bristol_Bay_2065885               64         1   
Bristol_Bay_2066555               65         1   
Bristol_Bay_2066734               66         1   
Bristol_Bay_2066827               67         1   
Bristol_Bay_2067075               68         1   
Bristol_Bay_2067097               69         1   
Bristol_Bay_2067114               70         1   
Bristol_Bay_2067195               71         1   
Bristol_Bay_2067465               72         1   
Bristol_Bay_2067604               73         1   
Bristol_Bay_2068087               74         1   
Bristol_Bay_2068147               75         1   
Bristol_Bay_2068305               76         1   
Bristol_Bay_2068474               77         1   
Bristol_Bay_2068514               78         1   
Bristol_Bay_2068597         

In [45]:
bbay_df = wtds_df.filter(like='Bristol_Bay', axis = 0)
bbay_df

OBJECTID  ORIG_FID  \
cat_ID_con                                
Bristol_Bay_1003859         1         1   
Bristol_Bay_1004129         2         1   
Bristol_Bay_1006868         3         1   
Bristol_Bay_1007408         4         1   
Bristol_Bay_1008168         5         1   
Bristol_Bay_1008527         6         1   
Bristol_Bay_1008597         7         1   
Bristol_Bay_1013111         8         1   
Bristol_Bay_1013306         9         1   
Bristol_Bay_1013765        10         1   
Bristol_Bay_1014251        11         1   
Bristol_Bay_1014341        12         1   
Bristol_Bay_1014516        13         1   
Bristol_Bay_1014641        14         1   
Bristol_Bay_1014786        15         1   
Bristol_Bay_1014821        16         1   
Bristol_Bay_1015186        17         1   
Bristol_Bay_1015281        18         1   
Bristol_Bay_1015516        19         1   
Bristol_Bay_1015685        20         1   
Bristol_Bay_1015771        21         1   
Bristol_Bay_1015821        22         1   
Bristol_Bay_1016325        23         1   
Bristol_Bay_1016515        24         1   
Bristol_Bay_1016825        25         1   
Bristol_Bay_1021823        26         1   
Bristol_Bay_1021914        27         1   
Bristol_Bay_1021984        28         1   
Bristol_Bay_1022264        29         1   
Bristol_Bay_1023034        30         1   
Bristol_Bay_1025113        31         1   
Bristol_Bay_1025432        32         1   
Bristol_Bay_1025533        33         1   
Bristol_Bay_1025683        34         1   
Bristol_Bay_1025783        35         1   
Bristol_Bay_1026233        36         1   
Bristol_Bay_1026463        37         1   
Bristol_Bay_1026613        38         1   
Bristol_Bay_1026983        39         1   
Bristol_Bay_1027852        40         1   
Bristol_Bay_1028212        41         1   
Bristol_Bay_1028322        42         1   
Bristol_Bay_1029732        43         1   
Bristol_Bay_1029872        44         1   
Bristol_Bay_1030072        45         1   
Bristol_Bay_1030462        46         1   
Bristol_Bay_1030642        47         1   
Bristol_Bay_1031022        48         1   
Bristol_Bay_2019750        49         1   
Bristol_Bay_2020120        50         1   
Bristol_Bay_2040341        51         1   
Bristol_Bay_2041261        52         1   
Bristol_Bay_2042341        53         1   
Bristol_Bay_2060975        54         1   
Bristol_Bay_2061205        55         1   
Bristol_Bay_2061325        56         1   
Bristol_Bay_2063167        57         1   
Bristol_Bay_2063257        58         1   
Bristol_Bay_2064245        59         1   
Bristol_Bay_2064327        60         1   
Bristol_Bay_2064385        61         1   
Bristol_Bay_2065025        62         1   
Bristol_Bay_2065485        63         1   
Bristol_Bay_2065885        64         1   
Bristol_Bay_2066555        65         1   
Bristol_Bay_2066734        66         1   
Bristol_Bay_2066827        67         1   
Bristol_Bay_2067075        68         1   
Bristol_Bay_2067097        69         1   
Bristol_Bay_2067114        70         1   
Bristol_Bay_2067195        71         1   
Bristol_Bay_2067465        72         1   
Bristol_Bay_2067604        73         1   
Bristol_Bay_2068087        74         1   
Bristol_Bay_2068147        75         1   
Bristol_Bay_2068305        76         1   
Bristol_Bay_2068474        77         1   
Bristol_Bay_2068514        78         1   
Bristol_Bay_2068597        79         1   
Bristol_Bay_2068715        80         1   
Bristol_Bay_2068895        81         1   
Bristol_Bay_2069087        82         1   
Bristol_Bay_2069134        83         1   
Bristol_Bay_2069144        84         1   
Bristol_Bay_2069287        85         1   
Bristol_Bay_2069334        86         1   
Bristol_Bay_2069365        87         1   
Bristol_Bay_2069504        88         1   
Bristol_Bay_2069737        89         1   
Bristol_Bay_2069835        90         1   
Bristol_Bay_2069987        91         1   
Bristol_Bay_2070127   

In [46]:
kod_df = wtds_df.filter(like='Kodiak', axis = 0)
kod_df

OBJECTID  ORIG_FID  \
cat_ID_con                          
Kodiak_13958        582         1   
Kodiak_14049        583         1   
Kodiak_14069        584         1   
Kodiak_14658        585         1   
Kodiak_14858        586         1   
Kodiak_14958        587         1   
Kodiak_15261        588         1   
Kodiak_45317        589         1   
Kodiak_45537        590         1   
Kodiak_46167        591         1   
Kodiak_46347        592         1   
Kodiak_46907        593         1   
Kodiak_47187        594         1   
Kodiak_47207        595         1   
Kodiak_47317        596         1   
Kodiak_48057        597         1   
Kodiak_48067        598         1   
Kodiak_48267        599         1   
Kodiak_48707        600         1   
Kodiak_48997        601         1   
Kodiak_49617        602         1   
Kodiak_50207        603         1   
Kodiak_63603        604         1   
Kodiak_63943        605         1   
Kodiak_63963        606         1   
Kodiak_64263        607         1   
Kodiak_64593        608         1   
Kodiak_64633        609         1   
Kodiak_64673        610         1   
Kodiak_66383        611         1   
Kodiak_74254        612         1   
Kodiak_75052        613         1   
Kodiak_75104        614         1   
Kodiak_75194        615         1   
Kodiak_75624        616         1   
Kodiak_75664        617         1   
Kodiak_76204        618         1   
Kodiak_76354        619         1   
Kodiak_76542        620         1   
Kodiak_76564        621         1   
Kodiak_76942        622         1   
Kodiak_77254        623         1   
Kodiak_77294        624         1   
Kodiak_77372        625         1   
Kodiak_77702        626         1   
Kodiak_77824        627         1   
Kodiak_77844        628         1   
Kodiak_77864        629         1   
Kodiak_77872        630         1   
Kodiak_78072        631         1   
Kodiak_78104        632         1   
Kodiak_78362        633         1   
Kodiak_78602        634         1   
Kodiak_78804        635         1   
Kodiak_79642        636         1   
Kodiak_79852        637         1   
Kodiak_80022        638         1   
Kodiak_80054        639         1   
Kodiak_80624        640         1   
Kodiak_80644        641         1   
Kodiak_95226        642         1   
Kodiak_96786        643         1   
Kodiak_97006        644         1   
Kodiak_99996        645         1   
Kodiak_100826       646         1   
Kodiak_101146       647         1   
Kodiak_101736       648         1   
Kodiak_101826       649         1   
Kodiak_102106       650         1   
Kodiak_102746       651         1   
Kodiak_102936       652         1   
Kodiak_103016       653         1   
Kodiak_103196       654         1   
Kodiak_103266       655         1   
Kodiak_103296       656         1   
Kodiak_103556       657         1   
Kodiak_103936       658         1   
Kodiak_104296       659         1   
Kodiak_105086       660         1   
Kodiak_106486       661         1   
Kodiak_107216       662         1   
Kodiak_107376       663         1   
Kodiak_107686       664         1   
Kodiak_108206       665         1   
Kodiak_108376       666         1   
Kodiak_108606       667         1   
Kodiak_117795       668         1   
Kodiak_121025       669         1   
Kodiak_122415       670         1   
Kodiak_122785       671         1   
Kodiak_123415       672         1   
Kodiak_123695       673         1   
Kodiak_124065       674         1   
Kodiak_124185       675         1   
Kodiak_124215       676         1   
Kodiak_124815       677         1   
Kodiak_124945       678         1   
Kodiak_125115       679         1   
Kodiak_125235       680         1   
Kodiak_125245       681         1   
Kodiak_125365       682         1   
Kodiak_126005       683         1   
Kodiak_126265       684         1   
Kodiak_127785       685         1   
Kodiak_127895       686         1   
Kodiak_127995       687         1   
Kodiak_128765      

In [47]:
pws_df = wtds_df.filter(like='Prince', axis = 0)
pws_df

OBJECTID  ORIG_FID  \
cat_ID_con                                       
Prince_William_Sound_685         696         1   
Prince_William_Sound_3038        697         1   
Prince_William_Sound_13227       698         1   
Prince_William_Sound_16467       699         1   
Prince_William_Sound_17027       700         1   
Prince_William_Sound_17697       701         1   
Prince_William_Sound_18357       702         1   
Prince_William_Sound_18547       703         1   
Prince_William_Sound_18737       704         1   
Prince_William_Sound_18967       705         1   
Prince_William_Sound_19416       706         1   
Prince_William_Sound_23574       707         1   
Prince_William_Sound_24654       708         1   
Prince_William_Sound_25516       709         1   
Prince_William_Sound_26246       710         1   
Prince_William_Sound_26334       711         1   
Prince_William_Sound_28465       712         1   
Prince_William_Sound_28576       713         1   
Prince_William_Sound_28734       714         1   
Prince_William_Sound_29704       715         1   
Prince_William_Sound_29954       716         1   
Prince_William_Sound_29994       717         1   
Prince_William_Sound_30114       718         1   
Prince_William_Sound_30596       719         1   
Prince_William_Sound_30774       720         1   
Prince_William_Sound_30886       721         1   
Prince_William_Sound_30934       722         1   
Prince_William_Sound_31226       723         1   
Prince_William_Sound_32766       724         1   
Prince_William_Sound_32806       725         1   
Prince_William_Sound_33036       726         1   
Prince_William_Sound_34003       727         1   
Prince_William_Sound_35343       728         1   
Prince_William_Sound_36553       729         1   
Prince_William_Sound_37373       730         1   
Prince_William_Sound_37815       731         1   
Prince_William_Sound_37935       732         1   
Prince_William_Sound_37955       733         1   
Prince_William_Sound_38615       734         1   
Prince_William_Sound_39065       735         1   
Prince_William_Sound_39255       736         1   
Prince_William_Sound_39565       737         1   
Prince_William_Sound_40615       738         1   
Prince_William_Sound_40743       739         1   
Prince_William_Sound_41025       740         1   
Prince_William_Sound_41123       741         1   
Prince_William_Sound_41143       742         1   
Prince_William_Sound_41515       743         1   
Prince_William_Sound_41525       744         1   
Prince_William_Sound_41963       745         1   
Prince_William_Sound_41995       746         1   
Prince_William_Sound_42455       747         1   
Prince_William_Sound_43125       748         1   
Prince_William_Sound_43135       749         1   
Prince_William_Sound_43195       750         1   
Prince_William_Sound_43473       751         1   
Prince_William_Sound_43513       752         1   
Prince_William_Sound_43705       753         1   
Prince_William_Sound_43753       754         1   
Prince_William_Sound_43793       755         1   
Prince_William_Sound_44113       756         1   
Prince_William_Sound_44503       757         1   
Prince_William_Sound_44545       758         1   
Prince_William_Sound_44595       759         1   
Prince_William_Sound_44633       760         1   
Prince_William_Sound_44663       761         1   
Prince_William_Sound_45273       762         1   
Prince_William_Sound_45473       763         1   
Prince_William_Sound_45835       764         1   
Prince_William_Sound_45863       765         1   
Prince_William_Sound_45905       766         1   
Prince_William_Sound_46065       767         1   
Prince_William_Sound_46103       768         1   
Prince_William_Sound_46293       769         1   
Prince_William_Sound_46493       770         1   
Prince_William_Sound_61812       771         1   
Prince_William_Sound_62232       772         1   
Prince_William_Sound_64192       773         1   
Prince_William_Sound_66912  

In [48]:
ci_df = wtds_df.filter(like='Cook', axis = 0)
ci_df

Empty DataFrame
Columns: [OBJECTID, ORIG_FID, MERGE_SRC, cat_ID, cat_ID_txt, Shape_Length, Shape_Area, AwcHuc12_non_north_area, AwcHuc12_north_area, AwcHuc12_wtd_north_per, AwcHuc12_cat_elev_ZONE_CODE, AwcHuc12_cat_elev_COUNT, AwcHuc12_cat_elev_AREA, AwcHuc12_cat_elev_MIN, AwcHuc12_cat_elev_MAX, AwcHuc12_cat_elev_RANGE, AwcHuc12_cat_elev_MEAN, AwcHuc12_cat_elev_STD, AwcHuc12_cat_elev_SUM, AwcHuc12_cat_elev_VARIETY, AwcHuc12_cat_elev_MAJORITY, AwcHuc12_cat_elev_MINORITY, AwcHuc12_cat_elev_MEDIAN, AwcHuc12_cat_elev_PCT90, AwcHuc12_wtd_elev_MIN, AwcHuc12_wtd_elev_MAX, AwcHuc12_wtd_elev_MEAN, AwcHuc12_wtd_elev_STD, AwcHuc12_wtd_slope_MIN, AwcHuc12_wtd_slope_MAX, AwcHuc12_wtd_slope_MEAN, AwcHuc12_wtd_slope_STD, AwcHuc12_cat_slope_ZONE_CODE, AwcHuc12_cat_slope_COUNT, AwcHuc12_cat_slope_AREA, AwcHuc12_cat_slope_MIN, AwcHuc12_cat_slope_MAX, AwcHuc12_cat_slope_RANGE, AwcHuc12_cat_slope_MEAN, AwcHuc12_cat_slope_STD, AwcHuc12_cat_slope_SUM, AwcHuc12_cat_slope_MEDIAN, AwcHuc12_cat_slope_PCT90, AwcHuc12_non_wetland_area, AwcHuc12_wetland_area, AwcHuc12_wtd_wet_per, AwcHuc12_wtd_glacier_area_sqm, AwcHuc12_wtd_glacier_per, ftype, AwcHuc12_wtd_lake_area_sqm, AwcHuc12_wtd_lake_per, AwcHuc12_wtd_lcld_mn_2001, AwcHuc12_wtd_lcld_mn_2002, AwcHuc12_wtd_lcld_mn_2003, AwcHuc12_wtd_lcld_mn_2004, AwcHuc12_wtd_lcld_mn_2005, AwcHuc12_wtd_lcld_mn_2006, AwcHuc12_wtd_lcld_mn_2007, AwcHuc12_wtd_lcld_mn_2008, AwcHuc12_wtd_lcld_mn_2009, AwcHuc12_wtd_lcld_mn_2010, AwcHuc12_wtd_lcld_mn_2011, AwcHuc12_wtd_lcld_mn_2012, AwcHuc12_wtd_lcld_mn_2013, AwcHuc12_wtd_lcld_mn_2014, AwcHuc12_wtd_lcld_mn_2015, AwcHuc12_wtd_lcld_mn_2016, AwcHuc12_wtd_lcld_mn_2017, AwcHuc12_wtd_lcld_mn_2018, AwcHuc12_wtd_lcld_mn_2019]
Index: []

[0 rows x 70 columns]

In [49]:
cop_df = wtds_df.filter(like='Copper', axis = 0)
cop_df

Empty DataFrame
Columns: [OBJECTID, ORIG_FID, MERGE_SRC, cat_ID, cat_ID_txt, Shape_Length, Shape_Area, AwcHuc12_non_north_area, AwcHuc12_north_area, AwcHuc12_wtd_north_per, AwcHuc12_cat_elev_ZONE_CODE, AwcHuc12_cat_elev_COUNT, AwcHuc12_cat_elev_AREA, AwcHuc12_cat_elev_MIN, AwcHuc12_cat_elev_MAX, AwcHuc12_cat_elev_RANGE, AwcHuc12_cat_elev_MEAN, AwcHuc12_cat_elev_STD, AwcHuc12_cat_elev_SUM, AwcHuc12_cat_elev_VARIETY, AwcHuc12_cat_elev_MAJORITY, AwcHuc12_cat_elev_MINORITY, AwcHuc12_cat_elev_MEDIAN, AwcHuc12_cat_elev_PCT90, AwcHuc12_wtd_elev_MIN, AwcHuc12_wtd_elev_MAX, AwcHuc12_wtd_elev_MEAN, AwcHuc12_wtd_elev_STD, AwcHuc12_wtd_slope_MIN, AwcHuc12_wtd_slope_MAX, AwcHuc12_wtd_slope_MEAN, AwcHuc12_wtd_slope_STD, AwcHuc12_cat_slope_ZONE_CODE, AwcHuc12_cat_slope_COUNT, AwcHuc12_cat_slope_AREA, AwcHuc12_cat_slope_MIN, AwcHuc12_cat_slope_MAX, AwcHuc12_cat_slope_RANGE, AwcHuc12_cat_slope_MEAN, AwcHuc12_cat_slope_STD, AwcHuc12_cat_slope_SUM, AwcHuc12_cat_slope_MEDIAN, AwcHuc12_cat_slope_PCT90, AwcHuc12_non_wetland_area, AwcHuc12_wetland_area, AwcHuc12_wtd_wet_per, AwcHuc12_wtd_glacier_area_sqm, AwcHuc12_wtd_glacier_per, ftype, AwcHuc12_wtd_lake_area_sqm, AwcHuc12_wtd_lake_per, AwcHuc12_wtd_lcld_mn_2001, AwcHuc12_wtd_lcld_mn_2002, AwcHuc12_wtd_lcld_mn_2003, AwcHuc12_wtd_lcld_mn_2004, AwcHuc12_wtd_lcld_mn_2005, AwcHuc12_wtd_lcld_mn_2006, AwcHuc12_wtd_lcld_mn_2007, AwcHuc12_wtd_lcld_mn_2008, AwcHuc12_wtd_lcld_mn_2009, AwcHuc12_wtd_lcld_mn_2010, AwcHuc12_wtd_lcld_mn_2011, AwcHuc12_wtd_lcld_mn_2012, AwcHuc12_wtd_lcld_mn_2013, AwcHuc12_wtd_lcld_mn_2014, AwcHuc12_wtd_lcld_mn_2015, AwcHuc12_wtd_lcld_mn_2016, AwcHuc12_wtd_lcld_mn_2017, AwcHuc12_wtd_lcld_mn_2018, AwcHuc12_wtd_lcld_mn_2019]
Index: []

[0 rows x 70 columns]

In [50]:
from collections import Counter
inhucs = os.path.join(outgdb,"AKSSF_awcHuc12s")
inwtds = os.path.join(outgdb,"AKSSF_awcHuc12_Watersheds_Merge")
wtdfields = [f.name  for f in arcpy.ListFields(inwtds)]
if 'HUC12' not in wtdfields:
    print (f'HUC12 field not present in {inwtds}')
    print (f'Joining HUC12 field to watershed merge feature class')
    arcpy.JoinField_management(inwtds,'cat_ID_con', cats_outlets,'cat_ID_con','HUC12')
else:
    print(f'HUC12 field present')
# Identify watershed that was created but did not have HUC12 identifier joined?
awcHucs = [r[0] for r in arcpy.da.SearchCursor(inhucs,'cat_ID_con')]
wtdHucs = [r[0] for r in arcpy.da.SearchCursor(inwtds,'cat_ID_con')]
c1 = Counter(awcHucs)
c2 = Counter(wtdHucs)
diff = Counter(c2)-Counter(c1)
print(len(awcHucs))
print(f'{len(wtdHucs) - len(awcHucs) }')
missingHucs = list(diff.elements())
print(missingHucs)
print(len(missingHucs))

HUC12 field not present in D:\GIS\outputs_20230518\outputs_20230518.gdb\AKSSF_awcHuc12_Watersheds_Merge
Joining HUC12 field to watershed merge feature class
1663
-858
[]
0


In [51]:
arcpy.env.workspace = outgdb
outlet_cats = arcpy.ListFeatureClasses("*cats_outlets", "POLYGON")
outlet_cats
outlet_cats_merge = os.path.join(outgdb, 'AKSSF_awcHuc12_outlet_cats_merge')
if not arcpy.Exists(outlet_cats_merge):
    print(f'Merging all Huc12 outlet catchments...')
    arcpy.Merge_management(outlet_cats, outlet_cats_merge, add_source=True)
    print(f'Joining HUC12 identifiers')
    arcpy.JoinField_management(outlet_cats_merge,'cat_ID_con', cats_outlets,'cat_ID_con','HUC12')

else:
    print(f'{outlet_cats_merge} dataset already exists')
print(f'Complete')

Merging all Huc12 outlet catchments...
Joining HUC12 identifiers
Complete


In [52]:
import arcpy
arcpy.env.overwriteOutput = True
#outgdb  = r'D:\\GIS\\AKSSF_awcHuc12_cv_Final\\AKSSF_awcHuc12_cv_Final.gdb'
outlet_cats = os.path.join(outgdb,r'AKSSF_awcHuc12_outlet_cats_merge')
wtds_merge = os.path.join(outgdb,r'AKSSF_awcHuc12_Watersheds_Merge')
catsFields = [f.name for f in arcpy.ListFields(outlet_cats)]
catsKeepFields = ['cat_ID_con','str_slope', 'str_slope_dg','str_ord']
wtdsFields = [f.name for f in arcpy.ListFields(wtds_merge)]
wtdsKeepFields = ['Shape_Area','HUC12']
print(catsFields)
print(f'\n{wtdsFields}')
fieldmappings = arcpy.FieldMappings()
fieldmappings.addTable(outlet_cats)
for field in fieldmappings.fields:
    if field.name not in catsKeepFields:
        fieldmappings.removeFieldMap(fieldmappings.findFieldMapIndex(field.name))
streamwtdtable = arcpy.TableToTable_conversion(outlet_cats,outgdb,'AKSSF_AwcHuc12_StrWtd_cv',None,fieldmappings)
arcpy.JoinField_management(streamwtdtable,'cat_ID_con',wtds_merge,'cat_ID_con',wtdsKeepFields)
arcpy.AddField_management(streamwtdtable,'wtd_AreaSqKm','DOUBLE','','','','Watershed Area Square Kilometers')
arcpy.AddField_management(streamwtdtable,'region','TEXT')
for field in arcpy.ListFields(streamwtdtable):
    print(field.name)
# Use update cursor to calculate region and wtd area
with arcpy.da.UpdateCursor(streamwtdtable,['cat_ID_con','region','Shape_Area','wtd_AreaSqKm']) as cur:
    for row in cur:
        region = row[0].rsplit('_',1)[::-1][1]
        areaSqkm = row[2]*1e-6
        print(f'{row[0]} will have region = {region} and shape area {row[2]} sq meters = {areaSqkm} sqKm')
        row[1] = region
        row[3] = areaSqkm
        cur.updateRow(row)
    del(row)
del(cur)

['OBJECTID', 'Shape', 'gridcode', 'catID', 'DSContArea', 'cat_ID_con', 'str_slope', 'str_ord', 'ds_dist_outlet_km', 'DSContArea_SqKM', 'str_slope_dg', 'MERGE_SRC', 'Shape_Length', 'Shape_Area', 'HUC12']

['OBJECTID', 'Shape', 'ORIG_FID', 'MERGE_SRC', 'cat_ID_con', 'cat_ID', 'cat_ID_txt', 'Shape_Length', 'Shape_Area', 'AwcHuc12_non_north_area', 'AwcHuc12_north_area', 'AwcHuc12_wtd_north_per', 'AwcHuc12_cat_elev_ZONE_CODE', 'AwcHuc12_cat_elev_COUNT', 'AwcHuc12_cat_elev_AREA', 'AwcHuc12_cat_elev_MIN', 'AwcHuc12_cat_elev_MAX', 'AwcHuc12_cat_elev_RANGE', 'AwcHuc12_cat_elev_MEAN', 'AwcHuc12_cat_elev_STD', 'AwcHuc12_cat_elev_SUM', 'AwcHuc12_cat_elev_VARIETY', 'AwcHuc12_cat_elev_MAJORITY', 'AwcHuc12_cat_elev_MINORITY', 'AwcHuc12_cat_elev_MEDIAN', 'AwcHuc12_cat_elev_PCT90', 'AwcHuc12_wtd_elev_MIN', 'AwcHuc12_wtd_elev_MAX', 'AwcHuc12_wtd_elev_MEAN', 'AwcHuc12_wtd_elev_STD', 'AwcHuc12_wtd_slope_MIN', 'AwcHuc12_wtd_slope_MAX', 'AwcHuc12_wtd_slope_MEAN', 'AwcHuc12_wtd_slope_STD', 'AwcHuc12_cat_slop

In [53]:
import pandas as pd
import numpy as np

#convert to df and check
final_df = pd.DataFrame()
final_fl = ['cat_ID_con','region','wtd_AreaSqKm','str_ord','str_slope','str_slope_dg','HUC12']
final_h12wtds_arr = arcpy.da.TableToNumPyArray(streamwtdtable, final_fl)
final_df = pd.DataFrame(final_h12wtds_arr)
final_df = final_df.set_index('cat_ID_con')
final_df


region  wtd_AreaSqKm  str_ord  \
cat_ID_con                                                                
Bristol_Bay_1003859                  Bristol_Bay         39.98        4   
Bristol_Bay_1004129                  Bristol_Bay         45.34        5   
Bristol_Bay_1006868                  Bristol_Bay         35.79        4   
Bristol_Bay_1007408                  Bristol_Bay         42.60        4   
Bristol_Bay_1008168                  Bristol_Bay         45.60        4   
Bristol_Bay_1008527                  Bristol_Bay         69.57        4   
Bristol_Bay_1008597                  Bristol_Bay        117.89        5   
Bristol_Bay_1013111                  Bristol_Bay         56.22        4   
Bristol_Bay_1013306                  Bristol_Bay         99.64        5   
Bristol_Bay_1013765                  Bristol_Bay         49.40        4   
Bristol_Bay_1014251                  Bristol_Bay        142.75        5   
Bristol_Bay_1014341                  Bristol_Bay        121.89        4   
Bristol_Bay_1014516                  Bristol_Bay         60.91        5   
Bristol_Bay_1014641                  Bristol_Bay        256.46        6   
Bristol_Bay_1014786                  Bristol_Bay         81.89        5   
Bristol_Bay_1014821                  Bristol_Bay       1649.30        6   
Bristol_Bay_1015186                  Bristol_Bay        567.62        5   
Bristol_Bay_1015281                  Bristol_Bay       1899.45        6   
Bristol_Bay_1015516                  Bristol_Bay        729.14        6   
Bristol_Bay_1015685                  Bristol_Bay        100.17        5   
Bristol_Bay_1015771                  Bristol_Bay       2511.88        7   
Bristol_Bay_1015821                  Bristol_Bay       7010.39        8   
Bristol_Bay_1016325                  Bristol_Bay        351.94        5   
Bristol_Bay_1016515                  Bristol_Bay         58.11        4   
Bristol_Bay_1016825                  Bristol_Bay         70.35        4   
Bristol_Bay_1021823                  Bristol_Bay         42.78        3   
Bristol_Bay_1021914                  Bristol_Bay        132.16        5   
Bristol_Bay_1021984                  Bristol_Bay        100.55        5   
Bristol_Bay_1022264                  Bristol_Bay        186.90        5   
Bristol_Bay_1023034                  Bristol_Bay       3257.85        7   
Bristol_Bay_1025113                  Bristol_Bay        121.34        5   
Bristol_Bay_1025432                  Bristol_Bay         64.28        3   
Bristol_Bay_1025533                  Bristol_Bay        131.32        4   
Bristol_Bay_1025683                  Bristol_Bay        186.90        5   
Bristol_Bay_1025783                  Bristol_Bay        118.42        5   
Bristol_Bay_1026233                  Bristol_Bay        206.25        5   
Bristol_Bay_1026463                  Bristol_Bay        270.03        5   
Bristol_Bay_1026613                  Bristol_Bay        753.57        6   
Bristol_Bay_1026983                  Bristol_Bay       3913.58        7   
Bristol_Bay_1027852                  Bristol_Bay        118.27        5   
Bristol_Bay_1028212                  Bristol_Bay        146.48        5   
Bristol_Bay_1028322                  Bristol_Bay        248.78        5   
Bristol_Bay_1029732                  Bristol_Bay        338.19        5   
Bristol_Bay_1029872                  Bristol_Bay        218.28        5   
Bristol_Bay_1030072                  Bristol_Bay        192.79        5   
Bristol_Bay_1030462                  Bristol_Bay         98.69        4   
Bristol_Bay_1030642                  Bristol_Bay        193.11        5   
Bristol_Bay_1031022                  Bristol_Bay       1445.60        6   
Bristol_Bay_2019750                  Bristol_Bay        402.36        6   
Bristol_Bay_2020120                  Bristol_Bay        512.37        6   
Bristol_Bay_2040341                  Bristol_Bay        932.96        7   
Bristol_Bay_2041261                  Bristol_Bay       1136.88     

In [54]:
# Export merged dataframe to csv
import os
#outdir = r"C:\Users\dwmerrigan\Documents\GitHub\AKSSF\data_preparation\sensitivity_drivers"
fin_csv_out = os.path.join(outdir,'AKSSF_AwcHuc12s_strwtd_cv.csv')
final_df.to_csv(fin_csv_out, encoding = 'utf-8')
print('Export all watershed and stream covariates dataframe to csv complete')


Export all watershed and stream covariates dataframe to csv complete


#  Discharge Merrit
Becky will put flow networks on T: